# Watershed metrics for all Huc12 subwatersheds that intersect AWC recorded streams
Iterate over AKSSF regions and identify all HUC12 sub-watersheds that intersect an AWC recorded stream. Identify the downstream-most/outlet catchment for each Huc12 from this pool and convert the polygon to INSIDE centroid point.  Calculate the distance to coastline as the straight line distance in Km from centroid point to NHD recorded coastline and export this as a feature class/table.  Next use the outlet catchments unique identifier to query the appropriate dataset and build watersheds for each outlet catchment.  Calculate watershed metrics listed in the covariate section and export final merged csv using the catchment unique identifier field "cat_ID_con" to link the metric back to the source catchment/HUC12.  Merge watersheds together and use to calculate covariates.
## Covariates
Covariates needed for prediction on AWC-HUC12 outlets are as follows:
### Summer Precipitation
To be calculated in R using the outlet catchment centroid point feature class exported during outlet identification process.
### Watershed Slope Metrics
Regional Slope grids created in AKSSF_merge_grids.ipynb script.
Run zonal statistics on slope grid using merged watershed as zone feature.
Field names and descriptions:
* **awc_huc12s_wtd_slope_mn = mean watershed slope**
* **awc_huc12s_wtd_slope_min = min watershed slope**
* **awc_huc12s_wtd_slope_max = max watershed slope**
* **awc_huc12s_wtd_slope_sd (or cv) = standard deviation of watershed slope**
### Watershed Percent North Aspect
Regional North grids created in AKSSF_merge_grids.ipynb scripts.
North = aspects from 315-45 degrees and calculate the percentage of land area facing north for each watershed. Run tabulate area on north grid using merged watershed as zone feature and calculate percentage from area.
Field names and descriptions:
* **awc_huc12s_north_wtd = percent watershed with north aspect**
### Watershed Percent Lake Cover
Lakes feature classes for each network datatype (NHDPlus vs TauDEM) stored in AKSSF hydrography database on the T:
Calculate percentage of watershed that is covered by lakes/ponds using tabulate interesection between lake features and watersheds.
Field names and descriptions:
* **awc_huc12s_wtd_lake_per = percent watershed covered by lakes**
### Watershed Percent Glacier Cover
Use input glacier fc (from previous covariate calculations) stored in regional gdbs an calculate percent of watershed with glacial coverage using tabulate intersection between lake features and watersheds.
Field names and descriptions:
* **awc_huc12s_wtd_glac_per = percent watershed covered by glaciers**
### Watershed LCLD
LCLD rasters created in AKSSF_MODIS_lcld_ipynb.
Iterate over LCLD input rasters to produce yearly means for watersheds using zonal statistics.
Field names and descriptions:
* **awc_huc12s_wtd_lcld_mn_YYYY = mean lcld**


## Import modules
Set initial environments and import modules
Print system paths

In [1]:
import os, arcpy, sys,datetime, traceback

arcpy.env.overwriteOutput = True
sr = arcpy.SpatialReference(3338)  #'NAD_1983_Alaska_Albers'
arcpy.env.outputCoordinateSystem = sr
print(f'Date: {datetime.datetime.now()}')
print('imports complete')
print(f'{("-"*100)}')
print(f'sys paths {sys.path}')
print(f'{("-"*100)}')
print(f'Python Environment set to - {sys.base_exec_prefix}')
print(f'{("-"*100)}')
print (datetime.datetime.now())
outdir = os.path.dirname(os.getcwd())
print(f'CSV table output directory set to {outdir}')

Date: 2023-03-01 10:29:02.079657
imports complete
----------------------------------------------------------------------------------------------------
sys paths ['C:\\Users\\dwmerrigan\\Documents\\GitHub\\AKSSF\\data_preparation\\sensitivity_drivers\\landcover', 'C:\\Program Files\\ArcGIS\\Pro\\Resources\\ArcPy', 'C:\\Users\\dwmerrigan\\Documents\\GitHub\\AKSSF', 'C:\\Program Files\\ArcGIS\\Pro\\bin\\Python\\envs\\arcgispro-py3\\python39.zip', 'C:\\Program Files\\ArcGIS\\Pro\\bin\\Python\\envs\\arcgispro-py3\\DLLs', 'C:\\Program Files\\ArcGIS\\Pro\\bin\\Python\\envs\\arcgispro-py3\\lib', 'C:\\Program Files\\ArcGIS\\Pro\\bin\\Python\\envs\\arcgispro-py3', '', 'C:\\Program Files\\ArcGIS\\Pro\\bin\\Python\\envs\\arcgispro-py3\\lib\\site-packages', 'C:\\Program Files\\ArcGIS\\Pro\\bin', 'C:\\Program Files\\ArcGIS\\Pro\\Resources\\ArcToolbox\\Scripts', 'C:\\Program Files\\ArcGIS\\Pro\\bin\\Python\\envs\\arcgispro-py3\\lib\\site-packages\\Babel-2.11.0-py3.9.egg', 'C:\\Program Files\\ArcGIS\\

## Functions
Define any functions that will be used

In [2]:
# Function to add key, value pairs to dictionary
def append_value(dict_obj, key, value):
    # Check if key exist in dict or not
    if key in dict_obj:
        # Key exist in dict.
        # Check if type of value of key is list or not
        if not isinstance(dict_obj[key], list):
            # If type is not list then make it list
            dict_obj[key] = [dict_obj[key]]
        # Append the value in list
        dict_obj[key].append(value)
    else:
        # As key is not in dict,
        # so, add key-value pair
        dict_obj[key] = value
# Function to remove parenthesis from user inputs
def replace_all(userinput, dic):
    for i, j in dic.items():
        userinput = userinput.replace(i, j)
    return userinput

# Getnull rows from numpy array
def getnull(cat_ID_con):
    nullRows = []
    nullRows.append(cat_ID_con)
    return True

#Generate unique column names
def uniquify(df_final):
    seen = set()
    for item in df_final:
        fudge = 1
        newitem = item
        while newitem in seen:
            fudge += 1
            newitem = "{}_{}".format(item, fudge)
        yield newitem
        seen.add(newitem)

## Section 1
### Set input datasets, output locations, and scratch workspaces
User to input paths for necessary input data and output locations
Scratch workspaces and output workspaces will be automatically created if they do not already exist.

In [3]:
# Get user inputs
# Used to format user inputs
inputDict = {"'":"",'"':""}

# Specify path to nhdPlus lakes
while True:
    try:
        nhdlakesinput = replace_all((input('Input path to NHDPlus lakes feature class.\nHydrography database on T: has copy\nLeave blank and hit enter to use the default location.\nDefault = D:\\Basedata\\AKSSF_Basedata\\AKSSF_Basedata.gdb\\AKSSF_NHDPlus_LakePond_alb') or 'D:\\Basedata\\AKSSF_Basedata\\AKSSF_Basedata.gdb\\AKSSF_NHDPlus_LakePond_alb'),inputDict)
        if not arcpy.Exists(nhdlakesinput):
            print('Path specified does not exist!\nPlease re-enter a valid path')
            continue
        else:
            nhd_lakes_fc = nhdlakesinput
            break
    except KeyboardInterrupt:
        print('interrupted!')
        sys.exit()

print(f'NHDPlus lakes set to {nhd_lakes_fc}\n {"-"*100}')

# Specify path to nhd lakes for tau regions
while True:
    try:
        taulakesinput = replace_all((input('Input path to NHD_H_Alaska_State_GDB lakes feature class.\nHydrography database on T: has copy\nLeave blank and hit enter to use the default location.\nDefault = D:\\Basedata\\AKSSF_Basedata\\AKSSF_Basedata.gdb\\AKSSF_NHD_LakesPonds_alb') or 'D:\\Basedata\\AKSSF_Basedata\\AKSSF_Basedata.gdb\\AKSSF_NHD_LakesPonds_alb'),inputDict)
        if not arcpy.Exists(taulakesinput):
            print('Path specified does not exist!\nPlease re-enter a valid path')
            continue
        else:
            tau_lakes_fc = taulakesinput
            break
    except KeyboardInterrupt:
        print('interrupted!')
        sys.exit()
print(f'NHD_H_Alaska lakes for TauDEM regions set to {nhd_lakes_fc}\n {"-"*100}')

# Specify path to coastline fc
while True:
    try:
        coastinput = replace_all((input('Input path to coastline fc.\nHydrography database on T: has copy\nLeave blank and hit enter to use the default location.\nDefault = D:\\Basedata\\AKSSF_Basedata\\AKSSF_Basedata.gdb\\NHD_H_Alaska_Coastline_alb') or 'D:\\Basedata\\AKSSF_Basedata\\AKSSF_Basedata.gdb\\NHD_H_Alaska_Coastline_alb'),inputDict)
        if not arcpy.Exists(coastinput):
            print('Path specified does not exist!\nPlease re-enter a valid path')
            continue
        else:
            coast = coastinput
            break
    except KeyboardInterrupt:
        print('interrupted!')
        sys.exit()
print(f'Coastline for all regions set to {coast}\n {"-"*100}')

# Specify path to AKSSF parent directory
while True:
    try:
        datadirinput = replace_all((input('Input AKSSF parent directory containing regional sub-folders.\nLeave blank and hit enter to use the default location.\nDefault = D:\\GIS\\AKSSF\\') or 'D:\\GIS\\AKSSF'),inputDict)
        if not arcpy.Exists(datadirinput):
            print('Path specified does not exist!\nPlease re-enter a valid path')
            continue
        else:
            data_dir = datadirinput
            break
    except KeyboardInterrupt:
        print('interrupted!')
        sys.exit()

print(f'AKSSF parent directory set to {data_dir}\n {"-"*100}')

# Specify path to AWC events fc
while True:
    try:
        awceventsinput = replace_all((input('Input path to awc events feature class or shapefile.\nLeave blank and hit enter to use the default location.\nDefault = D:\\GIS\\AKSSF_land_met\\AKSSF_land_met.gdb\\awcEventArcs_Intersect_H12sDiss') or "D:\\GIS\\AKSSF_land_met\\AKSSF_land_met.gdb\\awcEventArcs_Intersect_H12sDiss"), inputDict)
        if not arcpy.Exists(awceventsinput):
            print('Path specified does not exist!\nPlease re-enter a valid path')
            continue
        else:
            awc_events = awceventsinput
            break
    except KeyboardInterrupt:
        print('interrupted!')
        sys.exit()
print(f'AWC events feature class set to {awc_events}\n {"-"*100}')

# Enter output destination  - to create working folders and gdbs
while True:
    try:
        temppathinput = replace_all((input('Input path to create working folders.\nLeave blank and hit enter to use the default location.\nDefault = D:\\GIS\\') or 'D:\\GIS\\'),inputDict)
        if not arcpy.Exists(temppathinput):
            print('Path specified does not exist!\nPlease re-enter a valid path')
            continue
        else:
            temp_path = temppathinput
            print(f'Output locations will be created at {temp_path}\n {"-"*100}')
            break
    except KeyboardInterrupt:
        print('interrupted!')
        sys.exit()


# Path to lcld rasters
# Enter output destination  - to create working folders and gdbs
while True:
    try:
        lcldfolinput = replace_all((input('Input path to LCLD raster parent folder.\nLeave blank and hit enter to use the default location.\nDefault = D:\\Basedata\\LCLD_rasters_archive\\') or 'D:\\Basedata\\LCLD_rasters_archive'),inputDict)
        if not arcpy.Exists(lcldfolinput):
            print('Path specified does not exist!\nPlease re-enter a valid path')
            continue
        else:
            lcld_folder = lcldfolinput
            print(f'LCLD subfolders located at {lcld_folder}\n {"-"*100}')
            break
    except KeyboardInterrupt:
        print('interrupted!')
        sys.exit()

# Threshold in meters to use as cutoff for selecting awcEvents polylines
while True:
    try:
        awcthreshinput = (input('Input minimum awc stream length in meters to use as threshold for selection.\nLeave blank and hit enter to use the default value of 500 meters.\nDefault = 500') or 500)
        if not type(awcthreshinput) == int or type(awcthreshinput) == float:
            print('Please enter a valid number')
            continue
        else:
            awcthresh = awcthreshinput
            print(f'Only stream segments greater than {awcthresh} meters will be used for selection\n {"-"*100}')
            break
    except KeyboardInterrupt:
        print('interrupted!')
        sys.exit()
# Threshold in meters to use as cutoff for selecting awcEvents polylines
while True:
    try:
        dirname = (input('Input name of directory being created for outputs'))
        if not dirname:
            print(f'Must not be blank\n {"-"*100}')
            break
        else:
            dirname = dirname
            tempgdbname = dirname + '.gdb'
            temp_dir = os.path.join(temp_path, dirname)
            outdir = temp_dir
            outcheck = os.path.join(temp_dir, tempgdbname)
            print(f'output directory set to {temp_dir} output gdb = {outcheck}' )
            break
    except KeyboardInterrupt:
        print('interrupted!')
        sys.exit()

# Create temporary working gdb
if not arcpy.Exists(temp_dir):
    os.makedirs(temp_dir)
else:
    print(f'Working Folder already created {temp_dir}\n {"-"*100}')

if arcpy.Exists(outcheck):
    print (f'Output location already exists {outcheck}\n {"-"*100}')
    outgdb = outcheck
if not arcpy.Exists(outcheck):
    print(f'Creating output GDB\n {"-"*100}')
    tempgdb = arcpy.CreateFileGDB_management(temp_dir,tempgdbname)
    print (f'Output geodatabase created at {outcheck}\n {"-"*100}')
    outgdb = tempgdb.getOutput(0)


NHDPlus lakes set to D:\Basedata\AKSSF_Basedata\AKSSF_Basedata.gdb\AKSSF_NHDPlus_LakePond_alb
 ----------------------------------------------------------------------------------------------------
NHD_H_Alaska lakes for TauDEM regions set to D:\Basedata\AKSSF_Basedata\AKSSF_Basedata.gdb\AKSSF_NHDPlus_LakePond_alb
 ----------------------------------------------------------------------------------------------------
Coastline for all regions set to D:\Basedata\AKSSF_Basedata\AKSSF_Basedata.gdb\NHD_H_Alaska_Coastline_alb
 ----------------------------------------------------------------------------------------------------
AKSSF parent directory set to D:\GIS\AKSSF
 ----------------------------------------------------------------------------------------------------
AWC events feature class set to D:\GIS\AKSSF_land_met\AKSSF_land_met.gdb\awcEventArcs_Intersect_H12sDiss
 ----------------------------------------------------------------------------------------------------
Output locations will be

## Section 1.1
### Set and create local copies of additional input data


In [4]:

import arcpy
arcpy.env.overwriteOutput = True
sr = arcpy.SpatialReference(3338)  #'NAD_1983_Alaska_Albers'
arcpy.env.outputCoordinateSystem = sr

nhdplusfol = []
tahuc12=[]

# Create and set HUC12 data if it does not already exist
nhdplushucs = os.path.join(outgdb, 'NHDPlusHUC12')
tauhucs = os.path.join(outgdb, 'NHD_H_HUC12')

if not arcpy.Exists(tauhucs):
    print(f'Huc12 data for Tau Regions not yet created')
    #Enter path to WBDHU12 from NHD_H gdb
    while True:
        try:
            tauhuc12input = replace_all((input('Input path to source WBDHU12 for state of Alaska.\nLeave blank and hit enter to use the default location.\nDefault = D:\\Basedata\\NHD_H_Alaska_State_GDB.gdb\\WBD\\WBDHU12') or 'D:\\Basedata\\NHD_H_Alaska_State_GDB.gdb\\WBD\\WBDHU12'),inputDict)
            if not arcpy.Exists(tauhuc12input):
                print('Path specified does not exist!\nPlease re-enter a valid path')
                continue
            else:
                tauhuc12 = tauhuc12input
                arcpy.CopyFeatures_management(tauhuc12,tauhucs)
                print(f'WBD Huc12  copied to {tauhucs}\n {"-"*100}')
                break
        except KeyboardInterrupt:
            print('interrupted!')
            sys.exit()

else:
    print(f'Tau Region Hucs {tauhucs} located and exists = {arcpy.Exists(tauhucs)}')
    tauhucs = os.path.join(outgdb, 'NHD_H_HUC12')

if not arcpy.Exists(nhdplushucs):
    print(f'Huc12 data for NHDPlus Regions not yet created')
    #Enter NHDplus data folder
    while True:
        try:
            nhdplusfolinput = replace_all((input('Input path to source NHDPlus parent folder.\nLeave blank and hit enter to use the default location.\nDefault = D:\\Basedata\\NHDPlus') or 'D:\\Basedata\\NHDPlus'),inputDict)
            if not arcpy.Exists(nhdplusfolinput):
                print('Path specified does not exist!\nPlease re-enter a valid path')
                continue
            else:
                nhdplusfol = nhdplusfolinput
                print(f'NHD HUC12 will be copied to {nhdplushucs}\n {"-"*100}')
                hucs = []
                walk = arcpy.da.Walk(nhdplusfol, datatype="FeatureClass", type="Polygon")

                for dirpath, dirnames, filenames in walk:
                    for filename in filenames:
                        if filename == 'WBDHU12':
                            hucs.append(os.path.join(dirpath, filename))
                arcpy.Merge_management(hucs,nhdplushucs,'','ADD_SOURCE_INFO')
                break
        except KeyboardInterrupt:
            print('interrupted!')
            sys.exit()
else:
    print(f'NHDPlus Hucs {nhdplushucs} located and exists = {arcpy.Exists(nhdplushucs)}')
    nhdplushucs = os.path.join(outgdb, 'NHDPlusHUC12')



Huc12 data for Tau Regions not yet created
WBD Huc12  copied to D:\GIS\outputs_2023\outputs_2023.gdb\NHD_H_HUC12
 ----------------------------------------------------------------------------------------------------
Huc12 data for NHDPlus Regions not yet created
NHD HUC12 will be copied to D:\GIS\outputs_2023\outputs_2023.gdb\NHDPlusHUC12
 ----------------------------------------------------------------------------------------------------


## Section 2
## Identify outlet catchments by region
Identify downstream-most catchment for each Huc 12
 * Select by location and select catchment with most us contributing area
    * NHDPlus
        * Use update cursor to join TotalDrainageAreaSqKm from vaa table to catchment
        * Find max value from selection and save as outlet catchment for that HUC12
    * TauDEM
        * DSContArea - Drainage area at the downstream end of the link. Generally this is one grid cell upstream of the downstream end because the drainage area at the downstream end grid cell includes the area of the stream being joined.
 * Generate Centroid point and append to centroid dataset
    * Retain cat_id and Huc12-id
 * Append to HUC12 catchment dataset
 * **NOTE- Since the HUC12 Boundaries do not align perfectly with TauDEM (and at least one NHDPlus copper river: 190201040109) catchments, the outlet catchment that is identified may be further upstream than we would like.**


## Set Qc dictionaries and lists if necessary
Initially flagged for review if length of awc in HUC12 was < threshold of 500 meters to identify HUCS that may have been chosen in error due to differences between AWC streams and NHDPlus/Tau Streams and Catchments


In [5]:
# Change outdir to temp_dir if QC otherwise comment out
#outdir = temp_dir
print(f'CSV table output directory set to {outdir}')

# key = cat_ID_con:vals [new cat_ID_con (may stay the same or pick a new catchment that best represents the HUC12), AWCCODE,HUC12, ReviewCode(1 - Keep but change awc relation, 2 - choose new catchment and re-run watersheds, 3 - drop, 4 - Additional Review), 0 - leave as is]
awcQcDict = {}
# Update reviewDict to match qcDict from sp_ls script after initial/subsequent reviews (Only wrong catchments and drops)
# reviewDict = {'Cook_Inlet_75000200005366': ['Cook_Inlet_75000200005366','NA','190205051307',3],
#               'Copper_River_75019700004288':['Copper_River_75019700004288','NA','190201031502',3],
#               'Cook_Inlet_75004400008887': ['Cook_Inlet_75004400008887','NA','190203021908',3],
#               'Copper_River_75003900043422': ['Copper_River_75003900043422','NA','190201041710',3],
#               'Copper_River_75003900033530':['Copper_River_75003900033530','NA','190201041708',3],
#               'Cook_Inlet_75004300002143': ['Cook_Inlet_75004300002143','NA','190203010803',3],
#               'Cook_Inlet_75000100000043': ['Cook_Inlet_75000100000043','NA','190204010702',3],
#               'Cook_Inlet_75000100002150': ['Cook_Inlet_75000100002150','NA','190204010808',3],
#               'Copper_River_75003900029096': ['Copper_River_75003900029096','NA','190201042002',3],
#               'Prince_William_Sound_46513': ['Prince_William_Sound_46513','NA','190202010200',3],
#               'Cook_Inlet_75004200012620': ['Cook_Inlet_75004200001574', '232-21-10240', '190202021202', 2],
#               'Cook_Inlet_75004200000726': ['Cook_Inlet_75004200000726', '226-50-16242', '190202020101', 0],
#               'Cook_Inlet_75004200002407': ['Cook_Inlet_75004200007843', '232-40-10254', '190202020704', 2],
#               'Cook_Inlet_75004300006726': ['Cook_Inlet_75004300006726', '241-15-10370', '190203011111', 0],
#               'Cook_Inlet_75004300005625': ['Cook_Inlet_75004300005625', '241-13-10760', '190203010805', 0],
#               'Cook_Inlet_75004300001512': ['Cook_Inlet_75004300001512', 'NA', '190203010801', 3],
#               'Cook_Inlet_75004300000779': ['Cook_Inlet_75004300000779', 'NA', '190203010806', 3],
#               'Cook_Inlet_75004400008539': ['Cook_Inlet_75004400008539', '244-30-10010-2225-3056', '190203021002', 3],
#               'Cook_Inlet_75004400009109': ['Cook_Inlet_75004400009109', 'NA', '190203022005', 3],
#               'Cook_Inlet_75004400001134': ['Cook_Inlet_75004400001134', '247-60-10180', '190203020704', 0],
#               'Cook_Inlet_75004400002718': ['Cook_Inlet_75004400002718', '247-60-10200', '190203020302', 3],
#               'Cook_Inlet_75000100002639': ['Cook_Inlet_75000100002639', 'NA', '190204010403', 3],
#               'Cook_Inlet_75000100004624': ['Cook_Inlet_75000100004624', 'NA', '190204010401', 3],
#               'Cook_Inlet_75000400015018': ['Cook_Inlet_75000400015018', '247-50-10200-2160-3070', '190204020903', 0],
#               'Cook_Inlet_75000700037019': ['Cook_Inlet_75000700037019', 'NA', '190205011609', 3],
#               'Cook_Inlet_75000500009993': ['Cook_Inlet_75000500009993', '247-41-10200-2381-3260-4020', '190205020203',
#                                             0],
#               'Cook_Inlet_75000500015568': ['Cook_Inlet_75000500015568', 'NA', '190205020309', 3],
#               'Cook_Inlet_75000500006160': ['Cook_Inlet_75000500006160', 'NA', '190205020703', 3],
#               'Cook_Inlet_75000500012136': ['Cook_Inlet_75000500012136', '247-41-10200-2381-3161-4151', '190205020902',
#                                             0],
#               'Cook_Inlet_75000500009986': ['Cook_Inlet_75000500009986', 'NA', '190205020410', 3],
#               'Cook_Inlet_75000300007777': ['Cook_Inlet_75000300007777', 'NA', '190205030305', 3],
#               'Cook_Inlet_75000300028089': ['Cook_Inlet_75000300028089', '247-41-10200-2370-3393', '190205030106', 0],
#               'Cook_Inlet_75000600014946': ['Cook_Inlet_75000600014946', 'NA', '190205041801', 3],
#               'Cook_Inlet_75000600031834': ['Cook_Inlet_75000600031834', '247-41-10200-2053-3229', '190205040502', 0],
#               'Cook_Inlet_75000600020425': ['Cook_Inlet_75000600020425', 'NA', '190205041101', 3],
#               'Cook_Inlet_75000200017518': ['Cook_Inlet_75000200017518', '247-41-10100-2387', '190205051201', 0],
#               'Cook_Inlet_75000200015292': ['Cook_Inlet_75000200015292', 'NA', '190205051103', 3],
#               'Cook_Inlet_75005300000657': ['Cook_Inlet_75005300000657', 'NA', '190206010902', 3],
#               'Cook_Inlet_75005400007190': ['Cook_Inlet_75005400007190', '243-20-10020', '190206020806', 0],
#               'Cook_Inlet_75005400045669': ['Cook_Inlet_75005400045669', 'NA', '190206020602', 3],
#               'Cook_Inlet_75005400028381': ['Cook_Inlet_75005400028381', 'NA', '190206020202', 3],
#               'Cook_Inlet_75005400041329': ['Cook_Inlet_75005400041329', '245-40-10020-2027', '190206020102', 0],
#               'Cook_Inlet_75005400023457': ['Cook_Inlet_75005400023457', 'NA', '190206020605', 3],
#               'Cook_Inlet_75005400047280': ['Cook_Inlet_75005400047280', '245-40-10020-2027', '190206020101', 3],
#               'Copper_River_75019800002596': ['Copper_River_75019800002596', 'NA', '190201010304', 3],
#               'Copper_River_75019800019137': ['Copper_River_75019800019137', 'NA', '190201010702', 3],
#               'Copper_River_75019800020572': ['Copper_River_75019800020572', 'NA', '190201011206', 3],
#               'Copper_River_75019800000761': ['Copper_River_75019800000761', 'NA', '190201010205', 3],
#               'Copper_River_75019600178680': ['Copper_River_75019600178680', 'NA', '190201020102', 3],
#               'Copper_River_75019600169875': ['Copper_River_75019600169875', '212-20-10080-2461-3091-4042',
#                                               '190201023302', 0],
#               'Copper_River_75019600151382': ['Copper_River_75019600151382', '212-20-10080-2461-3091-4049',
#                                               '190201020304', 0],
#               'Copper_River_75019600201122': ['Copper_River_75019600201122', 'NA', '190201023104', 3],
#               'Copper_River_75019600145942': ['Copper_River_75019600145942', 'NA', '190201020604', 3],
#               'Copper_River_75019600145695': ['Copper_River_75019600145695', '212-20-10080-2461-3044', '190201020605',
#                                               0],
#               'Copper_River_75019600198826': ['Copper_River_75019600198826', '212-20-10080-2440', '190201023405', 0],
#               'Copper_River_75019600200372': ['Copper_River_75019600200372', '212-20-10080-2431-3022', '190201021506',
#                                               0],
#               'Copper_River_75019600176914': ['Copper_River_75019600176914', '212-20-10080-2431', '190201021304', 0],
#               'Copper_River_75019600120847': ['Copper_River_75019600120847', '212-20-10080-2350', '190201022503', 0],
#               'Copper_River_75019600119614': ['Copper_River_75019600119614', '212-20-10080-2401-3100', '190201022002',
#                                               3],
#               'Copper_River_75019600130736': ['Copper_River_75019600130736', 'NA', '190201021903', 3],
#               'Copper_River_75019600198047': ['Copper_River_75019600198047', 'NA', '190201021804', 3],
#               'Copper_River_75019700003218': ['Copper_River_75019700003218', '212-20-10080-2300-3402', '190201032703',
#                                               0],
#               'Copper_River_75019700000617': ['Copper_River_75019700000617', 'NA', '190201032305', 3],
#               'Copper_River_75019700000923': ['Copper_River_75019700000923', 'NA', '190201032505', 3],
#               'Copper_River_75019700003395': ['Copper_River_75019700003395', 'NA', '190201031406', 3],
#               'Copper_River_75003900048794': ['Copper_River_75003900048794', '212-20-10080-2295', '190201040101', 0],
#               'Copper_River_75003900056636': ['Copper_River_75003900056636', '212-20-10080-2281', '190201040103', 0],
#               'Copper_River_75003900048464': ['Copper_River_75003900048464', '212-20-10080-2193', '190201040403', 0],
#               'Copper_River_75003900073776': ['Copper_River_75003900073776', 'NA', '190201040511', 3],
#               'Copper_River_75003900066004': ['Copper_River_75003900066004', 'NA', '190201041201', 3],
#               'Copper_River_75003900054248': ['Copper_River_75003900054248', 'NA', '190201041606', 3],
#               'Copper_River_75003900029086': ['Copper_River_75003900029086', 'NA', '190201042003', 3],
#               'Prince_William_Sound_13227': ['Prince_William_Sound_13227', '226-50-16436', '190202030302', 0],
#               'Prince_William_Sound_22134': ['Prince_William_Sound_27303', '222-30-12940', '190202030201', 2],
#               'Prince_William_Sound_23854': ['Prince_William_Sound_24654', '222-40-12960', '190202030202', 2],
#               'Prince_William_Sound_26334': ['Prince_William_Sound_26334', '224-20-13024', '190202011606', 0],
#               'Prince_William_Sound_31916': ['Prince_William_Sound_33036', '226-20-16170', '190202012506', 2],
#               'Prince_William_Sound_33616': ['Prince_William_Sound_33616', 'NA', '190202012505', 3],
#               'Prince_William_Sound_34455': ['Prince_William_Sound_32015', '226-20-16940', '190202030208', 2],
#               'Prince_William_Sound_43535': ['Prince_William_Sound_685', '224-40-14920', '190202012307', 2],
#               'Prince_William_Sound_74042': ['Prince_William_Sound_74042', '221-50-11150', '190202011108', 0],
#               'Prince_William_Sound_79972': ['Prince_William_Sound_79972', '222-30-12840', '190202011601', 0],
#               'Prince_William_Sound_87851': ['Prince_William_Sound_87851', '221-60-11360', '190202011101', 0],
#               'Prince_William_Sound_91751': ['Prince_William_Sound_91751', 'NA', '190202010905', 3],
#               'Prince_William_Sound_76692': ['Prince_William_Sound_71142', '221-50-11170', '190202011109', 2],
#               'Cook_Inlet_75004200001726': ['Cook_Inlet_75004200002199', '231-30-10080', '190202020508', 2],
#               'Cook_Inlet_75004200001298': ['Cook_Inlet_75004200000437', '232-40-10190', '190202020705', 2],
#               'Cook_Inlet_75004200006640': ['Cook_Inlet_75004200008847', '242-41-10380', '190202021303', 2],
#               'Cook_Inlet_75004200009218': ['Cook_Inlet_75004200000848', '232-30-10247', '190202020802', 2],
#               'Cook_Inlet_75004200013577': ['Cook_Inlet_75004200001003', '232-23-10100', '190202020902', 2],
#               'Cook_Inlet_75004200000478': ['Cook_Inlet_75004200005907', '231-30-10160', '190202020510', 2],
#               'Cook_Inlet_75004200001167': ['Cook_Inlet_75004200003399', '232-10-10330', '190202021103', 2],
#               'Cook_Inlet_75004300007319': ['Cook_Inlet_75004300007473', '241-12-10100', '190203010807', 2],
#
#               'Cook_Inlet_75000400029059': ['Cook_Inlet_75000400033841', '247-50-10200-2081-3025', '190204021206', 2],
#               'Cook_Inlet_75000500006404': ['Cook_Inlet_75000500002272', '247-41-10200-2381-3161-4080-5001',
#                                             '190205020806', 2],
#               'Cook_Inlet_75000300026273': ['Cook_Inlet_75000300022808', '247-41-10200-2370-3297', '190205030601', 2],
#               'Cook_Inlet_75000300000174': ['Cook_Inlet_75000300021956', '247-41-10200-2370', '190205030607', 2],
#               'Cook_Inlet_75000600015375': ['Cook_Inlet_75000600040122', '247-41-10200-2053-3220', '190205040805', 2],
#               'Cook_Inlet_75000600018321': ['Cook_Inlet_75000600018460', '247-41-10200-2053-3205-4099', '190205041501',
#                                             2],
#               'Cook_Inlet_75000600026866': ['Cook_Inlet_75000600006507', '247-41-10200-2053-3229-4200', '190205040503',
#                                             2],
#               'Cook_Inlet_75000600009692': ['Cook_Inlet_75000600025058', '247-41-10200-2053', '190205040808', 2],
#               'Cook_Inlet_75000200008552': ['Cook_Inlet_75000200005953', '247-41-10200-2130-3020', '190205050504', 2],
#               'Cook_Inlet_75000200002996': ['Cook_Inlet_75000200018317', '247-41-10200-2081-3100-4136', '190205050705',
#                                             2],
#               'Cook_Inlet_75000200003487': ['Cook_Inlet_75000200018781', '247-41-10200', '190205050305', 2],
#               'Cook_Inlet_75000200003483': ['Cook_Inlet_75000200008607', '247-41-10200-2250', '190205050105', 2],
#               'Cook_Inlet_75000200012956': ['Cook_Inlet_75000200000235', '247-41-10200', '190205051306', 2],
#               'Cook_Inlet_75005300003320': ['Cook_Inlet_75005300007002', '247-30-10090-2150', '190206010304', 2],
#               'Cook_Inlet_75005300018781': ['Cook_Inlet_75005300022592', '247-30-10090-2151', '190206010206', 2],
#               'Cook_Inlet_75005400022563': ['Cook_Inlet_75005400034611', '245-30-10084', '190206020308', 2],
#               'Cook_Inlet_75005400019698': ['Cook_Inlet_75005400008084', '243-50-10020', '190206021203', 2],
#               'Cook_Inlet_75005400000004': ['Cook_Inlet_75005400011026', '245-20-10230', '190206020506', 2],
#               'Copper_River_75019600174661': ['Copper_River_75019600181826', '212-20-10080-2401', '190201021805', 2],
#               'Copper_River_75019600198622': ['Copper_River_75019600133538', '212-20-10080-2331', '190201023602', 2],
#               'Copper_River_75003900024361': ['Copper_River_75003900057807', '212-20-10080-2100-3113', '190201040907',
#                                               2],
#               'Copper_River_75003900070258': ['Copper_River_75003900034185', '212-20-10080-2159-3021', '190201040509',
#                                               2],
#               'Copper_River_75003900008591': ['Copper_River_75003900084672', '212-20-10080-2100-3089', '190201040910',
#                                               2],
#               'Copper_River_75003900051393': ['Copper_River_75003900084267', '212-20-10080-2021', '190201041702', 2],
#               'Copper_River_75003900055093': ['Copper_River_75003900023613', '228-20-18420', '190201041805', 2],
#               'Copper_River_75003900054944': ['Copper_River_75003900054448', '228-70-10500', '190201041807', 2],
#               'Prince_William_Sound_18747': ['Prince_William_Sound_18967', '227-30-17780', '190202030702', 2],
#               'Prince_William_Sound_27856': ['Prince_William_Sound_19416', '226-40-16851', '190202030209', 2],
#               'Prince_William_Sound_30084': ['Prince_William_Sound_29704', '224-10-14540', '190202012104', 2],
#               'Prince_William_Sound_33106': ['Prince_William_Sound_16467', '226-50-16154', '190202030503', 2],
#               'Prince_William_Sound_42005': ['Prince_William_Sound_39255', '224-40-14904', '190202012306', 2],
#               'Prince_William_Sound_42595': ['Prince_William_Sound_41025', '224-40-14900', '190202012310', 2],
#               'Prince_William_Sound_43085': ['Prince_William_Sound_40635', '225-30-15070', '190202012509', 2],
#               'Prince_William_Sound_43255': ['Prince_William_Sound_37935', '226-20-16010', '190202012508', 2],
#               'Prince_William_Sound_44273': ['Prince_William_Sound_35343', '223-40-13390', '190202011605', 2],
#               'Prince_William_Sound_44605': ['Prince_William_Sound_35075', '226-20-16950', '190202030207', 2],
#               'Prince_William_Sound_45925': ['Prince_William_Sound_28734', '224-40-14860', '190202012304', 2],
#               'Prince_William_Sound_46613': ['Prince_William_Sound_36553', '224-10-14510', '190202012001', 2],
#               'Prince_William_Sound_46623': ['Prince_William_Sound_34993', '224-10-14500', '190202012003', 2],
#               'Prince_William_Sound_70762': ['Prince_William_Sound_61812', '222-10-12030', '190202011308', 2],
#               'Prince_William_Sound_75002': ['Prince_William_Sound_60732', '223-30-13180', '190202011805', 2],
#               'Prince_William_Sound_77992': ['Prince_William_Sound_75842', '224-10-14020', '190202011906', 2],
#               'Prince_William_Sound_80112': ['Prince_William_Sound_78912', '222-10-12040', '190202011307', 2],
#               'Prince_William_Sound_84641': ['Prince_William_Sound_72242', '222-20-12640', '190202011505', 2],
#               'Prince_William_Sound_89681': ['Prince_William_Sound_75151', '221-60-11520', '190202011103', 2],
#               'Cook_Inlet_75004200004105':['Cook_Inlet_75004200000559','226-50-16226','190202020102',2]
#               }

# key = cat_ID_con:vals [new cat_ID_con (may stay the same or pick a new catchment that best represents the HUC12), AWCCODE,HUC12, ReviewCode(1 - Keep but change awc relation, 2 - choose new catchment and re-run watersheds, 3 - drop, 4 - Additional Review), 0 - leave as is]
reviewDict = {

}

awcRelateList = []
newCatList = []
dropList = []
dropHucs = []
addRevList = []
noChangeList = []
newWtdHucs = []
hucNewcatdict = {}


for k,v in reviewDict.items():
    if v[3] == 1:
        awcRelateList.append(k)
        append_value(awcQcDict,k,v[1])
    elif v[3] == 2:
        newCatList.append(k)
        cid = v[0].split('_')[-1]
        append_value(hucNewcatdict,v[2],[v[0],cid])
        newWtdHucs.append(v[2])
    elif v[3] == 3:
        dropList.append(k)
        dropHucs.append(v[2])
    elif v[3] == 4:
        addRevList.append(k)
    elif v[3] == 0:
        noChangeList.append(k)

print (f'{len(awcRelateList)} Hucs need awc relationship changed/added\n{100*"-"}')
print (f'{len(newCatList)} Hucs had wrong catchment assigned and must have new watersheds run\n{100*"-"}')
print (f'{len(dropList)} Hucs should be dropped from the model\n{100*"-"}')
print (f'{len(addRevList)} Hucs need additional review\nHUCS to review:\n{addRevList}\n{100*"-"}')
print (f'{len(noChangeList)} Hucs need no actions\n{100*"-"}')
print(f'AWC QC Dictionary:\n{awcQcDict}')
print(f'HUC to new Catchment dictionary:\n{hucNewcatdict}')


CSV table output directory set to D:\GIS\outputs_2023
0 Hucs need awc relationship changed/added
----------------------------------------------------------------------------------------------------
62 Hucs had wrong catchment assigned and must have new watersheds run
----------------------------------------------------------------------------------------------------
49 Hucs should be dropped from the model
----------------------------------------------------------------------------------------------------
0 Hucs need additional review
HUCS to review:
[]
----------------------------------------------------------------------------------------------------
28 Hucs need no actions
----------------------------------------------------------------------------------------------------
AWC QC Dictionary:
{}
HUC to new Catchment dictionary:
{'190202021202': ['Cook_Inlet_75004200001574', '75004200001574'], '190202020704': ['Cook_Inlet_75004200007843', '75004200007843'], '190202030201': ['Prince_Wil

## Identify Outlet catchments - **IF RUNNING FOR QC, OVERWRITE INPUT 'hucs' WITH 'qcHucs' FROM BLOCK BELOW ELSE COMMENT OUT OR DO NOT RUN NEXT BLOCK**
Cook_Inlet_75000500002272 - This catchment/AWC pairing may need to be dropped.  NHDPlus shows this reach as draining North but AWC has reach connected to two systems from North to South.  So "outlet catchment"

In [6]:
# # Print HUCS that need new watersheds and create new dataset for qc
# nhdplushucs = os.path.join(outgdb, 'NHDPlusHUC12')
# tauhucs = os.path.join(outgdb, 'NHD_H_HUC12')
# hucQcclause = f'"HUC12" IN ({str(newWtdHucs).strip("[]")})'
# print(hucQcclause)
# nhdPlusQcHucs =  arcpy.FeatureClassToFeatureClass_conversion(nhdplushucs,outgdb,'nhdPlusQc_Hucs',hucQcclause)
# print(f'NHD Plus QC HUC12s for Cook Inlet/Copper River {nhdPlusQcHucs} created...')
# tauQcHucs = arcpy.FeatureClassToFeatureClass_conversion(tauhucs,outgdb,'tauQc_Hucs',hucQcclause)
# print(f'NHD_H QC HUC12s for Tau Regions {tauQcHucs} created...')
# tauhucs = tauQcHucs
# nhdplushucs = nhdPlusQcHucs

In [6]:
# Filter out hucs to be dropped prior to runing
nhdplushucs = os.path.join(outgdb, 'NHDPlusHUC12')
tauhucs = os.path.join(outgdb, 'NHD_H_HUC12')
dropclause = f'"HUC12" NOT IN ({str(dropHucs).strip("[]")})'
#print(dropclause)
print(f'{arcpy.GetCount_management(nhdplushucs)} hucs in Nhdplus dataset')
nhdPlusFinalHucs =  arcpy.FeatureClassToFeatureClass_conversion(nhdplushucs,outgdb,'nhdPlusFinal_Hucs',dropclause)
print(f'{arcpy.GetCount_management(nhdPlusFinalHucs)} NHDPlus HUC12s for Cook Inlet/Copper River {nhdPlusFinalHucs} created...')
print(f'{arcpy.GetCount_management(tauhucs)} hucs in NHD_H dataset')
tauFinalHucs = arcpy.FeatureClassToFeatureClass_conversion(tauhucs,outgdb,'tauFinal_Hucs',dropclause)
print(f'{arcpy.GetCount_management(tauFinalHucs)} NHD_H HUC12s for Entire AKSSF Region {tauFinalHucs} created...')
tauhucs = tauFinalHucs
nhdplushucs = nhdPlusFinalHucs

1686 hucs in Nhdplus dataset
1640 NHDPlus HUC12s for Cook Inlet/Copper River D:\GIS\outputs_2023\outputs_2023.gdb\nhdPlusFinal_Hucs created...
15085 hucs in NHD_H dataset
15037 NHD_H HUC12s for Entire AKSSF Region D:\GIS\outputs_2023\outputs_2023.gdb\tauFinal_Hucs created...


In [7]:
import arcpy, time, os, datetime, operator
from math import *
from collections import Counter

arcpy.env.workspace = data_dir
regions = arcpy.ListWorkspaces()

# Lists
flowlineList = [] # List to store regional NHDFlowline_merge
streamsList = [] # List to store regional streams_merge
vaas_lst = [] # List to store regional vaas_merge tables
nhdplusoutlets = [] # List to store NHDPlus HUC12 outlet catchment centroid points
tauoutlets = [] # List to store TauDEM HUC12 outlet catchment centroid points
nhdplusawccatouts = [] # List to store NHDPlus HUC12 outlet catchments
tauawccatouts = [] # List to store TauDEM HUC12 outlet catchments

# Dictionaries
dist2CoastDict = {}
vaaDict = {}
strDict = {}
catsDict = {}
huc12Dict = {}
nhdidDict = {}
tauidDict = {}
tauhuc12Dict = {}
hucreviewList = []

# Separate data by source type
nhdplus_dat = ['Cook_Inlet','Copper_River']
tauDem_dat = ['Bristol_Bay', 'Kodiak', 'Prince_William_Sound']

# Loop through all processing areas
# rois = nhdplus_dat + tauDem_dat

# Or comment above and specify below specific subset
#regions = ['D:\\GIS\\AKSSF\\Cook_Inlet', 'D:\\GIS\\AKSSF\\Copper_River' ,'D:\\GIS\\AKSSF\\Prince_William_Sound']
regions = ['D:\\GIS\\AKSSF\\Bristol_Bay','D:\\GIS\\AKSSF\\Kodiak']
# Start timing function
processStart = time.time()
processStartdt = datetime.datetime.now()
print(f'Begin {datetime.datetime.now()}')
for region in regions:
    upfcs = [] # List to store feature classes to be updated in update cursor
    roi = os.path.basename(region)
    print(roi)
    if roi in nhdplus_dat:
        # Start roi time
        roi_start = time.time()
        hucs = nhdplushucs
        catsList = []
        outletList = []
        print(f'{roi} using data from {region} folder')
        # Set workspace to region folder
        arcpy.env.workspace = region
        gdb = arcpy.ListWorkspaces(workspace_type='FileGDB')
        print(f'GDB {gdb}')
        sourcegdb = gdb[0]
        walk = arcpy.da.Walk(sourcegdb, datatype = ['FeatureClass','Table'])
        for dirpath, dirnames, filenames in walk:
            for filename in filenames:
                if filename == 'cats_merge':
                    cats  = os.path.join(dirpath, filename)
                    append_value(catsDict,roi,cats)
                elif filename == 'NHDFlowline_merge':
                    streamname = roi + '_' + filename
                    streams = os.path.join(outgdb,streamname)
                    if not arcpy.Exists(streams):
                        print(f'Copying {os.path.join(dirpath, filename)} to {outgdb}')
                        arcpy.FeatureClassToFeatureClass_conversion(os.path.join(dirpath,filename),outgdb,streamname)
                    else:
                        print(f'{streams} already created')
                    #upfcs.append(streams)
                    append_value(strDict, roi, streams)
                    flowlineList.append(streams)
                elif filename == 'vaa_merge':
                    vaas = os.path.join(dirpath, filename)
                    append_value(vaaDict, roi, vaas)
                    vaas_lst.append(vaas)

        #Output names and paths
        outletcatsname = roi + '_AwcHuc12_cats_outlets'
        outcatspath = os.path.join(outgdb,outletcatsname)
        outcatspath2 = os.path.join(sourcegdb,'awc_huc12_catchment_outlets')
        outletcatptsname = roi + '_AwcHuc12_cats_outlets_pts'
        outcatptspath = os.path.join(outgdb,outletcatptsname)
        outcatptspath2 = os.path.join(sourcegdb,'awc_huc12_catchment_outlets_pts')

        if not arcpy.Exists(outcatspath):
            # Build Value dictionary to relate NHDPlus id to contributing area
            fields = ['NHDPlusID','TotDASqKm','StreamOrde', 'Slope', 'AreaSqKm', 'ArbolateSu', 'PathLength', 'StartFlag', 'TerminalPa' ]
            fields2 = fields + ['cat_ID_con']
            updfields= ['NHDPlusID','DSContArea','cat_ID_con','str_ord', 'str_slope','ds_dist_outlet_km',"DSContArea_SqKM",'str_slope_dg','TotDASqKm']
            valueDict = {int(r[0]):(r[1]) for r in arcpy.da.SearchCursor(vaas, fields)}
            strValfieldList = ['NHDPlusID','StreamOrde', 'Slope','PathLength', 'TotDASqKm']
            strValDict = {r[0]:(r[1:]) for r in arcpy.da.SearchCursor(vaas, strValfieldList)}
            where_clause=f'"MERGE_SRC" LIKE \'%{roi}%\''
            print(f'where_clause = {where_clause}')
            awc_where_clause=f'"Shape_Length" >= {awcthresh}'
            print(f'Selecting feature from awc = {awc_where_clause}')
            huclayer1 = arcpy.MakeFeatureLayer_management(hucs,'huclayer1',where_clause = where_clause)
            huclayer2 = arcpy.MakeFeatureLayer_management(hucs,'huclayer2',where_clause = where_clause)
            awclayer1 = arcpy.MakeFeatureLayer_management(awc_events,'awclayer1')
            awclayer2 = arcpy.MakeFeatureLayer_management(awc_events,'awclayer2',where_clause = awc_where_clause)
            print(f'{arcpy.GetCount_management(huclayer1)} huc12s in {roi}')
            print(('*'*100))

            # Modify code to record Hucs that would be dropped and flag these for additional QA rather than dropping them here.
            hucselect_awc = arcpy.SelectLayerByLocation_management(huclayer1, "INTERSECT", awclayer1, None, "SUBSET_SELECTION", "NOT_INVERT") # Select all HUC12s that intersect AWC Events
            hucselect_awcList = [r[0] for r in arcpy.da.SearchCursor(hucselect_awc,'HUC12')] # Create a list of HUC12 numbers from selection
            hucselect_clementi_awc = arcpy.SelectLayerByLocation_management(huclayer2, "CONTAINS_CLEMENTINI", awclayer2, None, "SUBSET_SELECTION", "NOT_INVERT") # Select all HUC12s that intersect AWC Events using clementi option
            hucselect_clementi_awcList = [r[0] for r in arcpy.da.SearchCursor(hucselect_clementi_awc,'HUC12')]# Create a list of HUC12 numbers from clementi selection
            hucCheckList = list((Counter(hucselect_awcList) - Counter(hucselect_clementi_awcList)).elements())# Identify Hucs that are dropped as a result of clementi selection and create list to flag for review later
            hucreviewList.extend(hucCheckList)# add to review list
            hucnum = int(arcpy.GetCount_management(hucselect_awc)[0])
            hucnum_clementi = int(arcpy.GetCount_management(hucselect_clementi_awc)[0])
            diff = hucnum - hucnum_clementi
            print(('*'*100))
            print(f'{hucnum} Huc12s in {roi} intersect awc events input\n{hucnum_clementi} intersect awc events with Clementi intersections (difference of {diff})')
            print(('*'*100))
            hucFields = [f for f in arcpy.ListFields(hucselect_awc)]
            vcount =1
            with arcpy.da.SearchCursor(hucselect_awc,['HUC12','SHAPE@']) as cur:
                for row in cur:
                    print(f'Processing HUC {row[0]}')
                    inhuc = row[1]
                    # ADD if statement here to check if HUC was flagged to have a new outlet catchment else run as is
                    if row[0] in hucNewcatdict:
                        cidcon = hucNewcatdict[row[0]][0]
                        outcatch = hucNewcatdict[row[0]][1]
                        print (f'HUC {row[0]} flagged during review\nNew outlet catchment identified as {cidcon}')
                    else:
                        cat_layer = arcpy.MakeFeatureLayer_management(cats,'cat_layer')
                        # Select by location using awc and huc 12
                        arcpy.SelectLayerByLocation_management(cat_layer,'HAVE_THEIR_CENTER_IN',inhuc,'','NEW_SELECTION')
                        print(f'{vcount}. Finding outlet for HUC {row[0]} out of {arcpy.GetCount_management(cat_layer)} catchments ({hucnum-vcount} remain).\n{("*" * 60)}')
                        catList = [r[0] for r in arcpy.da.SearchCursor(cat_layer, 'NHDPlusID')]
                        intersect = list(set(catList).intersection(valueDict))
                        catDict = {int(i):(valueDict[i]) for i in intersect}
                        # Find Catchment with max drainage area
                        outcatch = max(catDict.items(), key = operator.itemgetter(1))[0]
                        cidcon = roi + '_' + str(int(outcatch))
                    append_value(dist2CoastDict,cidcon,row[0])
                    append_value(huc12Dict, row[0], [int(outcatch),roi,valueDict[int(outcatch)]])
                    append_value(nhdidDict,int(outcatch),[roi,row[0], valueDict[int(outcatch)]])
                    outletList.append(int(outcatch))
                    vcount+=1
                del(row)
            del(cur)

            outlet_cats = arcpy.MakeFeatureLayer_management(cats,'outlet_cats')
            out_expression ='"NHDPlusID" IN ' + str(tuple(outletList))
            #print(out_expression)
            outlet_cats_select = arcpy.SelectLayerByAttribute_management(outlet_cats,'NEW_SELECTION', out_expression)
            print(f'Creating copy of {arcpy.GetCount_management(outlet_cats)} outlet catchments for Region {roi} at {outcatspath}')
            print(('*'*100))

            # Copy outputs
            arcpy.FeatureClassToFeatureClass_conversion(outlet_cats_select,outgdb,outletcatsname)
            arcpy.FeatureToPoint_management(outcatspath, outcatptspath, 'INSIDE')
            # Create Copies to akssf data_dir regional gdbs also
            arcpy.FeatureClassToFeatureClass_conversion(outlet_cats_select,sourcegdb,'awc_huc12_catchment_outlets')
            arcpy.FeatureToPoint_management(outcatspath2, outcatptspath2, 'INSIDE')
            nhdplusoutlets.append(outcatptspath)
            nhdplusawccatouts.append(outcatspath)
            # Add total drainage km from value dict to feature classes and cat_ID_con from regDict
            # Add str slope and str order from vaaDict
            upfcs = [outcatspath, outcatptspath,outcatptspath2,outcatptspath2]
            for upfc in upfcs:
                arcpy.AddField_management(upfc,fields[1],'DOUBLE') # TotDASqKm
                arcpy.AddField_management(upfc,fields2[9],'TEXT')#add cat_ID_con field
                arcpy.AddField_management(upfc, "str_slope", field_type="DOUBLE")
                arcpy.AddField_management(upfc, "str_ord", field_type="SHORT")
                arcpy.AddField_management(upfc, "ds_dist_outlet_km", field_type="DOUBLE")
                arcpy.AddField_management(upfc, "DSContArea_SqKM",'DOUBLE') #add DSContArea_SqKM area field
                arcpy.AddField_management(upfc, "DSContArea",'DOUBLE') #add DSCont area field
                arcpy.AddField_management(upfc, "str_slope_dg",'DOUBLE') #add stream slope degrees field
                with arcpy.da.UpdateCursor(upfc,updfields) as cur:
                    for row in cur:
                        if not row[0] in strValDict:
                            print(f'No records for NHDPLUS feature {row[0]} in VAA table')
                        else:
                            dsarea = strValDict[row[0]][3] * 1e+6 # Convert TotDASqKm to area in meters
                            row[1] = dsarea
                            catcon = roi + '_' + str(int(row[0])) # calculate cat_ID_con
                            row[2] = catcon # calculate cat_ID_con
                            strord = strValDict[row[0]][0] # add str order
                            row[3] = strord # add str order
                            strslope = strValDict[row[0]][1] # add str slope
                            row[4] = strslope # add str slope
                            ds_dist = strValDict[row[0]][2] # convert to km
                            row[5] = ds_dist # add distance to outlet from reach end
                            dsareasqkm = strValDict[row[0]][3] # Populate with TotDASqKm
                            row[6] = dsareasqkm
                            strSlopedg = degrees(atan(strslope)) # Convert unitless rise/run to degrees
                            row[7] = strSlopedg # Populate field
                            row[8] = dsareasqkm #  Copy TotDASqKm from vaa table
                            #print(f'Catchment {catcon} has the following attributes\nslope = {strslope} dg\nstream order = {strord}\nCont area = {dsarea}\nDistance to outlet = {ds_dist}\n{"*"*100}')
                        cur.updateRow(row)
                    del(row)
                del(cur)

            # End roi time
            roi_stop = time.time()
            roi_time = int (roi_stop - roi_start)
            print(f'{roi} Elapsed time: ({datetime.timedelta(seconds=roi_time)})')
            print(f'{"*"*60}')
        else:
            print(f'Catchments for {roi} already created at {outcatspath2}')

    elif roi in tauDem_dat:
        # Start roi time
        roi_start = time.time()
        hucs = tauhucs
        catsList = []
        outletList = []
        print(f'{roi} using data from {region} folder')
        # Set workspace to region folder
        arcpy.env.workspace = region
        gdb = arcpy.ListWorkspaces(workspace_type='FileGDB')
        sourcegdb = gdb[0]
        walk = arcpy.da.Walk(sourcegdb, datatype = ['FeatureClass','Table'])
        for dirpath, dirnames, filenames in walk:
            for filename in filenames:
                if filename == 'cats_merge':
                    cats  = os.path.join(dirpath, filename)
                    append_value(catsDict,roi,cats)
                elif filename == 'streams_merge':
                    streamname = roi + '_' + filename
                    streams = os.path.join(outgdb,streamname)
                    if not arcpy.Exists(streams):
                        print(f'Copying {os.path.join(dirpath, filename)} to {outgdb}')
                        arcpy.FeatureClassToFeatureClass_conversion(os.path.join(dirpath,filename),outgdb,streamname)
                    else:
                        print(f'{streams} already created')
                    #upfcs.append(streams)
                    append_value(strDict, roi, streams)
                    streamsList.append(streams)

        #Output names and paths
        outletcatsname = roi + '_TauAwcH12_cats_outlets'
        outcatspath = os.path.join(outgdb,outletcatsname)
        outcatspath2 = os.path.join(sourcegdb,'awc_huc12_catchment_outlets')
        outletcatptsname = roi + '_TauAwcH12_cats_outlets_pts'
        outcatptspath = os.path.join(outgdb,outletcatptsname)
        outcatptspath2 = os.path.join(sourcegdb,'awc_huc12_catchment_outlets_pts')
        print(('-'*100),'\n')
        if not arcpy.Exists(outcatspath):
            # Build Value dictionary to relate TauDEM gridcodes to contributing area
            if roi == 'Bristol_Bay':
                fields = ['catID','DSContArea']
                fields2 = fields + ['cat_ID_con']
                fields3 = ['catID','DSContArea','cat_ID_con']
                strValfieldList = ['catID','strmOrder', 'Slope', 'USContArea', 'DSContArea', 'DOUTEND', 'DOUTSTART']
                updfields= ['catID','DSContArea','cat_ID_con','str_ord', 'str_slope','ds_dist_outlet_km','DSContArea_SqKM','str_slope_dg']
                strValDict = {r[0]:(r[1:]) for r in arcpy.da.SearchCursor(streams, strValfieldList)}
            else:
                fields = ['LINKNO','DSContArea']
                fields2 = fields + ['cat_ID_con']
                fields3 = ['gridcode','DSContArea','cat_ID_con']
                updfields= ['gridcode','DSContArea','cat_ID_con','str_ord', 'str_slope','ds_dist_outlet_km','DSContArea_SqKM','str_slope_dg']
                strValfieldList = ['LINKNO','strmOrder', 'Slope', 'USContArea', 'DSContArea', 'DOUTEND', 'DOUTSTART']
                strValDict = {r[0]:(r[1:]) for r in arcpy.da.SearchCursor(streams, strValfieldList)}
            valueDict = {int(r[0]):(r[1]) for r in arcpy.da.SearchCursor(streams, fields)}

            awc_where_clause=f'"Shape_Length" >= {awcthresh}'
            print(f'Selecting feature from awc = {awc_where_clause}')
            huclayer1 = arcpy.MakeFeatureLayer_management(hucs,'huclayer1')
            huclayer2 = arcpy.MakeFeatureLayer_management(hucs,'huclayer2')
            awclayer1 = arcpy.MakeFeatureLayer_management(awc_events,'awclayer1')
            awclayer2 = arcpy.MakeFeatureLayer_management(awc_events,'awclayer2',where_clause = awc_where_clause)
            hucselect_reg1 = arcpy.SelectLayerByLocation_management(huclayer1,'INTERSECT',streams,'','NEW_SELECTION') #Select only Hucs in TauDEM roi using streams
            hucselect_reg2 = arcpy.SelectLayerByLocation_management(huclayer2,'INTERSECT',streams,'','NEW_SELECTION') #Select only Hucs in TauDEM roi using streams
            print(f'{arcpy.GetCount_management(hucselect_reg1)} huc12s in {roi}')
            print(('*'*100))
            # Modify code to record Hucs that would be dropped and flag these for additional QA rather than drop them here.
            hucselect_awc = arcpy.SelectLayerByLocation_management(hucselect_reg1, "INTERSECT", awclayer1, None, "SUBSET_SELECTION", "NOT_INVERT") # Select all HUC12s that intersect AWC Events
            hucselect_awcList = [r[0] for r in arcpy.da.SearchCursor(hucselect_awc,'HUC12')] # Create a list of HUC12 numbers from selection
            hucselect_clementi_awc = arcpy.SelectLayerByLocation_management(hucselect_reg2, "CONTAINS_CLEMENTINI", awclayer2, None, "SUBSET_SELECTION", "NOT_INVERT") # Select all HUC12s that intersect AWC Events using clementi option and streams above threshold
            hucselect_clementi_awcList = [r[0] for r in arcpy.da.SearchCursor(hucselect_clementi_awc,'HUC12')]# Create a list of HUC12 numbers from clementi selection
            hucCheckList = list((Counter(hucselect_awcList) - Counter(hucselect_clementi_awcList)).elements())# Identify Hucs that are dropped as a result of clementi selection and create list to flag for review later
            hucreviewList.extend(hucCheckList)# add to review list
            hucnum = int(arcpy.GetCount_management(hucselect_awc)[0])
            hucnum_clementi = int(arcpy.GetCount_management(hucselect_clementi_awc)[0])
            diff = hucnum - hucnum_clementi
            print(('*'*100))
            print(f'{hucnum} Huc12s in {roi} intersect awc events input\n{hucnum_clementi} intersect awc events with Clementi intersections (difference of {diff})')
            print(('*'*100))
            hucFields = [f for f in arcpy.ListFields(hucselect_awc)]
            vcount =1
            with arcpy.da.SearchCursor(hucselect_awc,['HUC12','SHAPE@']) as cur:
                for row in cur:
                    print(f'Processing HUC {row[0]}')
                    inhuc = row[1]
                    if row[0] in hucNewcatdict:
                        cidcon = hucNewcatdict[row[0]][0]
                        outcatch = hucNewcatdict[row[0]][1]
                        print (f'HUC {row[0]} flagged during review\nNew outlet catchment identified as {cidcon}')
                    else:
                        cat_layer = arcpy.MakeFeatureLayer_management(cats,'cat_layer')
                        # Select by location using awc and huc 12
                        arcpy.SelectLayerByLocation_management(cat_layer,'HAVE_THEIR_CENTER_IN',inhuc,'','NEW_SELECTION')
                        print(f'{vcount}. Finding outlet for HUC {row[0]} out of {arcpy.GetCount_management(cat_layer)} catchments ({hucnum-vcount} remain).\n{("*" * 60)}')
                        catList = [r[0] for r in arcpy.da.SearchCursor(cat_layer, f'{fields3[0]}')]
                        intersect = list(set(catList).intersection(valueDict))
                        catDict = {int(i):(valueDict[i]) for i in intersect}
                        # Find Catchment with max drainage area
                        outcatch = max(catDict.items(), key = operator.itemgetter(1))[0]
                        cidcon = roi +'_'+ str(int(outcatch))
                    append_value(dist2CoastDict,cidcon,row[0])
                    append_value(tauhuc12Dict, row[0], [int(outcatch),roi,valueDict[int(outcatch)]])
                    append_value(tauidDict,cidcon,[roi,row[0], valueDict[int(outcatch)]])
                    outletList.append(int(outcatch))
                    vcount+=1
                del(row)
            del(cur)
            outlet_cats = arcpy.MakeFeatureLayer_management(cats,'outlet_cats')
            out_expression =f'"{fields3[0]}" IN ' + str(tuple(outletList))
            #print(out_expression)
            outlet_cats_select = arcpy.SelectLayerByAttribute_management(outlet_cats,'NEW_SELECTION', out_expression)
            print(f'Creating copy of {arcpy.GetCount_management(outlet_cats)} outlet catchments for Region {roi} at {outcatspath}')
            print(('*'*100))

            # Copy outputs
            arcpy.FeatureClassToFeatureClass_conversion(outlet_cats_select,outgdb,outletcatsname)
            arcpy.FeatureToPoint_management(outcatspath, outcatptspath, 'INSIDE')
            # Create Copies to akssf data_dir regional gdbs also
            arcpy.FeatureClassToFeatureClass_conversion(outlet_cats_select,sourcegdb,'awc_huc12_catchment_outlets')
            arcpy.FeatureToPoint_management(outcatspath2, outcatptspath2, 'INSIDE')
            tauoutlets.append(outcatptspath)
            tauawccatouts.append(outcatspath)
            # Add total drainage km from value dict to feature classes and cat_ID_con from regDict
            # Add Stream slope and stream order from stream dictionary
            upfcs = [outcatspath, outcatptspath,outcatptspath2,outcatptspath2]
            for upfc in upfcs:
                arcpy.AddField_management(upfc,fields[1],'DOUBLE') #add DSCont area field
                arcpy.AddField_management(upfc,fields2[2],'TEXT')#add cat_ID_con field
                arcpy.AddField_management(upfc, "str_slope", field_type="DOUBLE")
                arcpy.AddField_management(upfc, "str_ord", field_type="SHORT")
                arcpy.AddField_management(upfc, "ds_dist_outlet_km", field_type="DOUBLE")
                arcpy.AddField_management(upfc, "DSContArea_SqKM",'DOUBLE') # add DSCont area field
                arcpy.AddField_management(upfc, 'str_slope_dg','DOUBLE') # add stream slope in degrees field
                with arcpy.da.UpdateCursor(upfc,updfields) as cur:
                    for row in cur:
                        dsarea = strValDict[row[0]][3] # Update ds contributing area
                        row[1] = int(dsarea)
                        catcon = roi + '_' + str(int(row[0])) # calculate cat_ID_con
                        row[2] = catcon # calculate cat_ID_con
                        strord = strValDict[row[0]][0] # add str order
                        row[3] = strord # add str order
                        strslope = strValDict[row[0]][1] # add str slope
                        row[4] = strslope # add str slope
                        ds_dist = strValDict[row[0]][4] * 1e-3 # convert to km
                        row[5] = ds_dist # add distance to outlet from reach end
                        dsareasqkm = int(strValDict[row[0]][3]) * 1e-6 # Update ds contributing area
                        row[6] = dsareasqkm
                        strSlopedg = degrees(atan(strslope))
                        row[7] = strSlopedg
                        #print(f'Catchment {catcon} has the following attributes\nslope = {strslope} dg\nstream order = {strord}\nCont area = {dsarea}\nDistance to outlet = {ds_dist}\n{"*"*100}')
                        cur.updateRow(row)
                    del(row)
                del(cur)
            # End roi time
            roi_stop = time.time()
            roi_time = int (roi_stop - roi_start)
            print(f'{roi} Elapsed time: ({datetime.timedelta(seconds=roi_time)})')
            print(f'{"*"*60}')

# End timing
processEnd = time.time()
processElapsed = int(processEnd - processStart)
processSuccess_time = datetime.datetime.now()
# Report success
print(f'Process completed at {processSuccess_time.strftime("%Y-%m-%d %H:%M")} '
      f'(Elapsed time: {datetime.timedelta(seconds=processElapsed)})')
print(f'{"*"*100}')

Begin 2023-03-01 11:00:33.149113
Bristol_Bay
Bristol_Bay using data from D:\GIS\AKSSF\Bristol_Bay folder
Copying D:\GIS\AKSSF\Bristol_Bay\Bristol_Bay.gdb\streams_merge to D:\GIS\outputs_2023\outputs_2023.gdb
---------------------------------------------------------------------------------------------------- 

Selecting feature from awc = "Shape_Length" >= 500
826 huc12s in Bristol_Bay
****************************************************************************************************
****************************************************************************************************
613 Huc12s in Bristol_Bay intersect awc events input
576 intersect awc events with Clementi intersections (difference of 37)
****************************************************************************************************
Processing HUC 190302030205
1. Finding outlet for HUC 190302030205 out of 107 catchments (612 remain).
************************************************************
Processing HUC 19030

## Write huc review list to output text file

In [11]:
# no need to run if
# print (os.getcwd())
# with open("HUCS4Review.txt", "w") as output:
#     output.write(str(hucreviewList))
hucreviewList
sourcegdb

'D:\\GIS\\AKSSF\\Kodiak\\Kodiak.gdb'

## Section 2.1
### Merge all outlet points together and calculate distance to coastline
This chunk is dependent on the data dictionaries created in Step 2
Calculate Distance to Coast from outlet catchment point to the nearest coastline as a straight line distance
 * Generate near table and export as seperate csv

NHDPlus Section


In [10]:
import arcpy, datetime
import numpy as pd

# Input path to coastline
# Merge all catchment outlet centroids togethera
nhdoutletsname = 'AKSSF_NHDPlus_awcHuc12_outlet_cats_points'
nhdoutletspath = os.path.join(outgdb, nhdoutletsname)

#if not arcpy.Exists(nhdoutletspath):
all_nhd_outlet_pts = arcpy.Merge_management(nhdplusoutlets,nhdoutletspath)
# Start timing function
start = datetime.datetime.now()
print(f'Getting distance to coast {datetime.datetime.now()}...')
arcpy.analysis.Near(all_nhd_outlet_pts, coast, None, "NO_LOCATION", "NO_ANGLE", "GEODESIC", "NEAR_DIST NEAR_DIST")
arcpy.AlterField_management(all_nhd_outlet_pts,'NEAR_DIST','dist_catch_coast_km','dist_catch_coast_km' )
arcpy.AddField_management(all_nhd_outlet_pts,'HUC12','TEXT')
arcpy.AddField_management(all_nhd_outlet_pts,'HUC12_Review','SHORT')

# Convert distance in meters to km
with arcpy.da.UpdateCursor(all_nhd_outlet_pts,['dist_catch_coast_km','NHDPlusID','HUC12','HUC12_Review']) as cur:
    for row in cur:
        row[0] = row[0] * 0.001
        Huc12 = nhdidDict[row[1]][1] # add HuC12 id
        row[2] = Huc12
        if Huc12 in hucreviewList:
            row[3] = 1
        else:
            row[3] = 0
        cur.updateRow(row)
    del(row)
del(cur)
print(f'Process complete')
# else:
#     print(f'Outlet points already created at {nhdoutletspath}')


Getting distance to coast 2022-04-14 17:49:37.348710...
Process complete


TauDEM Section


In [12]:
import arcpy, datetime
import numpy as pd

# Merge all catchment outlet centroids together
tauoutname = 'AKSSF_TauDEM_awcHuc12_outlet_cats_points'
tauoutpath = os.path.join(outgdb, tauoutname)

#if not arcpy.Exists(tauoutpath):
all_tau_outpts = arcpy.Merge_management(tauoutlets,tauoutpath)
# Start timing function
start = datetime.datetime.now()
print(f'Getting distance to coast {datetime.datetime.now()}...')
arcpy.analysis.Near(all_tau_outpts, coast, None, "NO_LOCATION", "NO_ANGLE", "GEODESIC", "NEAR_DIST NEAR_DIST")
arcpy.AlterField_management(all_tau_outpts,'NEAR_DIST','dist_catch_coast_km','dist_catch_coast_km' )
arcpy.AddField_management(all_tau_outpts,'HUC12','TEXT')
arcpy.AddField_management(all_tau_outpts,'DSContAreaSqKM','DOUBLE')
arcpy.AddField_management(all_tau_outpts,'HUC12_Review','SHORT')

# Convert distance in meters to km
with arcpy.da.UpdateCursor(all_tau_outpts,['dist_catch_coast_km','cat_ID_con','HUC12','DSContArea','DSContAreaSqKM','HUC12_Review']) as cur:
    for row in cur:
        row[0] = row[0] * 0.001
        Huc12 = tauidDict[row[1]][1] # Identify HUC12
        row[2] = Huc12 #add HUC12
        row[4] = int(row[3])/1000000 #convert sq meters to sq km
        if Huc12 in hucreviewList:
            row[5] = 1
        else:
            row[5] = 0
        cur.updateRow(row)
    del(row)
del(cur)
print(f'Process complete')
# else:
#     print(f'Outlet points already created at {tauoutpath}')

Getting distance to coast 2023-03-01 12:33:02.492047...
Process complete



## Merge NHD and Tau points together and export as CSV


In [14]:
tauoutpath

'D:\\GIS\\outputs_2023\\outputs_2023.gdb\\AKSSF_TauDEM_awcHuc12_outlet_cats_points'

In [16]:
print(f'Merging all available catchment outlet points')
# NHDPoints

# nhdoutletsname = 'AKSSF_NHDPlus_awcHuc12_outlet_cats_points'
# nhdoutletspath = os.path.join(outgdb, nhdoutletsname)
nhdoutletspath = r'D:\GIS\AKSSF_awcHuc12_cv_Final\AKSSF_awcHuc12_cv_Final.gdb\AKSSF_NHDPlus_awcHuc12_outlet_cats_points'


# Taupoints
tauoutname = 'AKSSF_TauDEM_awcHuc12_outlet_cats_points'
tauoutpath = os.path.join(outgdb, tauoutname)

# All points
catpointsname = 'AKSSF_awcHuc12_outlet_cats_points'
catpointspath = os.path.join(outgdb, catpointsname)

# Create FieldMappings object to manage merge output fields
out_fms = arcpy.FieldMappings()

# Add all fields from both point fcs
out_fms.addTable(nhdoutletspath)
out_fms.addTable(tauoutpath)

# Add input fields
out_fm_dsdrain = arcpy.FieldMap()
out_fm_dsdrain.addInputField(nhdoutletspath,'TotDASqKm')
out_fm_dsdrain.addInputField(tauoutpath,'DSContAreaSqKM')

# Set name of new output field "DsContAreaSK"
dsdrain = out_fm_dsdrain.outputField
dsdrain.name = "DsContAreaSqKm"
out_fm_dsdrain.outputField = dsdrain

# add to field mappings
out_fms.addFieldMap(out_fm_dsdrain)

for field in out_fms.fields:
    if field.name not in ['cat_ID_con', 'DsContAreaSqKm','dist_catch_coast_km', 'HUC12', 'HUC12_Review']:
        out_fms.removeFieldMap(out_fms.findFieldMapIndex(field.name))

#if not arcpy.Exists(catpointspath):
addSourceInfo = "ADD_SOURCE_INFO"
cats_outlets = arcpy.Merge_management([nhdoutletspath,tauoutpath],
                                      catpointspath,
                                      out_fms,
                                      addSourceInfo)

#else:
#    print(f'AKSSF AWC Catchment outlets already identified and exported to {catpointspath}')
print(f'Merge Complete')

Merging all available catchment outlet points
Merge Complete


### Convert to df and examine

In [17]:
import numpy
import pandas as pd
pd.set_option("display.max_rows", None)
# Make catchment points df
cat_df = pd.DataFrame()
cat_field_list = []

for field in arcpy.ListFields(catpointspath):
    print(field.name)
    cat_field_list.append(field.name)
cat_arr = arcpy.da.TableToNumPyArray(catpointspath, ['cat_ID_con','dist_catch_coast_km','DsContAreaSqKm','HUC12','HUC12_Review'])
cat_df = pd.DataFrame(cat_arr)
cat_df = cat_df.set_index('cat_ID_con')
cat_df

OBJECTID
Shape
cat_ID_con
dist_catch_coast_km
HUC12
HUC12_Review
DsContAreaSqKm
MERGE_SRC


dist_catch_coast_km  DsContAreaSqKm  \
cat_ID_con                                                         
Cook_Inlet_75004200000901              21.633384       36.962575   
Cook_Inlet_75004200001724              17.599013      170.812175   
Cook_Inlet_75004200000437               0.318196        7.584725   
Cook_Inlet_75004200001493               0.147499        9.640600   
Cook_Inlet_75004200009084               0.787633       26.753250   
Cook_Inlet_75004200003619               0.089052      135.005850   
Cook_Inlet_75004200001047               0.548926       12.012100   
Cook_Inlet_75004200016346               0.171205       10.734100   
Cook_Inlet_75004200010717               0.349695       15.916525   
Cook_Inlet_75004200010096               0.076809        7.266700   
Cook_Inlet_75004200003399               0.173348       37.866925   
Cook_Inlet_75004200000722               0.029182       48.072025   
Cook_Inlet_75004200000726               0.315951       66.517075   
Cook_Inlet_75004200012986               1.332331       43.229850   
Cook_Inlet_75004200008847               0.015401        3.652100   
Cook_Inlet_75004200010465               0.021366       10.441625   
Cook_Inlet_75004200014411               0.195336       25.663575   
Cook_Inlet_75004200012680               0.175628       28.307425   
Cook_Inlet_75004200000559               0.087143        2.790175   
Cook_Inlet_75004200007843               0.218678        1.171575   
Cook_Inlet_75004200009093               0.456912       22.003525   
Cook_Inlet_75004200008970               0.082471       14.768975   
Cook_Inlet_75004200005429              21.477566       37.976200   
Cook_Inlet_75004200012771               0.016949      127.594800   
Cook_Inlet_75004200012099               2.280098      266.149950   
Cook_Inlet_75004200001003               0.309558       14.935775   
Cook_Inlet_75004200000848               0.748290       10.283725   
Cook_Inlet_75004200011012               0.110729      289.799275   
Cook_Inlet_75004200006975               0.128601       19.503725   
Cook_Inlet_75004200005415              16.890604       55.250425   
Cook_Inlet_75004200000064               0.985950       97.162700   
Cook_Inlet_75004200001191               0.367926       19.096450   
Cook_Inlet_75004200001574               0.100115        3.595850   
Cook_Inlet_75004200003989               6.715231      403.877375   
Cook_Inlet_75004200002199               0.204518      101.170825   
Cook_Inlet_75004200005203               0.481730       64.664875   
Cook_Inlet_75004200001716               0.872756      295.298075   
Cook_Inlet_75004200008853               0.297196       58.593775   
Cook_Inlet_75004200008845               1.072117       15.334600   
Cook_Inlet_75004200005283               0.106344        4.820600   
Cook_Inlet_75004200005907               0.112917        1.054550   
Cook_Inlet_75004300004332               0.488941      330.124075   
Cook_Inlet_75004300005723               0.634398       65.409050   
Cook_Inlet_75004300006970               0.194162      501.735400   
Cook_Inlet_75004300002057              21.842191       45.969325   
Cook_Inlet_75004300005518              13.313859       73.485400   
Cook_Inlet_75004300004701               6.612002      154.661600   
Cook_Inlet_75004300004365               5.063402       93.164800   
Cook_Inlet_75004300006839               0.064884       71.286925   
Cook_Inlet_75004300007978               0.183661       87.060725   
Cook_Inlet_75004300007859               0.704871       26.989025   
Cook_Inlet_75004300005004               0.267006      230.420400   
Cook_Inlet_75004300005103              40.356818       56.978100   
Cook_Inlet_75004300000311               9.980660       51.811850   
Cook_Inlet_75004300008012               0.980620       59.414950   
Cook_Inlet_75004300001135               0.075955       57.483925   
Cook_Inlet_75004300007259               0.190951      136.892900   
Cook_Inlet_750043

### Export csv of outlet points for NHDPlus regions


In [14]:
import os
#Export CSV to read into R
catpts_outname = 'AKSSF_awcHuc12_dist_catch_coast_km.csv'
outlets_csv = os.path.join(outdir,catpts_outname)
if not arcpy.Exists(outlets_csv):
    arcpy.da.NumPyArrayToTable(cat_arr,outlets_csv)
    print('CSV export complete')
else:
    print(f'Csv of catchment outlet points already exported to {outlets_csv}')
print('----------')

CSV export complete
----------


## Section 3
### Watersheds
Generate Watersheds
* If watersheds have already been created there is no need to run this section again in order for subsequent process to run.
### 2022-04-06 Need to Modify a bit to accept an input list or point file to run a subset of additional watersheds based on QC review of the original outputs
I think just set the idlist = list of catchment id's found during qc and make sure to save to a new location and not overwrite originals.

In [18]:
# Watersheds
import arcpy, time, datetime, os
import pandas as pd
from functools import reduce
import arcpy, time, os, datetime, operator

arcpy.env.workspace = data_dir
regions = arcpy.ListWorkspaces()
arcpy.env.overwriteOutput = True
arcpy.env.qualifiedFieldNames = False
sr = arcpy.SpatialReference(3338)  #'NAD_1983_Alaska_Albers'
arcpy.env.outputCoordinateSystem = sr

wtdDict = {}

# Separate data by source type
nhdplus_dat = ['Cook_Inlet','Copper_River']
tauDem_dat = ['Bristol_Bay', 'Kodiak', 'Prince_William_Sound']

# Limit to Cook inlet for testing
#regions = ['D:\\GIS\\AKSSF\\Cook_Inlet', 'D:\\GIS\\AKSSF\\Copper_River' ,'D:\\GIS\\AKSSF\\Prince_William_Sound']
regions = ['D:\\GIS\\AKSSF\\Bristol_Bay', 'D:\\GIS\\AKSSF\\Kodiak']
#regions = ['D:\\GIS\\AKSSF\\Bristol_Bay']

# Start timing function
processStart = time.time()
processStartdt = datetime.datetime.now()

for region in regions:
    reg_start = time.time()
    roi = os.path.basename(region)
    print(roi)
    if roi in nhdplus_dat:
        try:
            wtdList = []
            arcpy.env.workspace = region
            gdb = arcpy.ListWorkspaces(workspace_type='FileGDB')
            ingdb = gdb[0]
            # set inputs
            vaa = os.path.join(ingdb, "vaa_merge")
            cats = os.path.join(ingdb, "cats_merge")
            streams = os.path.join(ingdb, "NHDFlowline_merge")
            outcats = os.path.join(ingdb, "awc_huc12_catchment_outlets")
            # Create list of nhdplus ids for outlet catchments
            idList = [int(row[0]) for row in arcpy.da.SearchCursor(outcats,'NHDPlusID')]
            #Make test list of few small catchments
            #idList = [75004400004166,75004400004344, 75004400010328]
            # Get list of index names for cats merge and add index if not already created
            index_names = [i.name for i in arcpy.ListIndexes(cats)]
            print(index_names)
            if 'NHDPlusID_index' not in index_names:
                print (f'Creating index for {cats}')
                arcpy.AddIndex_management(cats,'NHDPlusID','NHDPlusID_index')
            else:
                print(f'{cats} Indexed')

            #watersheds feature dataset for storing fcs
            fdatname = roi + '_Watersheds'
            fdat = os.path.join(outgdb,fdatname)
            if not arcpy.Exists(fdat):
                arcpy.management.CreateFeatureDataset(outgdb, fdatname, sr)
            else:
                print(f'{fdat} exists for {roi}')

            vaa_df1 = pd.DataFrame(arcpy.da.TableToNumPyArray(vaa, ("NHDPlusID", "FromNode", "ToNode", "StartFlag")))
            stream_df = pd.DataFrame(arcpy.da.TableToNumPyArray(streams, ("NHDPlusID", "FType")))
            dfs = [vaa_df1, stream_df]
            vaa_df = reduce(lambda left,right: pd.merge(left,right,on='NHDPlusID',how="outer"), dfs)
            # remove pipelines
            vaa_df = vaa_df[(vaa_df['FType'] != 428 )]
            vaa_df

            c=1
            for id in idList:
                iteration_start = time.time()
                print(f'{c}. Starting watershed for catchment {str(id)} ({(len(idList) - c)} remaining)')
                rec = [id]
                up_ids = []
                up_ids.append(rec)
                rec_len = len(rec)
                hws_sum = 0

                while rec_len != hws_sum:
                    fromnode = vaa_df.loc[vaa_df["NHDPlusID"].isin(rec), "FromNode"]
                    rec = vaa_df.loc[vaa_df["ToNode"].isin(fromnode), "NHDPlusID"]
                    rec_len = len(rec)
                    rec_hws = vaa_df.loc[vaa_df["ToNode"].isin(fromnode), "StartFlag"]
                    hws_sum = sum(rec_hws)
                    up_ids.append(rec)
                #up_ids is a list with more than numbers, use extend to only keep numeric nhdplusids
                newup_ids = []
                for x in up_ids:
                    newup_ids.extend(x)

                tempLayer = "catsLyr"
                expression = '"NHDPlusID" IN ({0})'.format(', '.join(map(str, newup_ids)) or 'NULL')
                arcpy.MakeFeatureLayer_management(cats, tempLayer, where_clause=expression)
                outdis = "memory/wtd_" + str(round(id))
                outwtd = os.path.join(fdat,f'{roi}_wtd_{str(int(id))}')
                dis = arcpy.Dissolve_management(tempLayer, outdis)
                watershed = arcpy.EliminatePolygonPart_management(dis, outwtd,"PERCENT", "0 SquareKilometers", 90, "CONTAINED_ONLY")
                wtdList.append(outwtd)
                append_value(wtdDict,roi,outwtd)

                # Stop iteration timer
                iteration_stop = time.time()
                iter_time = int (iteration_stop - iteration_start)
                print(f'Elapsed time: ({datetime.timedelta(seconds=iter_time)})')
                print(f'{"*"*60}')
                c+=1

            wtd_merge = arcpy.Merge_management(wtdList, os.path.join(ingdb,'awc_huc12_wtds_merge'),'','ADD_SOURCE_INFO')
            arcpy.AddField_management(wtd_merge,'cat_ID_con','TEXT')
            arcpy.AddField_management(wtd_merge,'cat_ID','DOUBLE')
            arcpy.AddField_management(wtd_merge,'cat_ID_txt','TEXT')
            arcpy.AddField_management(wtd_merge,'NHDPlusID','DOUBLE')
            with arcpy.da.UpdateCursor(wtd_merge,['MERGE_SRC','NHDPlusID','cat_ID_con','cat_ID','cat_ID_txt']) as cur:
                for row in cur:
                    # Pull nhdplus id from merge source and calculate fields
                    nhdplusid= int(row[0].split('_')[-1])
                    row[1] = nhdplusid
                    row[2] = roi + '_' + str(nhdplusid)
                    row[3] = nhdplusid
                    row[4] = str(nhdplusid)
                    cur.updateRow(row)
                del(row)
            del(cur)
            arcpy.CopyFeatures_management(wtd_merge,os.path.join(outgdb,f'{roi}_AwcHuc12_wtds_merge' ))

            # Stop iteration timer
            reg_stop = time.time()
            reg_time = int (reg_stop - reg_start)
            print(f'{roi} Elapsed time: ({datetime.timedelta(seconds=reg_time)})')
            print(f'{"*"*100}')

        except:
            e = sys.exc_info()[1]
            print(e.args[0])
            arcpy.AddError(e.args[0])

    elif roi in tauDem_dat:
        try:
            reg_start = time.time()
            wtdList = []
            arcpy.env.workspace = region
            gdb = arcpy.ListWorkspaces(workspace_type='FileGDB')
            ingdb = gdb[0]
            # set inputs
            cats = os.path.join(ingdb, "cats_merge")
            streams = os.path.join(ingdb, "streams_merge")
            outcats = os.path.join(ingdb, "awc_huc12_catchment_outlets")

            # Create list of catID/gridcode ids for outlet catchments
            idList = [int(row[0]) for row in arcpy.da.SearchCursor(outcats,'catID')]
            index_names = [i.name for i in arcpy.ListIndexes(cats)]
            if 'catid_index' not in index_names:
                print (f'Creating index for {cats}')
                arcpy.AddIndex_management(cats, "catID", "catid_index")
            else:
                print(f'{cats} Indexed')
            #watersheds feature dataset for storing fcs
            fdatname = roi + '_Watersheds'
            fdat = os.path.join(outgdb,fdatname)
            if not arcpy.Exists(fdat):
                arcpy.management.CreateFeatureDataset(outgdb, fdatname, sr)
            else:
                print(f'{fdat} exists for {roi}')
            fields = arcpy.ListFields(streams)
            if roi == 'Bristol_Bay':
                str_df_fields = ["catID", "upCatID1", "upCatID2"]
                str_df = pd.DataFrame(arcpy.da.FeatureClassToNumPyArray(streams, ("catID", "upCatID1", "upCatID2")))
                hws_codes = [999999, 1999999, 2999999, 3999999, 4999999]
            else:
                str_df_fields = ["LINKNO", "USLINKNO1", "USLINKNO2"]
                str_df = pd.DataFrame(arcpy.da.FeatureClassToNumPyArray(streams, ("LINKNO", "USLINKNO1", "USLINKNO2")))
                hws_codes = [-1]

            # Generate watersheds
            c=1
            for id in idList:
                iteration_start = time.time()
                print(f'{c}. Starting watershed for catchment {str(id)} ({(len(idList) - c)} remaining)')
                rec = [id]
                up_ids = []
                sum_rec = sum(rec)
                while(sum_rec > 0):
                    up_ids.append(rec)
                    rec = str_df.loc[str_df[str_df_fields[0]].isin(rec), (str_df_fields[1], str_df_fields[2])]
                    rec = pd.concat([rec[str_df_fields[1]], rec[str_df_fields[2]]])
                    sum_rec = sum(rec)
                # up_ids is a list with more than numbers, use extend to only keep numeric nhdplusids
                newup_ids = []
                for x in up_ids:
                    newup_ids.extend(x)

                tempLayer = "catsLyr"
                expression = '"catID" IN ({0})'.format(', '.join(map(str, newup_ids)) or 'NULL')
                arcpy.MakeFeatureLayer_management(cats, tempLayer)
                arcpy.management.SelectLayerByAttribute(tempLayer, "NEW_SELECTION", expression, None)
                print("Starting dissolve")
                outdis = "memory/wtd_" + str(round(id))
                outwtd = os.path.join(fdat,f'{roi}_wtd_{str(int(id))}')
                dis = arcpy.Dissolve_management(tempLayer, outdis)
                watershed = arcpy.EliminatePolygonPart_management(dis, outwtd,"PERCENT", "0 SquareKilometers", 90, "CONTAINED_ONLY")
                wtdList.append(watershed)
                append_value(wtdDict,roi,outwtd)

                # Stop iteration timer
                iteration_stop = time.time()
                iter_time = int (iteration_stop - iteration_start)
                print(f'Elapsed time: ({datetime.timedelta(seconds=iter_time)})')
                print(f'{"*"*60}')
                c+=1
            print(f'Begin merge all watersheds for {roi}')
            wtd_merge = arcpy.Merge_management(wtdList, os.path.join(ingdb,'awc_huc12_wtds_merge'),'','ADD_SOURCE_INFO')
            arcpy.AddField_management(wtd_merge,'cat_ID_con','TEXT')
            arcpy.AddField_management(wtd_merge,'cat_ID','DOUBLE')
            arcpy.AddField_management(wtd_merge,'cat_ID_txt','TEXT')
            with arcpy.da.UpdateCursor(wtd_merge,['MERGE_SRC','cat_ID_con','cat_ID','cat_ID_txt']) as cur:
                for row in cur:
                    gridcode= int(row[0].split('_')[-1])
                    row[1] = roi + '_' + str(gridcode)
                    row[2] = int(gridcode)
                    row[3] = str(gridcode)
                    cur.updateRow(row)
                del(row)
            del(cur)
            print(f'Additional copy of merged watersheds saved to {os.path.join(outgdb, f"{roi}_AwcHuc12_wtds_merge" )}')
            arcpy.CopyFeatures_management(wtd_merge,os.path.join(outgdb, f'{roi}_AwcHuc12_wtds_merge' ))

            # Stop iteration timer
            reg_stop = time.time()
            reg_time = int (reg_stop - reg_start)
            print(f'{roi} Elapsed time: ({datetime.timedelta(seconds=reg_time)})')
            print(f'{"*"*100}')

        except:
            e = sys.exc_info()[1]
            print(e.args[0])
            arcpy.AddError(e.args[0])
    else:
        print(f'{roi} not found - check inputs')
        sys.exit(f'{roi} not found - check inputs')

# End timing
processEnd = time.time()
processElapsed = int(processEnd - processStart)
processSuccess_time = datetime.datetime.now()

# Report success
print(f'Process completed at {processSuccess_time.strftime("%Y-%m-%d %H:%M")} '
      f'(Elapsed time: {datetime.timedelta(seconds=processElapsed)})')
print(f'{"*"*100}')




Bristol_Bay
D:\GIS\AKSSF\Bristol_Bay\Bristol_Bay.gdb\cats_merge Indexed
1. Starting watershed for catchment 1003859 (612 remaining)
Starting dissolve
Elapsed time: (0:00:01)
************************************************************
2. Starting watershed for catchment 1004129 (611 remaining)
Starting dissolve
Elapsed time: (0:00:02)
************************************************************
3. Starting watershed for catchment 1006858 (610 remaining)
Starting dissolve
Elapsed time: (0:00:01)
************************************************************
4. Starting watershed for catchment 1007408 (609 remaining)
Starting dissolve
Elapsed time: (0:00:01)
************************************************************
5. Starting watershed for catchment 1008168 (608 remaining)
Starting dissolve
Elapsed time: (0:00:01)
************************************************************
6. Starting watershed for catchment 1008527 (607 remaining)
Starting dissolve
Elapsed time: (0:00:01)
***********

## TROUBLESHOOTING BLOCK
### Zonal statistics as table is failing with unknown error when run on watershed_merge and slope/elev rasters if using 'ALL' statistics.
Try alternative methods.  Below is test chunk for iterating over a list of stats individually and join results back to a copy of the merged watershed table.
* Cannot Run ZonalStatistics because tool does not process overlapping polygons as individual features whereas ZonalStatistics as table will




In [16]:
### TEST CHUNK###

# import os, arcpy,time, datetime
# arcpy.env.overwriteOutput = True
#
# testoutgdb = r"C:\\Users\\dwmerrigan\\Documents\\GitHub\\ArcGIS_Default\\ArcGIS_Default.gdb"
# wtd_merge = r"D:\\GIS\\AKSSF_awcHuc12_cv\\AKSSF_awcHuc12_cv.gdb\\Cook_Inlet_AwcHuc12_wtds_merge"
# wtd_cur_fields = ['cat_ID_txt', 'cat_ID',"cat_ID_con"]
# elev_rast = r"D:\\GIS\\AKSSF\\Cook_Inlet\\elev.tif"
# zstats = ['MIN_MAX_MEAN','STD']
# roi = 'Cook_Inlet'
#
# # Elevation variables
# wtd_merge_elev_table_name = roi + "_Watersheds_Merge_ElevZstats"
# wtd_merge_elev_table_path = os.path.join(testoutgdb, wtd_merge_elev_table_name)
#
# # list to store zonal stat tables
# wtdelevstats =[]
#
# # Create field mappings
# elev_fm = arcpy.FieldMap()
# elev_fms = arcpy.FieldMappings()
# for field in arcpy.ListFields(wtd_merge)[6:]:
#     elev_fm = arcpy.FieldMap()
#     elev_fm.addInputField(wtd_merge,field.name)
#     elev_fm.mergeRule = 'First'
#     # Set properties of the output name.
#     f_name = elev_fm.outputField
#     f_name.name = field.name
#     f_name.aliasName = field.name
#     elev_fm.outputField = f_name
#     elev_fms.addFieldMap(elev_fm)
#
# # Make copy of watershed merge input as table to join stats fields
# wtd_elev_metrics_table = arcpy.TableToTable_conversion(wtd_merge,
#                                                        testoutgdb,
#                                                        wtd_merge_elev_table_name,
#                                                        '',
#                                                        elev_fms,
#                                                        )
# # Add region identifier field for watershed tables                                                )
# arcpy.AddField_management(wtd_elev_metrics_table,'region',field_type='TEXT')
# # expression to calculate region field with roi name
# exp =  '"'+roi+'"'
# arcpy.CalculateField_management(wtd_elev_metrics_table,'region',exp)
#
# zstat_start = time.time()
# for stat in zstats:
#     outstattable = os.path.join(testoutgdb,f'{roi}_wtdElev{stat}')
#     zstat_start1 = time.time()
#     try:
#         print (f'running {stat}')
#         stat_table = ZonalStatisticsAsTable(in_zone_data = wtdmerge,
#                                             zone_field = wtd_cur_fields[0],
#                                             in_value_raster = elev_rast,
#                                             out_table = outstattable,
#                                             statistics_type=stat
#                                             )
#
#         stat_fields = [f.name for f in arcpy.ListFields(stat_table)]
#         arcpy.JoinField_management(wtd_elev_metrics_table,
#                                wtd_cur_fields[0],
#                                stat_table,
#                                wtd_cur_fields[0],
#                                stat_fields[5:]
#                                )
#
#         # Report time
#         zstat_stop1 = time.time()
#         zstat_time1 = int (zstat_stop1 - zstat_start1)
#         print(f'Watershed elev Zonal Stats for {stat} Elapsed time: ({datetime.timedelta(seconds=zstat_time1)})')
#         print(f'{"*"*100}')
#     except:
#         e = sys.exc_info()[1]
#         print(e.args[0])
#         arcpy.AddError(e.args[0])
# # Report time
# zstat_stop = time.time()
# zstat_time = int (zstat_stop - zstat_start)
# print(f'Watershed elev Zonal Stats for {roi} Elapsed time: ({datetime.timedelta(seconds=zstat_time)})')
# print(f'{"*"*100}')

## Section 4
Calculate Covariates


In [19]:
from arcpy.sa import *
arcpy.env.workspace = data_dir
arcpy.env.overwriteOutput = True
sr = arcpy.SpatialReference(3338) #'NAD_1983_Alaska_Albers'
arcpy.env.outputCoordinateSystem = sr
regions  = arcpy.ListWorkspaces(workspace_type="Folder")

# Lists for variables not needed at present time
#cat_asp_ztables = []
#wtd_asp_ztables = []
#cat_pernorth_taba_tables=[]

# Lists to store output tables
wtd_pernorth_taba_tables=[]
wtd_lp_tabint_tables = []
wtd_glac_tabint_tables = []
wtd_wet_taba_tables = []
cat_elev_ztables = []
wtd_elev_ztables = []
cat_slope_ztables = []
wtd_slope_ztables = []
lcld_Ztables = []

# Clear lists
cat_cur_fields = []
wtd_cur_fields = []

# Start timing function
processStart = time.time()
processStartdt = datetime.datetime.now()

# Split data by type
nhdplus_dat = ['Cook_Inlet','Copper_River']
tauDem_dat = ['Bristol_Bay', 'Kodiak', 'Prince_William_Sound']

# Limit to ci for testing
#regions = ['D:\\GIS\\AKSSF\\Cook_Inlet', 'D:\\GIS\\AKSSF\\Copper_River' ,'D:\\GIS\\AKSSF\\Prince_William_Sound']
regions = ['D:\\GIS\\AKSSF\\Bristol_Bay', 'D:\\GIS\\AKSSF\\Kodiak']
# regions = ['D:\\GIS\\AKSSF\\Cook_Inlet','D:\\GIS\\AKSSF\\Copper_River']
# Try with both data types
# regions = ['D:\\GIS\\AKSSF\\Prince_William_Sound','D:\\GIS\\AKSSF\\Cook_Inlet','D:\\GIS\\AKSSF\\Copper_River']

for region in regions:
    roi = os.path.basename(region)
    # expression to calculate region field with roi name
    exp =  '"'+roi+'"'
    if roi in nhdplus_dat:
        lakes_fc = nhd_lakes_fc
        # Fields for update cursor
        cat_cur_fields = ['cat_ID_txt', 'NHDPlusID',"cat_ID_con"]
        wtd_cur_fields = ['cat_ID_txt', 'cat_ID',"cat_ID_con"]
        print (f'{roi} in {nhdplus_dat} AKSSF list, using cat_fields {cat_cur_fields} and watershed fields {wtd_cur_fields}')
        print(f'{"*"*100}')
    # Set data and variables unique to regions with TauDEM Data
    elif roi in tauDem_dat:
        lakes_fc = tau_lakes_fc
        # Fields for update cursor
        if roi == 'Bristol_Bay':
            cat_cur_fields = ['cat_ID_txt', 'catID',"cat_ID_con"]
            wtd_cur_fields = ['cat_ID_txt', 'cat_ID',"cat_ID_con"]
        else:
            cat_cur_fields = ['cat_ID_txt', 'gridcode',"cat_ID_con"]
            wtd_cur_fields = ['cat_ID_txt', 'cat_ID',"cat_ID_con"]
        print (f'{roi} in {tauDem_dat} TauDEM list, using cat_fields {cat_cur_fields} and watershed fields {wtd_cur_fields}')
        print(f'{"*"*100}')
    # Start iter timing function
    iteration_start = time.time()
    # Set workspace to region folder
    arcpy.env.workspace = region
    walk = arcpy.da.Walk(region, datatype = ['FeatureClass','RasterDataset'])
    for dirpath, dirnames, filenames in walk:
        for filename in filenames:
            # Set merged watersheds dataset
            if 'awc_huc12_wtds_merge'== filename:
                wtdpath = os.path.join(dirpath,filename)
                wtdname = roi +'_'+ filename
                # Make local copy projected in AKAlbers
                wtd_merge = os.path.join(dirpath, filename)
                print(f'Merged watershed dataset {filename} found')
                print(f'{"*"*100}')
                wtdfieldnames = []
                wtdlstFields = arcpy.ListFields(wtd_merge)
                for field in wtdlstFields:
                    wtdfieldnames.append(field.name)
                if str(wtd_cur_fields[0]) in wtdfieldnames:
                    print (f'{wtd_cur_fields[0]} field already in dataset')
                    print(f'{"*"*100}')
                else:
                    print (f'Adding {wtd_cur_fields[0]} field to watershed dataset {wtd_merge}')
                    print(f'{"*"*100}')
                    # add cat_ID_txt field and concat cat_ID + region
                    arcpy.AddField_management(wtd_merge, str(wtd_cur_fields[0]),field_type='TEXT')
                    # populate cat_ID_txt
                    with arcpy.da.UpdateCursor(wtd_merge, wtd_cur_fields[0:2]) as cur:
                        for row in cur:
                            strval = str(row[1])
                            row[0] = strval.replace('.0',"")
                            # Update rows
                            cur.updateRow(row)
                        del(row)
                    del(cur)
                if str(wtd_cur_fields[2]) in wtdfieldnames:
                    print (f'{wtd_cur_fields[2]} field already in dataset {wtd_merge}')
                    print(f'{"*"*100}')
                else:
                    print (f'Adding {wtd_cur_fields[2]} field to watershed dataset {wtd_merge}')
                    print(f'{"*"*100}')
                    # add cat_ID_con field and concat cat_ID + region
                    arcpy.AddField_management(wtd_merge, str(wtd_cur_fields[2]),field_type='TEXT')
                    # populate cat_ID_txt
                    with arcpy.da.UpdateCursor(wtd_merge, wtd_cur_fields) as cur:
                        for row in cur:
                            strval = str(row[1])
                            row[2] = str(roi) +'_'+ strval.replace(".0","")
                            # Update rows
                            cur.updateRow(row)
                        del(row)
                    del(cur)

            # Select glaciers fc
            elif 'glaciers' == filename:
                # Make local copy projected in AKAlbers
                glacpath = os.path.join(dirpath, filename)
                glacname = roi+'_'+filename
                glac_fc = glacpath

            # Select elevation raster
            elif 'elev.tif' == filename:
                elev_rast = os.path.join(dirpath, filename)

            # # Select aspect raster
            # elif 'aspect' in filename:
            #     asp_rast = os.path.join(dirpath, filename)

            # Select north raster
            elif 'north.tif' == filename:
                nor_rast = os.path.join(dirpath, filename)

            # Select slope raster
            elif 'slope.tif' == filename:
                slope_rast = os.path.join(dirpath, filename)

            # Select wetland raster
            elif 'wetlands.tif' == filename:
                wet_rast = os.path.join(dirpath, filename)

            # Select catch_int fc (catchments of interest for region) and make a copy
            elif 'awc_huc12_catchment_outlets' == filename:
                # Make local copy projected in AKAlbers
                catspath = os.path.join(dirpath,filename)
                catsname = roi +"_"+filename
                cats = catspath
                catlstfields = arcpy.ListFields(cats)
                catfieldnames = []
                for field in catlstfields:
                    catfieldnames.append(field.name)
                if str(cat_cur_fields[0]) in catfieldnames:
                    print (f'{cat_cur_fields[0]} field already in dataset {cats}')
                    print(f'{"*"*100}')
                else:
                    print (f'Adding {cat_cur_fields[0]} field to catchment dataset {cats}')
                    print(f'{"*"*100}')
                    # add cat_ID_txt field
                    arcpy.AddField_management(cats, str(cat_cur_fields[0]), field_type='TEXT')
                    # populate cat_ID_txt
                    with arcpy.da.UpdateCursor(cats, cat_cur_fields[0:2]) as cur:
                        for row in cur:
                            strval = str(row[1])
                            row[0] = strval.replace('.0',"")
                            # Update rows
                            cur.updateRow(row)
                        del(row)
                    del(cur)
                if str(cat_cur_fields[2]) in catfieldnames:
                    print (f'{cat_cur_fields[2]} field already in dataset {cats}')
                    print(f'{"*"*100}')
                else:
                    print (f'Adding {cat_cur_fields[2]} field to catchment dataset {cats}')
                    print(f'{"*"*100}')
                    # add cat_ID_txt field & cat_ID + region concat field
                    arcpy.AddField_management(cats,str(cat_cur_fields[2]),field_type='TEXT')
                    # populate cat_ID_con
                    with arcpy.da.UpdateCursor(cats, cat_cur_fields) as cur:
                        for row in cur:
                            strval = str(row[1])
                            row[2] = str(roi) +'_'+ strval.replace('.0',"")
                            # Update rows
                            cur.updateRow(row)
                        del(row)
                    del(cur)

    print (f'Calculating topographic metrics for catchments & watersheds of interest in {roi} region')
    print ('----------')
    print(f'Geodatabase: {outgdb}')
    print ('----------')
    print (f'Watershed Merge: {wtd_merge}')
    print (f'  Projection {arcpy.Describe(wtd_merge).spatialReference.name}')
    print ('----------')
    print (f'HUC12 Catchment Outlets: {cats}')
    print (f'  Projection {arcpy.Describe(cats).spatialReference.name}')
    print ('----------')
    print (f'Elevation Raster: {elev_rast}')
    print (f'  Projection: {arcpy.Describe(elev_rast).spatialReference.name}')
    print ('----------')
    print (f'North Aspect Raster: {nor_rast}')
    print (f'  Projection: {arcpy.Describe(nor_rast).spatialReference.name}')
    print ('----------')
    print (f'Wetlands Raster: {wet_rast}')
    print (f'  Projection {arcpy.Describe(wet_rast).spatialReference.name}')
    print ('----------')
    print (f'Slope Raster: {slope_rast}')
    print (f'  Projection {arcpy.Describe(slope_rast).spatialReference.name}')
    print ('----------')
    print (f'Lakes Ponds fc: {lakes_fc}')
    print (f'  Projection {arcpy.Describe(lakes_fc).spatialReference.name}')
    print ('----------')
    print (f'Glaciers fc: {glac_fc} ')
    print (f'  Projection {arcpy.Describe(glac_fc).spatialReference.name}')
    print ('----------')
    print (f'{arcpy.GetCount_management(wtd_merge)} Watersheds to process')
    print ('----------')
    print (f'Catchment intersect {cats} selected')
    print ('----------')

    # # Aspect variables
    # wtd_merge_asp_table_name = roi + "_AwcHuc12_wtd_mer_AspectZstats"
    # wtd_merge_asp_table_path = os.path.join(outgdb, wtd_merge_asp_table_name)
    # cat_asp_table_name = roi + "_AwcHuc12_cats_AspectZstats"
    # cat_asp_table_path = os.path.join(outgdb, cat_asp_table_name)

    # Percent North variables
    wtd_merge_pernorth_table_name = roi + "_AwcHuc12_wtd_mer_PerNorth"
    wtd_merge_pernorth_table_path = os.path.join(outgdb, wtd_merge_pernorth_table_name)
    # cat_pernorth_table_name = roi + "_AwcHuc12_cats_PercentNorth"
    # cat_pernorth_table_path = os.path.join(outgdb, cat_pernorth_table_name)

    # Elevation variables
    wtd_merge_elev_table_name = roi + "_AwcHuc12_wtd_mer_ElevZstats"
    wtd_merge_elev_table_path = os.path.join(outgdb, wtd_merge_elev_table_name)
    cat_elev_table_name = roi + "_AwcHuc12_cats_ElevZstats"
    cat_elev_table_path = os.path.join(outgdb, cat_elev_table_name)

    # Slope variables
    wtd_merge_slope_table_name = roi + "_AwcHuc12_wtd_mer_SlopeZstats"
    wtd_merge_slope_table_path = os.path.join(outgdb, wtd_merge_slope_table_name)
    cat_slope_table_name = roi + "_AwcHuc12_cats_SlopeZstats"
    cat_slope_table_path = os.path.join(outgdb, cat_slope_table_name)

    # Lakes Ponds variables
    wtd_merge_lp_table_name = roi + "_AwcHuc12_wtd_mer_PerLakes"
    wtd_merge_lp_table_path = os.path.join(outgdb, wtd_merge_lp_table_name)
    cat_lp_table_name = roi + "_AwcHuc12_cats_PerLakes"
    cat_lp_path = os.path.join(outgdb, cat_lp_table_name)

    # Wetlands variables
    wtd_merge_wetlands_table_name = roi + "_AwcHuc12_wtd_mer_PerWet"
    wtd_merge_wetlands_table_path = os.path.join(outgdb, wtd_merge_wetlands_table_name)
    cat_wetlands_table_name = roi + "AwcHuc12_cats_PerWet"
    cat_wetlands_table_path = os.path.join(outgdb, cat_wetlands_table_name)

    # Glaciers
    wtd_merge_glac_table_name = roi + "_AwcHuc12_wtd_mer_PerGlac"
    wtd_merge_glac_table_path = os.path.join(outgdb, wtd_merge_glac_table_name)
    cat_glac_table_name = roi + "_AwcHuc12_cats_Glaciers"
    cat_glac_table_path = os.path.join(outgdb, cat_glac_table_name)

    try: # Zonal Stats section
        print(f'Begin Slope zonal statistics min/mean/max std dev for watersheds and catchments in {roi}'
              f' region')
        # Statistics to run for watersheds - 'ALL' is not an option at this time as tool will fail with unknown error
        zstats = ['MIN_MAX_MEAN','STD']
        # Begin Zonal Stats
        zstat_start = time.time()
        zstat_start1 = time.time()

        # Watershed slope Zonal Statistics
        print(f'Calculating {roi} watershed slope zonal stats...')
        arcpy.env.snapRaster = slope_rast
        arcpy.env.cellSize = slope_rast

        # Create field mappings
        slope_fm = arcpy.FieldMap()
        slope_fms = arcpy.FieldMappings()
        for field in arcpy.ListFields(wtd_merge)[6:]:
            slope_fm = arcpy.FieldMap()
            slope_fm.addInputField(wtd_merge,field.name)
            slope_fm.mergeRule = 'First'
            # Set properties of the output name.
            f_name = slope_fm.outputField
            f_name.name = field.name
            f_name.aliasName = field.name
            slope_fm.outputField = f_name
            slope_fms.addFieldMap(slope_fm)

        # Make copy of watershed merge input as table to join stats fields
        wtd_slope_metrics_table = arcpy.TableToTable_conversion(wtd_merge,
                                                               outgdb,
                                                               wtd_merge_slope_table_name,
                                                               '',
                                                               slope_fms,
                                                               )
        # Add region identifier field for watershed tables                                                )
        arcpy.AddField_management(wtd_slope_metrics_table,'region',field_type='TEXT')
        arcpy.CalculateField_management(wtd_slope_metrics_table,'region',exp)

        for stat in zstats:
            outstattable = os.path.join(outgdb,f'{roi}_wtdSlope_{stat}')
            zstat_start1 = time.time()
            print (f'running {stat}')
            stat_table = ZonalStatisticsAsTable(in_zone_data = wtd_merge,
                                                zone_field = wtd_cur_fields[0],
                                                in_value_raster = slope_rast,
                                                out_table = outstattable,
                                                statistics_type=stat
                                                )

            stat_fields = [f.name for f in arcpy.ListFields(stat_table)]
            arcpy.JoinField_management(wtd_slope_metrics_table,
                                   wtd_cur_fields[0],
                                   stat_table,
                                   wtd_cur_fields[0],
                                   stat_fields[5:] # Keep only stat field/s
                                   )

            # Report time
            zstat_stop1 = time.time()
            zstat_time1 = int (zstat_stop1 - zstat_start1)
            print(f'Watershed Slope Zonal {stat} for {roi} complete.\nElapsed time: ({datetime.timedelta(seconds=zstat_time1)})')
            print(f'{"*"*100}')

        # Append watershed slope table to list
        wtd_slope_ztables.append(wtd_slope_metrics_table)


        # Elevation Zonal statistics  for watersheds
        print(f'Begin Elevation zonal statistics min/mean/max std dev for watersheds and catchments in {roi}'
              f' region')
        zstat_start2 = time.time()
        arcpy.env.snapRaster = elev_rast
        arcpy.env.cellSize = elev_rast

        # Create field mappings
        elev_fm = arcpy.FieldMap()
        elev_fms = arcpy.FieldMappings()
        for field in arcpy.ListFields(wtd_merge)[6:]:
            elev_fm = arcpy.FieldMap()
            elev_fm.addInputField(wtd_merge,field.name)
            elev_fm.mergeRule = 'First'
            # Set properties of the output name.
            f_name = elev_fm.outputField
            f_name.name = field.name
            f_name.aliasName = field.name
            elev_fm.outputField = f_name
            elev_fms.addFieldMap(elev_fm)

        # Make copy of watershed merge input as table to join stats fields
        wtd_elev_metrics_table = arcpy.TableToTable_conversion(wtd_merge,
                                                               outgdb,
                                                               wtd_merge_elev_table_name,
                                                               '',
                                                               elev_fms,
                                                               )
        # Add region identifier field for watershed tables                                                )
        arcpy.AddField_management(wtd_elev_metrics_table,'region',field_type='TEXT')
        arcpy.CalculateField_management(wtd_elev_metrics_table,'region',exp)

        for stat in zstats:
            outstattable = os.path.join(outgdb,f'{roi}_wtdElev_{stat}')
            zstat_start1 = time.time()
            print (f'running {stat}')
            stat_table = ZonalStatisticsAsTable(in_zone_data = wtd_merge,
                                                zone_field = wtd_cur_fields[0],
                                                in_value_raster = elev_rast,
                                                out_table = outstattable,
                                                statistics_type=stat
                                                )

            stat_fields = [f.name for f in arcpy.ListFields(stat_table)]
            arcpy.JoinField_management(wtd_elev_metrics_table,
                                   wtd_cur_fields[0],
                                   stat_table,
                                   wtd_cur_fields[0],
                                   stat_fields[5:] # Keep only stat field/s
                                   )

            # Report time
            zstat_stop2 = time.time()
            zstat_time2 = int (zstat_stop2 - zstat_start2)
            print(f'Watershed Elevation Zonal {stat} for {roi} complete.\nElapsed time: ({datetime.timedelta(seconds=zstat_time2)})')
            print(f'{"*"*100}')
        # Append watershed elev table to list
        wtd_elev_ztables.append(wtd_elev_metrics_table)


        # Elevation zonal statistics for catchments
        print(f'Calculating {roi} catchment elevation zonal stats...')
        zstat_start3 = time.time()
        arcpy.env.snapRaster = elev_rast
        arcpy.env.cellSize = elev_rast
        cat_elev_metrics_table = ZonalStatisticsAsTable(in_zone_data = cats ,
                                                        zone_field = cat_cur_fields[0],
                                                        in_value_raster = elev_rast,
                                                        out_table = cat_elev_table_path,
                                                        statistics_type='ALL'
                                                        )
        # Add region identifier field for catchment table
        arcpy.AddField_management(cat_elev_metrics_table,'region',field_type='TEXT')
        # Add cat_ID_Con field
        arcpy.AddField_management(cat_elev_metrics_table,'cat_ID_con',field_type='TEXT')

        # Update fields
        with arcpy.da.UpdateCursor(cat_elev_metrics_table,['region','cat_ID_txt','cat_ID_con']) as cur:
            for row in cur:
                row[0] = roi
                strval = str(row[1])
                row[2] = roi+"_"+strval.replace(".0","")
                # Update
                cur.updateRow(row)
            del(row)
        del(cur)
        # Append catchment elev table to list
        cat_elev_ztables.append(cat_elev_metrics_table)
        # Report time
        zstat_stop3 = time.time()
        zstat_time3 = int (zstat_stop3 - zstat_start3)
        print(f'Elevation Zonal Stats for {roi} catchments complete.\nElapsed time: ({datetime.timedelta(seconds=zstat_time3)})')
        print(f'{"*"*100}')

        # Slope zonal statistics for catchments
        zstat_start4 = time.time()
        print(f'Calculating {roi} catchment slope zonal stats...')
        arcpy.env.snapRaster = slope_rast
        arcpy.env.cellSize = slope_rast
        cat_slope_metrics_table = ZonalStatisticsAsTable(in_zone_data = cats ,
                                                        zone_field = cat_cur_fields[0],
                                                        in_value_raster = slope_rast,
                                                        out_table = cat_slope_table_path,
                                                        statistics_type='ALL'
                                                        )
        # Add region identifier field for catchment table
        arcpy.AddField_management(cat_slope_metrics_table,'region',field_type='TEXT')
        # Add cat_ID_Con field
        arcpy.AddField_management(cat_slope_metrics_table,'cat_ID_con',field_type='TEXT')

        # Update region field
        with arcpy.da.UpdateCursor(cat_slope_metrics_table,['region','cat_ID_txt','cat_ID_con']) as cur:
            for row in cur:
                row[0] = roi
                strval =str(row[1])
                row[2] = roi+"_"+strval.replace(".0","")
                # Update
                cur.updateRow(row)
            del(row)
        del(cur)
        # Append catchment slope table to list
        cat_slope_ztables.append(cat_slope_metrics_table)
        # Report time
        zstat_stop4 = time.time()
        zstat_time4 = int (zstat_stop4 - zstat_start4)
        print(f'Slope Zonal Stats for {roi} catchments complete.\nElapsed time: ({datetime.timedelta(seconds=zstat_time4)})')
        print(f'{"*"*100}')


        # # Aspect Zonal statistics  for watersheds
        # print(f'Calculating {roi} watershed aspect zonal stats...')
        # wtd_asp_metrics_table = ZonalStatisticsAsTable(in_zone_data = wtd_merge, zone_field ="cat_ID_txt",
        #                                                in_value_raster = asp_rast, out_table = wtd_merge_asp_table_path,
        #                                                statistics_type='ALL')
        # arcpy.AddField_management(wtd_asp_metrics_table, 'region', field_type='TEXT')
        # Add cat_ID_Con field
        # arcpy.AddField_management(wtd_asp_metrics_table,'cat_ID_con',field_type='TEXT')
        # arcpy.CalculateField_management(wtd_asp_metrics_table, 'region', 'roi')
        # Update region field
        # with arcpy.da.UpdateCursor(wtd_asp_metrics_table,['region','cat_ID_txt','cat_ID_con']) as cur:
        #     for row in cur:
        #         row[0] = roi
        #         strval = str(row[1])
        #         row[2] = roi+"_"+strval.replace(".0","")
        #         # Update
        #         cur.updateRow(row)
        #     del(row)
        # del(cur)
        # wtd_asp_ztables.append(wtd_asp_metrics_table)

        # # Aspect Zonal statistics for catchments
        # print(f'Calculating {roi} catchment aspect zonal stats...')
        # cat_asp_metrics_table = ZonalStatisticsAsTable(in_zone_data = cats, zone_field ="cat_ID_txt",
        #                                                in_value_raster = asp_rast, out_table = cat_asp_table_path,
        #                                                statistics_type='ALL')
        # arcpy.AddField_management(cat_asp_metrics_table, 'region', field_type='TEXT')
        # Add cat_ID_Con field
        # arcpy.AddField_management(cat_asp_metrics_table,'cat_ID_con',field_type='TEXT')
        # arcpy.CalculateField_management(cat_asp_metrics_table, 'region', 'roi')
        # Update region field
        # with arcpy.da.UpdateCursor(cat_asp_metrics_table,['region','cat_ID_txt','cat_ID_con']) as cur:
        #     for row in cur:
        #         strval = str(row[1])
        #         row[2] = roi+"_"+strval.replace(".0","")
        #         # Update
        #         cur.updateRow(row)
        #     del(row)
        # del(cur)
        # cat_asp_ztables.append(cat_asp_metrics_table)

        zstat_stop = time.time()
        zstat_time = int (zstat_stop - zstat_start)
        print(f'All Zonal Stats for {roi} Elapsed time: ({datetime.timedelta(seconds=zstat_time)})')
        print(f'{"*"*100}')

        # Tabulate Area with north grid and watersheds
        tabarea_start = time.time()
        tabarea_start1 = time.time()
        print(f'Begin tabulate area of north facing cells for watersheds and catchments in {roi} region')
        print(f'{"*"*100}')
        # Percent North Tabulate area for watersheds
        wtd_per_north_tabarea = arcpy.sa.TabulateArea(in_zone_data= wtd_merge,
                                                      zone_field= wtd_cur_fields[0],
                                                      in_class_data=nor_rast,
                                                      class_field="Value",
                                                      out_table = wtd_merge_pernorth_table_path
                                                      )
        # Add region and percent north fields
        arcpy.AlterField_management(wtd_per_north_tabarea,'CAT_ID_TXT','CAT_ID_TXT_DEL','CAT_ID_TXT_DEL')
        arcpy.AddField_management(wtd_per_north_tabarea, 'region', field_type='TEXT')
        arcpy.AddField_management(wtd_per_north_tabarea, 'AwcHuc12_wtd_north_per', field_type='Float')
        arcpy.AddField_management(wtd_per_north_tabarea, wtd_cur_fields[0], field_type='TEXT')
        arcpy.AddField_management(wtd_per_north_tabarea, wtd_cur_fields[2], field_type='TEXT')
        wtdnorfields = [f.name for f in arcpy.ListFields(wtd_per_north_tabarea)]
        #print (wtdnorfields)
        with arcpy.da.UpdateCursor(wtd_per_north_tabarea, wtdnorfields) as cur:
            for row in cur:
                strval = str(row[1])
                row[4] = roi
                row[5] = row[3]/(row[3]+row[2])*100
                row[6] = strval.replace('.0','')
                row[7] = roi +'_'+ strval.replace(".0","")
                # Update
                cur.updateRow(row)
            del(row)
        del(cur)
        # Drop UPPERCASE field form tab area
        arcpy.DeleteField_management(wtd_per_north_tabarea,'CAT_ID_TXT_DEL')
        # Append watershed percent north table to list
        wtd_pernorth_taba_tables.append(wtd_per_north_tabarea)
        # Report tab area times
        tabarea_stop1 = time.time()
        tabarea_time1 = int (tabarea_stop1 - tabarea_start1)
        print(f'Watershed percent north Tabulate area/intersections for {roi} complete.\nElapsed time: ({datetime.timedelta(seconds=tabarea_time1)})')
        print(f'{"*"*100}')

        # Percent Lakes Ponds using Tabulate Intersection for watersheds
        print(f'Begin watershed percent lakes ponds for {roi}')
        tabarea_start2 = time.time()
        wtd_lp_tabint = arcpy.TabulateIntersection_analysis(wtd_merge,
                                                            zone_fields=wtd_cur_fields[0],
                                                            in_class_features=lakes_fc,
                                                            out_table=wtd_merge_lp_table_path,
                                                            class_fields='Ftype',
                                                            out_units="SQUARE_METERS"
                                                            )
        # Add region and cat id fields
        arcpy.AlterField_management(wtd_lp_tabint,'PERCENTAGE','AwcHuc12_wtd_lake_per','AwcHuc12_wtd_lake_per')
        arcpy.AlterField_management(wtd_lp_tabint,'AREA','AwcHuc12_wtd_lake_area_sqm','AwcHuc12_wtd_lake_area_sqm')
        arcpy.AddField_management(wtd_lp_tabint, 'region', field_type='TEXT')
        arcpy.AddField_management(wtd_lp_tabint, wtd_cur_fields[1], field_type='TEXT')
        arcpy.AddField_management(wtd_lp_tabint, wtd_cur_fields[2], field_type='TEXT')
        wtdlpfields = [f.name for f in arcpy.ListFields(wtd_lp_tabint)]
        #print (wtdlpfields)
        with arcpy.da.UpdateCursor(wtd_lp_tabint, wtdlpfields) as cur:
            for row in cur:
                strval = str(row[1])
                row[5] = roi
                row[6] = strval.replace('.0','')
                row[7] = roi +'_'+ strval.replace(".0","")
                # Update
                cur.updateRow(row)
            del(row)
        del(cur)

        # Append watershed lakes ponds table to list
        wtd_lp_tabint_tables.append(wtd_lp_tabint)
        # Report tab area times
        tabarea_stop2 = time.time()
        tabarea_time2 = int (tabarea_stop2 - tabarea_start2)
        print(f'Percent Lakes Tabulate area/intersections for {roi} complete.\nElapsed time: ({datetime.timedelta(seconds=tabarea_time2)})')
        print(f'{"*"*100}')

        # Percent glaciers using Tabulate Intersection for watersheds
        tabarea_start3 = time.time()
        print(f'Begin tabulate intersection between {glac_fc} and watersheds in {roi} region')
        print(f'{"*"*100}')
        wtd_glac_tabint = arcpy.TabulateIntersection_analysis(wtd_merge,
                                                            zone_fields=wtd_cur_fields[0],
                                                            in_class_features=glac_fc,
                                                            out_table=wtd_merge_glac_table_path,
                                                            class_fields='O1Region',
                                                            out_units="SQUARE_METERS"
                                                            )
        # Add region and cat id fields
        arcpy.AlterField_management(wtd_glac_tabint,'PERCENTAGE','AwcHuc12_wtd_glacier_per','AwcHuc12_wtd_glacier_per')
        arcpy.AlterField_management(wtd_glac_tabint,'AREA','AwcHuc12_wtd_glacier_area_sqm','AwcHuc12_wtd_glacier_area_sqm')
        arcpy.AddField_management(wtd_glac_tabint, 'region', field_type='TEXT')
        arcpy.AddField_management(wtd_glac_tabint, wtd_cur_fields[1], field_type='TEXT')
        arcpy.AddField_management(wtd_glac_tabint, wtd_cur_fields[2], field_type='TEXT')
        wtdglacfields = [f.name for f in arcpy.ListFields(wtd_glac_tabint)]
        #print (wtdglacfields)
        with arcpy.da.UpdateCursor(wtd_glac_tabint, wtdglacfields) as cur:
            for row in cur:
                strval = str(row[1])
                row[5] = roi
                row[6] = strval.replace('.0','')
                row[7] = roi +'_'+ strval.replace(".0","")
                # Update
                cur.updateRow(row)
            del(row)
        del(cur)
        # Append watershed percent glacier table to list
        wtd_glac_tabint_tables.append(wtd_glac_tabint)
        # Report tab area times
        tabarea_stop3 = time.time()
        tabarea_time3 = int (tabarea_stop3 - tabarea_start3)
        print(f'Percent Glacier Tabulate area/intersections for {roi} complete.\nElapsed time: ({datetime.timedelta(seconds=tabarea_time3)})')
        print(f'{"*"*100}')

        # Tabulate Area with wetlands grid and watersheds
        tabarea_start4 = time.time()
        print(f'Begin tabulate intersection between {wet_rast} and watersheds in {roi} region')
        print(f'{"*"*100}')
        # Wetlands tabulate area for watersheds
        wtd_per_wet_tabarea = arcpy.sa.TabulateArea(in_zone_data= wtd_merge,
                                                      zone_field= wtd_cur_fields[0],
                                                      in_class_data=wet_rast,
                                                      class_field="Value",
                                                      out_table=wtd_merge_wetlands_table_path
                                                      )
        # Add region and percent wet fields
        arcpy.AlterField_management(wtd_per_wet_tabarea,'CAT_ID_TXT','CAT_ID_TXT_DEL','CAT_ID_TXT_DEL')
        arcpy.AddField_management(wtd_per_wet_tabarea, 'region', field_type='TEXT')
        arcpy.AddField_management(wtd_per_wet_tabarea, 'AwcHuc12_wtd_wet_per', field_type='Float')
        arcpy.AddField_management(wtd_per_wet_tabarea, wtd_cur_fields[0], field_type='TEXT')
        arcpy.AddField_management(wtd_per_wet_tabarea, wtd_cur_fields[2], field_type='TEXT')
        wtdwetfields = [f.name for f in arcpy.ListFields(wtd_per_wet_tabarea)]
        #print (wtdwetfields)
        with arcpy.da.UpdateCursor(wtd_per_wet_tabarea, wtdwetfields) as cur:
            for row in cur:
                strval = str(row[1])
                row[4] = roi
                row[5] = row[3]/(row[3]+row[2])*100
                row[6] = strval.replace('.0','')
                row[7] = roi +'_'+ strval.replace(".0","")
                # Update
                cur.updateRow(row)
            del(row)
        del(cur)
        # Drop UPPERCASE field form tab area
        arcpy.DeleteField_management(wtd_per_wet_tabarea,'CAT_ID_TXT_DEL')
        # Append watershed percent wetlands table to list
        wtd_wet_taba_tables.append(wtd_per_wet_tabarea)
        # Report tab area times
        tabarea_stop4 = time.time()
        tabarea_time4 = int (tabarea_stop4 - tabarea_start4)
        print(f'Percent Wetlands Tabulate area/intersections for {roi} complete.\nElapsed time: ({datetime.timedelta(seconds=tabarea_time4)})')
        print(f'{"*"*100}')

        # # Percent North Tabulate Area for catchments
        # cat_per_north_tabarea = arcpy.sa.TabulateArea(in_zone_data= cats, zone_field='cat_ID_con',
        #                                             in_class_data=nor_rast,"Value",
        #                                             out_table=cat_pernorth_table_path)

        # # Add and calculate region identifier field for catchment table
        # arcpy.AlterField_management(cat_per_north_tabarea,'CAT_ID_TXT','CAT_ID_TXT_DEL','CAT_ID_TXT_DEL')
        # arcpy.AddField_management(cat_per_north_tabarea, 'region', field_type='TEXT')
        # arcpy.AddField_management(cat_per_north_tabarea, 'cat_north_per', field_type='Float')
        # arcpy.AddField_management(cat_per_north_tabarea, cat_cur_fields[0], field_type='TEXT')
        # arcpy.AddField_management(cat_per_north_tabarea, cat_cur_fields[2], field_type='TEXT')
        # catnorfields = [f.name for f in arcpy.ListFields(cat_per_north_tabarea)]
        # print (catnorfields)
        # with arcpy.da.UpdateCursor(cat_per_north_tabarea,catnorfields) as cur:
        #     for row in cur:
        #         strval = str(row[1])
        #         row[4] = roi
        #         row[5] = row[3]/(row[3]+row[2])*100
        #         row[6] = strval.replace('.0','')
        #         row[7] = roi +'_'+ strval.replace(".0","")
        #         # Update
        #         cur.updateRow(row)
        #     del(row)
        # del(cur)
        # Drop UPPERCASE field form tab area
        # arcpy.DeleteField_management(cat_per_north_tabarea,'CAT_ID_TXT_DEL')
        # # Append catchment percent north table to list
        # cat_pernorth_taba_tables.append(cat_per_north_tabarea)
        # Report tab area times
        tabarea_stop = time.time()
        tabarea_time = int (tabarea_stop - tabarea_start)
        print(f'Tabulate area/intersections for {roi} complete\nElapsed time: ({datetime.timedelta(seconds=tabarea_time)})')
        print(f'{"*"*100}')

        # Begin LCLD calculations
        walk = arcpy.da.Walk(lcld_folder, datatype='RasterDataset')
        for dirpath, dirnames, filenames in walk:
            for filename in filenames:
                raspath = os.path.join(dirpath, filename)
                year = filename[0:4]
                lcld_outname = roi+'_AwcHuc12_lcld_'+str(year)+'_zStats'
                lcld_outpath = os.path.join(outgdb, lcld_outname)
                print(f'Year: {year} - raster path {raspath}')
                colname = 'AwcHuc12_wtd_lcld_mn_' + str(year)
                # lcld zonal statistics as table for all akssf watersheds
                print(f'Calculating {filename} zonal stats for all {roi} watersheds...')
                #arcpy.env.snapRaster = raspath
                #arcpy.env.cellSize = raspath

                # Begin Zonal Stats
                lcldzstat_start = time.time()
                print(f'Begin zonal stats for {filename}')
                lcld_table = ZonalStatisticsAsTable(in_zone_data = wtd_merge,
                                                                zone_field = 'cat_ID_con',
                                                                in_value_raster = raspath,
                                                                out_table = lcld_outpath,
                                                                statistics_type='MEAN'
                                                                )
                # Append zTable to table list
                lcld_Ztables.append(lcld_outpath)
                arcpy.AlterField_management(lcld_table,'MEAN', colname,colname)
                proc_list = [row[0] for row in arcpy.da.SearchCursor(lcld_table,'cat_ID_con')]
                lcldzstat_stop = time.time()
                lcldzstat_time = int (lcldzstat_stop - lcldzstat_start)
                print(f'Zonal Stats for {filename} - Elapsed time: ({datetime.timedelta(seconds=lcldzstat_time)})')


    except:
        e = sys.exc_info()[1]
        print(f'ERRFLAG!!! = {e.args[0]}')
        arcpy.AddError(e.args[0])

    iter_stop = time.time()
    iter_time = int(iter_stop - iteration_start)
    print(f'All Covariates for {roi} completed.\nElapsed time: ({datetime.timedelta(seconds=iter_time)})')
    print(f'{"*"*100}')

# End timing
processEnd = time.time()
processElapsed = int(processEnd - processStart)
processSuccess_time = datetime.datetime.now()

# Report success
print(f'Process completed at {processSuccess_time.strftime("%Y-%m-%d %H:%M")} '
      f'(Elapsed time: {datetime.timedelta(seconds=processElapsed)})')
print(f'{"*"*100}')


Bristol_Bay in ['Bristol_Bay', 'Kodiak', 'Prince_William_Sound'] TauDEM list, using cat_fields ['cat_ID_txt', 'catID', 'cat_ID_con'] and watershed fields ['cat_ID_txt', 'cat_ID', 'cat_ID_con']
****************************************************************************************************
Adding cat_ID_txt field to catchment dataset D:\GIS\AKSSF\Bristol_Bay\Bristol_Bay.gdb\awc_huc12_catchment_outlets
****************************************************************************************************
Adding cat_ID_con field to catchment dataset D:\GIS\AKSSF\Bristol_Bay\Bristol_Bay.gdb\awc_huc12_catchment_outlets
****************************************************************************************************
Merged watershed dataset awc_huc12_wtds_merge found
****************************************************************************************************
cat_ID_txt field already in dataset
***************************************************************************************

## Examine LCLD tables and merge/export
* Discovered one watershed for PWS (Prince_William_Sound_23854) only has 6 years of LCLD data attributed to it.  Modis Coverage along the Coastline and PWS in particular is poor and many of the Islands/Coastlines have limited coverage.

In [20]:
arcpy.env.workspace = outgdb
lcld_Ztables = [t for t in arcpy.ListTables('*_lcld_*')]
from collections import OrderedDict
lcld_Dict = {}
dfs = []
lcld_cols = []
drop_cols = ['OBJECTID','ZONE_CODE', 'AREA', 'COUNT']
for table in lcld_Ztables:
    cols = [f.name for f in arcpy.ListFields(table)]
    search_cols = [x for x in cols if x not in drop_cols]
    #cols.remove(drop_cols)
    print(search_cols)
    lcld_cols.append(search_cols)
    tblname = table[-16:]
    print(tblname)
    with arcpy.da.SearchCursor(table, search_cols) as cur:
        for row in cur:

            append_value(lcld_Dict,row[0],row[1])

lcld_cols = [item for sublist in lcld_cols for item in sublist]
lcld_cols = list(OrderedDict.fromkeys(lcld_cols))
print(lcld_cols)

#Create list of tuples containing unique id followed by mean lcld for years 2001-2019
row_values = [(k,)+tuple(v) for k,v in lcld_Dict.items()]

['cat_ID_con', 'AwcHuc12_wtd_lcld_mn_2001']
lcld_2001_zStats
['cat_ID_con', 'AwcHuc12_wtd_lcld_mn_2002']
lcld_2002_zStats
['cat_ID_con', 'AwcHuc12_wtd_lcld_mn_2003']
lcld_2003_zStats
['cat_ID_con', 'AwcHuc12_wtd_lcld_mn_2004']
lcld_2004_zStats
['cat_ID_con', 'AwcHuc12_wtd_lcld_mn_2005']
lcld_2005_zStats
['cat_ID_con', 'AwcHuc12_wtd_lcld_mn_2006']
lcld_2006_zStats
['cat_ID_con', 'AwcHuc12_wtd_lcld_mn_2007']
lcld_2007_zStats
['cat_ID_con', 'AwcHuc12_wtd_lcld_mn_2008']
lcld_2008_zStats
['cat_ID_con', 'AwcHuc12_wtd_lcld_mn_2009']
lcld_2009_zStats
['cat_ID_con', 'AwcHuc12_wtd_lcld_mn_2010']
lcld_2010_zStats
['cat_ID_con', 'AwcHuc12_wtd_lcld_mn_2011']
lcld_2011_zStats
['cat_ID_con', 'AwcHuc12_wtd_lcld_mn_2012']
lcld_2012_zStats
['cat_ID_con', 'AwcHuc12_wtd_lcld_mn_2013']
lcld_2013_zStats
['cat_ID_con', 'AwcHuc12_wtd_lcld_mn_2014']
lcld_2014_zStats
['cat_ID_con', 'AwcHuc12_wtd_lcld_mn_2015']
lcld_2015_zStats
['cat_ID_con', 'AwcHuc12_wtd_lcld_mn_2016']
lcld_2016_zStats
['cat_ID_con', 'AwcHuc12

Create an empty table to append yearly data
 * Attempting to convert to df and numpy arrays has been unsuccessful

In [21]:
lcld_table = arcpy.CreateTable_management(outgdb,'AKSSF_awcHuc12_ALL_LCLD_mn')
arcpy.AddField_management(lcld_table.getOutput(0),lcld_cols[0],'TEXT')
cur = arcpy.da.InsertCursor(lcld_table.getOutput(0),lcld_cols[0])
# Populate table with cat_ID_con values stored in list of lcld tuples
try:
    for row in row_values:
        cur.insertRow([row[0]])
        del(row)
    del(cur)
except:
    e = sys.exc_info()[1]
    print(f'ERRFLAG!!! = {e.args[0]}\n')
    # Get the traceback object
    tb = sys.exc_info()[2]
    tbinfo = traceback.format_tb(tb)[0]
    # Concatenate information together concerning the error into a message string
    pymsg = "PYTHON ERRORS:\nTraceback info:\n" + tbinfo + "\nError Info:\n" + str(sys.exc_info()[1])
    msgs = "ArcPy ERRORS:\n" + arcpy.GetMessages(2) + "\n"
    # Return Python error messages for use in script tool or Python window
    arcpy.AddError(pymsg)
    arcpy.AddError(msgs)
    # Print Python error messages for use in Python / Python window
    print(pymsg)
    print(msgs)
    arcpy.AddError(e.args[0])
print(f'LCDL table has {arcpy.GetCount_management(lcld_table)} records of {len(row_values)} input rows')

LCDL table has 738 records of 738 input rows


In [22]:

years = [x for x in range(2001,2020)]
lcldyr_Dict = {}
for y in years:
    for table in lcld_Ztables:
        if str(y) in table:
            append_value(lcldyr_Dict,str(y),table)
#print(lcldyr_Dict)

for k, v in lcldyr_Dict.items():
    year = k
    intables = v
    print (f'{year} using tables {intables} with val {v}\n')
    tempTable = arcpy.Merge_management(v,f'memory\\tempTable')
    infields = [f.name for f in arcpy.ListFields(tempTable)]
    print(f'Joining field {infields[5]} from {tempTable} to {lcld_table}')
    print(f'{"*"*100}\n')
    arcpy.JoinField_management(lcld_table,lcld_cols[0],tempTable,lcld_cols[0],infields[5])

2001 using tables ['Bristol_Bay_AwcHuc12_lcld_2001_zStats', 'Kodiak_AwcHuc12_lcld_2001_zStats'] with val ['Bristol_Bay_AwcHuc12_lcld_2001_zStats', 'Kodiak_AwcHuc12_lcld_2001_zStats']

Joining field AwcHuc12_wtd_lcld_mn_2001 from memory\tempTable to D:\GIS\outputs_2023\outputs_2023.gdb\AKSSF_awcHuc12_ALL_LCLD_mn
****************************************************************************************************

2002 using tables ['Bristol_Bay_AwcHuc12_lcld_2002_zStats', 'Kodiak_AwcHuc12_lcld_2002_zStats'] with val ['Bristol_Bay_AwcHuc12_lcld_2002_zStats', 'Kodiak_AwcHuc12_lcld_2002_zStats']

Joining field AwcHuc12_wtd_lcld_mn_2002 from memory\tempTable to D:\GIS\outputs_2023\outputs_2023.gdb\AKSSF_awcHuc12_ALL_LCLD_mn
****************************************************************************************************

2003 using tables ['Bristol_Bay_AwcHuc12_lcld_2003_zStats', 'Kodiak_AwcHuc12_lcld_2003_zStats'] with val ['Bristol_Bay_AwcHuc12_lcld_2003_zStats', 'Kodiak_AwcHuc12_lcld_2

In [23]:
# Convert to df and examine
# Make catchment lcld df
lcld_df = pd.DataFrame()
lcld_field_list = []
for field in arcpy.ListFields(lcld_table):
    lcld_field_list.append(field.name)
lcld_arr = arcpy.da.TableToNumPyArray(lcld_table,lcld_field_list)
lcld_df = pd.DataFrame(lcld_arr)
#lcld_df = lcld_df.drop(["OBJECTID","AwcHuc12_cat_elev_ZONE_CODE"],axis=1)
lcld_df = lcld_df.set_index('cat_ID_con')
#dfs.append(lcld_df)
lcld_df


OBJECTID  AwcHuc12_wtd_lcld_mn_2001  \
cat_ID_con                                                 
Bristol_Bay_1003859         1                 498.455807   
Bristol_Bay_1004129         2                 502.010116   
Bristol_Bay_1006858         3                 495.354769   
Bristol_Bay_1007408         4                 474.249194   
Bristol_Bay_1008168         5                 475.257172   
Bristol_Bay_1008527         6                 492.340235   
Bristol_Bay_1008597         7                 458.097105   
Bristol_Bay_1013001         8                 426.836520   
Bristol_Bay_1013111         9                 417.809235   
Bristol_Bay_1013306        10                 446.836640   
Bristol_Bay_1013765        11                 468.245079   
Bristol_Bay_1014251        12                 428.934352   
Bristol_Bay_1014341        13                 463.903521   
Bristol_Bay_1014516        14                 458.398097   
Bristol_Bay_1014641        15                 413.475299   
Bristol_Bay_1014786        16                 431.167366   
Bristol_Bay_1014821        17                 481.083656   
Bristol_Bay_1015186        18                 492.303775   
Bristol_Bay_1015281        19                 475.355691   
Bristol_Bay_1015516        20                 481.522403   
Bristol_Bay_1015685        21                 498.386584   
Bristol_Bay_1015771        22                 462.998699   
Bristol_Bay_1015821        23                 458.416158   
Bristol_Bay_1016325        24                 502.928045   
Bristol_Bay_1016515        25                 478.751408   
Bristol_Bay_1016825        26                 447.442045   
Bristol_Bay_1021823        27                 414.523728   
Bristol_Bay_1021914        28                 518.995709   
Bristol_Bay_1021984        29                 432.043196   
Bristol_Bay_1022284        30                 429.681798   
Bristol_Bay_1023034        31                 470.377071   
Bristol_Bay_1024403        32                 497.388059   
Bristol_Bay_1025113        33                 507.252904   
Bristol_Bay_1025432        34                 428.857623   
Bristol_Bay_1025533        35                 488.258449   
Bristol_Bay_1025683        36                 508.095647   
Bristol_Bay_1025783        37                 433.526570   
Bristol_Bay_1026233        38                 417.388678   
Bristol_Bay_1026463        39                 428.329983   
Bristol_Bay_1026613        40                 505.521983   
Bristol_Bay_1026983        41                 459.720617   
Bristol_Bay_1027852        42                 430.438721   
Bristol_Bay_1028122        43                 433.802136   
Bristol_Bay_1028212        44                 510.128934   
Bristol_Bay_1028322        45                 496.323281   
Bristol_Bay_1029732        46                 509.646140   
Bristol_Bay_1029872        47                 476.326014   
Bristol_Bay_1030062        48                 432.332817   
Bristol_Bay_1030462        49                 417.794413   
Bristol_Bay_1030642        50                 423.511440   
Bristol_Bay_1031022        51                 489.357250   
Bristol_Bay_2019230        52                 559.948210   
Bristol_Bay_2019750        53                 557.672064   
Bristol_Bay_2020120        54                 553.604577   
Bristol_Bay_2040601        55                 549.306255   
Bristol_Bay_2041261        56                 545.492641   
Bristol_Bay_2042341        57                 537.392748   
Bristol_Bay_2059915        58                 464.926872   
Bristol_Bay_2060975        59                 461.988276   
Bristol_Bay_2061205        60                 477.024447   
Bristol_Bay_2061325        61                 469.178089   
Bristol_Bay_2063167        62                 482.815156   
Bristol_Bay_2063257        63                 530.224999   
Bristol_Bay_2064245        64                 494.766317   
Bristol_Bay_2064385        65                 457.497483   
B

In [27]:
# Export LCLD table
arcpy.TableToTable_conversion(lcld_table,outdir,'AKSSF_awcHuc12_wtd_lcld_mn.csv')
print(f'Table exported...{outdir}')


Table exported...D:\GIS\outputs_2023


## Drop unnecessary fields and rename as needed from merged tables.
- Create Key value dictionary and use update cursor to rename fields.

In [28]:

# Input table names/paths
cat_elev_ztables = [t for t in arcpy.ListTables('*_AwcHuc12_cats_ElevZstats')]
cat_slope_ztables = [t for t in arcpy.ListTables('*_AwcHuc12_cats_SlopeZstats')]
wtd_elev_ztables = [t for t in arcpy.ListTables('*_AwcHuc12_wtd_mer_ElevZstats')]
wtd_slope_ztables = [t for t in arcpy.ListTables('*_AwcHuc12_wtd_mer_SlopeZstats')]
wtd_pernorth_taba_tables = [t for t in arcpy.ListTables('*_AwcHuc12_wtd_mer_PerNorth')]
wtd_wet_taba_tables = [t for t in arcpy.ListTables('*_AwcHuc12_wtd_mer_PerWet')]
wtd_glac_tabint_tables = [t for t in arcpy.ListTables('*_AwcHuc12_wtd_mer_PerGlac')]
wtd_lp_tabint_tables = [t for t in arcpy.ListTables('*_AwcHuc12_wtd_mer_PerLakes')]

# Output Table names/paths
wtd_per_north_table_out = os.path.join(outgdb, 'AKSSF_awchuc12_wtd_north_per')
cat_elev_table_out = os.path.join(outgdb,'AKSSF_awchuc12_cat_elev')
cat_slope_table_out = os.path.join(outgdb,'AKSSF_awchuc12_cat_slope')
wtd_elev_table_out = os.path.join(outgdb, 'AKSSF_awchuc12_wtd_elev')
wtd_per_glac_table_out = os.path.join(outgdb, 'AKSSF_awchuc12_wtd_glacier_per')
wtd_per_lp_table_out = os.path.join(outgdb, 'AKSSF_awchuc12_wtd_lakepond_per')
wtd_slope_table_out = os.path.join(outgdb, 'AKSSF_awchuc12_wtd_slope')
wtd_wet_table_out = os.path.join(outgdb, 'AKSSF_awchuc12_wtd_wetland_per')

# Merge all regional tables together
outtables = []
wtd_per_north = arcpy.Merge_management(wtd_pernorth_taba_tables, wtd_per_north_table_out)
arcpy.AlterField_management(wtd_per_north,"VALUE_0","AwcHuc12_non_north_area","AwcHuc12_non_north_area")
arcpy.AlterField_management(wtd_per_north,"VALUE_1","AwcHuc12_north_area","AwcHuc12_north_area")
outtables.append(wtd_per_north)
cat_elev = arcpy.Merge_management(cat_elev_ztables, cat_elev_table_out)
outtables.append(cat_elev)
wtd_elev = arcpy.Merge_management(wtd_elev_ztables, wtd_elev_table_out)
outtables.append(wtd_elev)
wtd_slope = arcpy.Merge_management(wtd_slope_ztables, wtd_slope_table_out)
outtables.append(wtd_slope)
cat_slope = arcpy.Merge_management(cat_slope_ztables, cat_slope_table_out)
outtables.append(cat_slope)
wtd_wet = arcpy.Merge_management(wtd_wet_taba_tables, wtd_wet_table_out)
arcpy.AlterField_management(wtd_wet,"VALUE_0","AwcHuc12_non_wetland_area","AwcHuc12_non_wetland_area")
arcpy.AlterField_management(wtd_wet,"VALUE_1","AwcHuc12_wetland_area","AwcHuc12_wetland_area")
outtables.append(wtd_wet)
wtd_glac = arcpy.Merge_management(wtd_glac_tabint_tables, wtd_per_glac_table_out)
outtables.append(wtd_glac)
wtd_lp = arcpy.Merge_management(wtd_lp_tabint_tables, wtd_per_lp_table_out)
outtables.append(wtd_lp)
print ('Tables merged')
print('----------')


Tables merged
----------


In [29]:
#Set up field dictionary
elevDict = { 'ZONE_CODE': ('AwcHuc12_cat_elev_ZONE_CODE', 'AwcHuc12_wtd_elev_ZONE_CODE'),
         'COUNT': ('AwcHuc12_cat_elev_COUNT', 'AwcHuc12_wtd_elev_COUNT'),
          'AREA': ('AwcHuc12_cat_elev_AREA', 'AwcHuc12_wtd_elev_AREA'),
          'MIN': ('AwcHuc12_cat_elev_MIN', 'AwcHuc12_wtd_elev_MIN'),
          'MAX': ('AwcHuc12_cat_elev_MAX', 'AwcHuc12_wtd_elev_MAX'),
          'RANGE': ('AwcHuc12_cat_elev_RANGE', 'AwcHuc12_wtd_elev_RANGE'),
          'MEAN': ('AwcHuc12_cat_elev_MEAN', 'AwcHuc12_wtd_elev_MEAN'),
          'STD': ('AwcHuc12_cat_elev_STD', 'AwcHuc12_wtd_elev_STD'),
          'SUM': ('AwcHuc12_cat_elev_SUM', 'AwcHuc12_wtd_elev_SUM'),
          'VARIETY': ('AwcHuc12_cat_elev_VARIETY', 'AwcHuc12_wtd_elev_VARIETY'),
          'MAJORITY': ('AwcHuc12_cat_elev_MAJORITY', 'AwcHuc12_wtd_elev_MAJORITY'),
          'MINORITY': ('AwcHuc12_cat_elev_MINORITY', 'AwcHuc12_wtd_elev_MINORITY'),
          'MEDIAN': ('AwcHuc12_cat_elev_MEDIAN', 'AwcHuc12_wtd_elev_MEDIAN'),
          'PCT90': ('AwcHuc12_cat_elev_PCT90', 'AwcHuc12_wtd_elev_PCT90')
         }

slopeDict = { 'ZONE_CODE': ('AwcHuc12_cat_slope_ZONE_CODE', 'AwcHuc12_wtd_slope_ZONE_CODE'),
         'COUNT': ('AwcHuc12_cat_slope_COUNT', 'AwcHuc12_wtd_slope_COUNT'),
          'AREA': ('AwcHuc12_cat_slope_AREA', 'AwcHuc12_wtd_slope_AREA'),
          'MIN': ('AwcHuc12_cat_slope_MIN', 'AwcHuc12_wtd_slope_MIN'),
          'MAX': ('AwcHuc12_cat_slope_MAX', 'AwcHuc12_wtd_slope_MAX'),
          'RANGE': ('AwcHuc12_cat_slope_RANGE', 'AwcHuc12_wtd_slope_RANGE'),
          'MEAN': ('AwcHuc12_cat_slope_MEAN', 'AwcHuc12_wtd_slope_MEAN'),
          'STD': ('AwcHuc12_cat_slope_STD', 'AwcHuc12_wtd_slope_STD'),
          'SUM': ('AwcHuc12_cat_slope_SUM', 'AwcHuc12_wtd_slope_SUM'),
          'VARIETY': ('AwcHuc12_cat_slope_VARIETY', 'AwcHuc12_wtd_slope_VARIETY'),
          'MAJORITY': ('AwcHuc12_cat_slope_MAJORITY', 'AwcHuc12_wtd_slope_MAJORITY'),
          'MINORITY': ('AwcHuc12_cat_slope_MINORITY', 'AwcHuc12_wtd_slope_MINORITY'),
          'MEDIAN': ('AwcHuc12_cat_slope_MEDIAN', 'AwcHuc12_wtd_slope_MEDIAN'),
          'PCT90': ('AwcHuc12_cat_slope_PCT90', 'AwcHuc12_wtd_slope_PCT90')
         }

# Rename fields for elevation tables
for field in arcpy.ListFields(wtd_elev):
    keyval = field.name
    if keyval in elevDict:
        newname = elevDict[keyval][1]
        newalias = elevDict[keyval][1]
        print (keyval, newname)
        arcpy.AlterField_management(wtd_elev, keyval, newname, newalias)

for field in arcpy.ListFields(cat_elev):
    keyval = field.name
    if keyval in elevDict:
        newname = elevDict[keyval][0]
        newalias = elevDict[keyval][0]
        print (keyval, newname)
        arcpy.AlterField_management(cat_elev, keyval, newname, newalias)

# Rename fields for slope tables
for field in arcpy.ListFields(wtd_slope):
    keyval = field.name
    if keyval in slopeDict:
        newname = slopeDict[keyval][1]
        newalias = slopeDict[keyval][1]
        print (keyval, newname)
        arcpy.AlterField_management(wtd_slope, keyval, newname, newalias)

for field in arcpy.ListFields(cat_slope):
    keyval = field.name
    if keyval in slopeDict:
        newname = slopeDict[keyval][0]
        newalias = slopeDict[keyval][0]
        print (keyval, newname)
        arcpy.AlterField_management(cat_slope, keyval, newname, newalias)

MIN AwcHuc12_wtd_elev_MIN
MAX AwcHuc12_wtd_elev_MAX
MEAN AwcHuc12_wtd_elev_MEAN
STD AwcHuc12_wtd_elev_STD
ZONE_CODE AwcHuc12_cat_elev_ZONE_CODE
COUNT AwcHuc12_cat_elev_COUNT
AREA AwcHuc12_cat_elev_AREA
MIN AwcHuc12_cat_elev_MIN
MAX AwcHuc12_cat_elev_MAX
RANGE AwcHuc12_cat_elev_RANGE
MEAN AwcHuc12_cat_elev_MEAN
STD AwcHuc12_cat_elev_STD
SUM AwcHuc12_cat_elev_SUM
VARIETY AwcHuc12_cat_elev_VARIETY
MAJORITY AwcHuc12_cat_elev_MAJORITY
MINORITY AwcHuc12_cat_elev_MINORITY
MEDIAN AwcHuc12_cat_elev_MEDIAN
PCT90 AwcHuc12_cat_elev_PCT90
MIN AwcHuc12_wtd_slope_MIN
MAX AwcHuc12_wtd_slope_MAX
MEAN AwcHuc12_wtd_slope_MEAN
STD AwcHuc12_wtd_slope_STD
ZONE_CODE AwcHuc12_cat_slope_ZONE_CODE
COUNT AwcHuc12_cat_slope_COUNT
AREA AwcHuc12_cat_slope_AREA
MIN AwcHuc12_cat_slope_MIN
MAX AwcHuc12_cat_slope_MAX
RANGE AwcHuc12_cat_slope_RANGE
MEAN AwcHuc12_cat_slope_MEAN
STD AwcHuc12_cat_slope_STD
SUM AwcHuc12_cat_slope_SUM
MEDIAN AwcHuc12_cat_slope_MEDIAN
PCT90 AwcHuc12_cat_slope_PCT90


### Create HUC12 fc for mapping and display purposes and add cat_ID_con to relate back to watersheds.

In [55]:
import arcpy, os
NHDPlusHUCS = os.path.join(outgdb,r'NHDPlusHUC12')
NHD_H_Hucs = os.path.join(outgdb,'NHD_H_HUC12')
nhd_hList = []
nhdPlusList = []
HUC12s2pointsDict = {}
sites  = os.path.join(outgdb,r'AKSSF_awcHuc12_outlet_cats_points')
with arcpy.da.SearchCursor(sites, ['cat_ID_con','HUC12']) as cur:
    for row in cur:
        regionname = row[0].rsplit('_', 1)[0]
        if regionname in nhdplus_dat:
            nhdPlusList.append(row[1])
        elif regionname in tauDem_dat:
            nhd_hList.append(row[1])
        #print(regionname)
        append_value(HUC12s2pointsDict,row[1],[row[0],regionname])
print(len(HUC12s2pointsDict))
HUC12s2pointsDict

1596


{'190202020501': ['Cook_Inlet_75004200000901', 'Cook_Inlet'],
 '190202020503': ['Cook_Inlet_75004200001724', 'Cook_Inlet'],
 '190202020705': ['Cook_Inlet_75004200000437', 'Cook_Inlet'],
 '190202020303': ['Cook_Inlet_75004200001493', 'Cook_Inlet'],
 '190202020511': ['Cook_Inlet_75004200009084', 'Cook_Inlet'],
 '190202021002': ['Cook_Inlet_75004200003619', 'Cook_Inlet'],
 '190202021003': ['Cook_Inlet_75004200001047', 'Cook_Inlet'],
 '190202020602': ['Cook_Inlet_75004200016346', 'Cook_Inlet'],
 '190202021201': ['Cook_Inlet_75004200010717', 'Cook_Inlet'],
 '190202021004': ['Cook_Inlet_75004200010096', 'Cook_Inlet'],
 '190202021103': ['Cook_Inlet_75004200003399', 'Cook_Inlet'],
 '190202020403': ['Cook_Inlet_75004200000722', 'Cook_Inlet'],
 '190202020101': ['Cook_Inlet_75004200000726', 'Cook_Inlet'],
 '190202021001': ['Cook_Inlet_75004200012986', 'Cook_Inlet'],
 '190202021303': ['Cook_Inlet_75004200008847', 'Cook_Inlet'],
 '190202021404': ['Cook_Inlet_75004200010465', 'Cook_Inlet'],
 '190202

In [63]:

HUC12s2pointsDict['190207010604']


['Kodiak_129805', 'Kodiak']

## Select and Merge

In [64]:
# Select HUCS from respective datasets using appropriate lists
arcpy.env.overwriteOutput = True
field = 'HUC12'
operator = 'IN'
nhdPlusvalue = str(nhdPlusList).strip("[]")
nhdHvalue = str(nhd_hList).strip("[]")
nhdplussba = """"{}" {} ({})""".format(field, operator, nhdPlusvalue)
nhdhsba = """"{}" {} ({})""".format(field, operator, nhdHvalue)

# Make Selections using lists
nhdplus_select = arcpy.SelectLayerByAttribute_management(NHDPlusHUCS,'NEW_SELECTION', nhdplussba)
nhd_h_select = arcpy.SelectLayerByAttribute_management(NHD_H_Hucs,'NEW_SELECTION', nhdhsba)

print(f'Hucs in NHDPlusList = {len(nhdPlusList)}\nHucs in NHD_H_List = {len(nhd_hList)}\nTotal Hucs in lists = {len(nhd_hList) + len(nhdPlusList)}')
print (f'Total hucs selected for merge  = {int(arcpy.GetCount_management(nhdplus_select)[0]) + int(arcpy.GetCount_management(nhd_h_select)[0])}')

outHucname = "AKSSF_awcHuc12s"
outhucpath = os.path.join(outgdb,outHucname)
#Merge HUCS
arcpy.Merge_management([nhdplus_select,nhd_h_select],outhucpath,'','ADD_SOURCE_INFO')
arcpy.AddField_management(outhucpath,'cat_ID_con','TEXT')
arcpy.AddField_management(outhucpath,'region','TEXT')
print('Merge Complete')

# Use update cursor to add cat_ID_con to merged Hucs from value dictionary
with arcpy.da.UpdateCursor(outhucpath,['HUC12','cat_ID_con','region']) as cur:
    for row in cur:
        #print(f'HUC {row[0]} associated with catchment/watershed {HUC12s2pointsDict[row[0]][0]}')
        row[1] = HUC12s2pointsDict[row[0]][0]
        row[2] = HUC12s2pointsDict[row[0]][1]
        cur.updateRow(row)
    del(row)
del(cur)
print('cat_ID_con and region fields updated')



Hucs in NHDPlusList = 858
Hucs in NHD_H_List = 738
Total Hucs in lists = 1596
Total hucs selected for merge  = 1596
Merge Complete
cat_ID_con and region fields updated


## Export Tables


In [27]:
# # Export copies of dbf tables as csv
for table in outtables:
    tablename = arcpy.Describe(table).basename + ".csv"
    tablepath = os.path.join(outdir,tablename)
    print( tablepath)
    arcpy.conversion.TableToTable(table, outdir, tablename)

D:\GIS\AKSSF_awcHuc12_cv_Final\AKSSF_awchuc12_wtd_north_per.csv
D:\GIS\AKSSF_awcHuc12_cv_Final\AKSSF_awchuc12_cat_elev.csv
D:\GIS\AKSSF_awcHuc12_cv_Final\AKSSF_awchuc12_wtd_elev.csv
D:\GIS\AKSSF_awcHuc12_cv_Final\AKSSF_awchuc12_wtd_slope.csv
D:\GIS\AKSSF_awcHuc12_cv_Final\AKSSF_awchuc12_cat_slope.csv
D:\GIS\AKSSF_awcHuc12_cv_Final\AKSSF_awchuc12_wtd_wetland_per.csv
D:\GIS\AKSSF_awcHuc12_cv_Final\AKSSF_awchuc12_wtd_glacier_per.csv
D:\GIS\AKSSF_awcHuc12_cv_Final\AKSSF_awchuc12_wtd_lakepond_per.csv


In [28]:
import pandas as pd
pd.options.display.float_format = '{:.2f}'.format # only display 2 decimal places
# list to store covariate data frames
dfs = []

In [30]:
# Make catchment elev df
cat_df = pd.DataFrame()
cat_field_list = []
for field in arcpy.ListFields(cat_elev):
    cat_field_list.append(field.name)
cat_elev_arr = arcpy.da.TableToNumPyArray(cat_elev,cat_field_list)
cat_df = pd.DataFrame(cat_elev_arr)
cat_df = cat_df.drop(["OBJECTID","AwcHuc12_cat_elev_ZONE_CODE","region","cat_ID_txt"],axis=1)
cat_df = cat_df.set_index('cat_ID_con')
dfs.append(cat_df)
cat_df


AwcHuc12_cat_elev_COUNT  AwcHuc12_cat_elev_AREA  \
cat_ID_con                                                             
Bristol_Bay_1003859                   2442.0                244200.0   
Bristol_Bay_1004129                    380.0                 38000.0   
Bristol_Bay_1006858                   4632.0                463200.0   
Bristol_Bay_1007408                  17509.0               1750900.0   
Bristol_Bay_1008168                  13266.0               1326600.0   
Bristol_Bay_1008527                  19118.0               1911800.0   
Bristol_Bay_1008597                   2299.0                229900.0   
Bristol_Bay_1013001                   8308.0                830800.0   
Bristol_Bay_1013111                   2342.0                234200.0   
Bristol_Bay_1013306                   2292.0                229200.0   
Bristol_Bay_1013765                   3506.0                350600.0   
Bristol_Bay_1014251                    227.0                 22700.0   
Bristol_Bay_1014341                   1854.0                185400.0   
Bristol_Bay_1014516                    929.0                 92900.0   
Bristol_Bay_1014641                   8158.0                815800.0   
Bristol_Bay_1014786                   2842.0                284200.0   
Bristol_Bay_1014821                   1968.0                196800.0   
Bristol_Bay_1015186                   6630.0                663000.0   
Bristol_Bay_1015281                   4465.0                446500.0   
Bristol_Bay_1015516                  14462.0               1446200.0   
Bristol_Bay_1015685                  18349.0               1834900.0   
Bristol_Bay_1015771                   1571.0                157100.0   
Bristol_Bay_1015821                   1141.0                114100.0   
Bristol_Bay_1016325                   3355.0                335500.0   
Bristol_Bay_1016515                   2797.0                279700.0   
Bristol_Bay_1016825                  13973.0               1397300.0   
Bristol_Bay_1021823                   2164.0                216400.0   
Bristol_Bay_1021914                      1.0                   100.0   
Bristol_Bay_1021984                   2996.0                299600.0   
Bristol_Bay_1022284                    780.0                 78000.0   
Bristol_Bay_1023034                   9215.0                921500.0   
Bristol_Bay_1024403                   2007.0                200700.0   
Bristol_Bay_1025113                  11051.0               1105100.0   
Bristol_Bay_1025432                   1193.0                119300.0   
Bristol_Bay_1025533                   5297.0                529700.0   
Bristol_Bay_1025683                  13682.0               1368200.0   
Bristol_Bay_1025783                    863.0                 86300.0   
Bristol_Bay_1026233                   1101.0                110100.0   
Bristol_Bay_1026463                   4154.0                415400.0   
Bristol_Bay_1026613                   1556.0                155600.0   
Bristol_Bay_1026983                   9003.0                900300.0   
Bristol_Bay_1027852                   6344.0                634400.0   
Bristol_Bay_1028122                   1934.0                193400.0   
Bristol_Bay_1028212                    314.0                 31400.0   
Bristol_Bay_1028322                  10280.0               1028000.0   
Bristol_Bay_1029732                   5302.0                530200.0   
Bristol_Bay_1029872                   1692.0                169200.0   
Bristol_Bay_1030062                  11933.0               1193300.0   
Bristol_Bay_1030462                   8143.0                814300.0   
Bristol_Bay_1030642                   1288.0                128800.0   
Bristol_Bay_1031022                   1699.0                169900.0   
Bristol_Bay_2019230                    292.0                 29200.0   
Bristol_Bay_2019750                    183.0                 18300.0   
Bristol_Bay_2020120                     61.0                 

In [31]:
# Make catchment slope df
cat_sl_df = pd.DataFrame()
cat_sl_field_list = []
for field in arcpy.ListFields(cat_slope):
    cat_sl_field_list.append(field.name)
cat_sl_arr = arcpy.da.TableToNumPyArray(cat_slope, cat_sl_field_list)
cat_sl_df = pd.DataFrame(cat_sl_arr)
cat_sl_df = cat_sl_df.drop(["OBJECTID", "AwcHuc12_cat_slope_ZONE_CODE","region","cat_ID_txt"],axis=1)
cat_sl_df = cat_sl_df.set_index('cat_ID_con')
dfs.append(cat_sl_df)
cat_sl_df

AwcHuc12_cat_slope_COUNT  AwcHuc12_cat_slope_AREA  \
cat_ID_con                                                               
Bristol_Bay_1003859                    2442.0                 244200.0   
Bristol_Bay_1004129                     380.0                  38000.0   
Bristol_Bay_1006858                    4632.0                 463200.0   
Bristol_Bay_1007408                   17509.0                1750900.0   
Bristol_Bay_1008168                   13266.0                1326600.0   
Bristol_Bay_1008527                   19118.0                1911800.0   
Bristol_Bay_1008597                    2299.0                 229900.0   
Bristol_Bay_1013001                    8308.0                 830800.0   
Bristol_Bay_1013111                    2342.0                 234200.0   
Bristol_Bay_1013306                    2292.0                 229200.0   
Bristol_Bay_1013765                    3506.0                 350600.0   
Bristol_Bay_1014251                     227.0                  22700.0   
Bristol_Bay_1014341                    1854.0                 185400.0   
Bristol_Bay_1014516                     929.0                  92900.0   
Bristol_Bay_1014641                    8158.0                 815800.0   
Bristol_Bay_1014786                    2842.0                 284200.0   
Bristol_Bay_1014821                    1968.0                 196800.0   
Bristol_Bay_1015186                    6630.0                 663000.0   
Bristol_Bay_1015281                    4465.0                 446500.0   
Bristol_Bay_1015516                   14462.0                1446200.0   
Bristol_Bay_1015685                   18349.0                1834900.0   
Bristol_Bay_1015771                    1571.0                 157100.0   
Bristol_Bay_1015821                    1141.0                 114100.0   
Bristol_Bay_1016325                    3355.0                 335500.0   
Bristol_Bay_1016515                    2797.0                 279700.0   
Bristol_Bay_1016825                   13973.0                1397300.0   
Bristol_Bay_1021823                    2164.0                 216400.0   
Bristol_Bay_1021914                       1.0                    100.0   
Bristol_Bay_1021984                    2996.0                 299600.0   
Bristol_Bay_1022284                     780.0                  78000.0   
Bristol_Bay_1023034                    9215.0                 921500.0   
Bristol_Bay_1024403                    2007.0                 200700.0   
Bristol_Bay_1025113                   11051.0                1105100.0   
Bristol_Bay_1025432                    1193.0                 119300.0   
Bristol_Bay_1025533                    5297.0                 529700.0   
Bristol_Bay_1025683                   13682.0                1368200.0   
Bristol_Bay_1025783                     863.0                  86300.0   
Bristol_Bay_1026233                    1101.0                 110100.0   
Bristol_Bay_1026463                    4154.0                 415400.0   
Bristol_Bay_1026613                    1556.0                 155600.0   
Bristol_Bay_1026983                    9003.0                 900300.0   
Bristol_Bay_1027852                    6344.0                 634400.0   
Bristol_Bay_1028122                    1934.0                 193400.0   
Bristol_Bay_1028212                     314.0                  31400.0   
Bristol_Bay_1028322                   10280.0                1028000.0   
Bristol_Bay_1029732                    5302.0                 530200.0   
Bristol_Bay_1029872                    1692.0                 169200.0   
Bristol_Bay_1030062                   11933.0                1193300.0   
Bristol_Bay_1030462                    8143.0                 814300.0   
Bristol_Bay_1030642                    1288.0                 128800.0   
Bristol_Bay_1031022                    1699.0                 169900.0   
Bristol_Bay_2019230                     292.0                  29200.0   
Bristol_Bay_2019750      

In [33]:
# Make watershed elev df
wtd_df = pd.DataFrame()
wtd_field_list = []
for field in arcpy.ListFields(wtd_elev):
    wtd_field_list.append(field.name)
wtd_elev_arr = arcpy.da.TableToNumPyArray(wtd_elev,wtd_field_list)
wtd_df = pd.DataFrame(wtd_elev_arr)
wtd_df = wtd_df.drop(["OBJECTID","cat_ID","region", "cat_ID_txt"],axis=1)
wtd_df = wtd_df.set_index('cat_ID_con')
dfs.append(wtd_df)
wtd_df

AwcHuc12_wtd_elev_MIN  AwcHuc12_wtd_elev_MAX  \
cat_ID_con                                                          
Bristol_Bay_1003859                      4                    884   
Bristol_Bay_1004129                      5                    784   
Bristol_Bay_1006858                     34                    820   
Bristol_Bay_1007408                      4                    638   
Bristol_Bay_1008168                      4                    768   
Bristol_Bay_1008527                      8                    907   
Bristol_Bay_1008597                      4                    766   
Bristol_Bay_1013001                      8                     76   
Bristol_Bay_1013111                     45                    121   
Bristol_Bay_1013306                     10                    678   
Bristol_Bay_1013765                     44                    750   
Bristol_Bay_1014251                      8                    121   
Bristol_Bay_1014341                     60                    574   
Bristol_Bay_1014516                      6                   1471   
Bristol_Bay_1014641                     27                    128   
Bristol_Bay_1014786                      4                    601   
Bristol_Bay_1014821                     60                   2164   
Bristol_Bay_1015186                     10                   1843   
Bristol_Bay_1015281                     33                   2164   
Bristol_Bay_1015516                      4                   1843   
Bristol_Bay_1015685                      4                   1212   
Bristol_Bay_1015771                      0                   2164   
Bristol_Bay_1015821                      0                   2164   
Bristol_Bay_1016325                     39                   1843   
Bristol_Bay_1016515                     38                    582   
Bristol_Bay_1016825                      4                    983   
Bristol_Bay_1021823                      3                     69   
Bristol_Bay_1021914                     91                   1843   
Bristol_Bay_1021984                     13                    110   
Bristol_Bay_1022284                      7                    125   
Bristol_Bay_1023034                      4                   1843   
Bristol_Bay_1024403                    190                   1043   
Bristol_Bay_1025113                    142                   1627   
Bristol_Bay_1025432                      2                     91   
Bristol_Bay_1025533                    134                   1006   
Bristol_Bay_1025683                    190                   1624   
Bristol_Bay_1025783                      4                    120   
Bristol_Bay_1026233                      2                    266   
Bristol_Bay_1026463                      2                    125   
Bristol_Bay_1026613                    140                   2164   
Bristol_Bay_1026983                      2                   1843   
Bristol_Bay_1027852                     68                    367   
Bristol_Bay_1028122                      0                     48   
Bristol_Bay_1028212                    215                   1270   
Bristol_Bay_1028322                    140                   1270   
Bristol_Bay_1029732                    169                   2164   
Bristol_Bay_1029872                    106                   1006   
Bristol_Bay_1030062                      3                    120   
Bristol_Bay_1030462                     12                    266   
Bristol_Bay_1030642                      2                     92   
Bristol_Bay_1031022                     75                   2164   
Bristol_Bay_2019230                    262                   2696   
Bristol_Bay_2019750                    240                   2696   
Bristol_Bay_2020120                    209                   2696   
Bristol_Bay_2040601                    141                   3127   
Bristol_Bay_2041261                     99                   3127   
Bristol_Bay_2042341

In [35]:
# Make watershed slope df
wtd_sl_df = pd.DataFrame()
wtd_sl_field_list = []
for field in arcpy.ListFields(wtd_slope):
    wtd_sl_field_list.append(field.name)
wtd_sl_arr = arcpy.da.TableToNumPyArray(wtd_slope, wtd_sl_field_list)
wtd_sl_df = pd.DataFrame(wtd_sl_arr)
wtd_sl_df = wtd_sl_df.drop(["OBJECTID","cat_ID","region","cat_ID","cat_ID_txt"],axis=1)
wtd_sl_df = wtd_sl_df.set_index('cat_ID_con')
dfs.append(wtd_sl_df)
wtd_sl_df

AwcHuc12_wtd_slope_MIN  AwcHuc12_wtd_slope_MAX  \
cat_ID_con                                                            
Bristol_Bay_1003859            1.062447e-08               66.369751   
Bristol_Bay_1004129            1.035992e-08               73.399933   
Bristol_Bay_1006858            8.670093e-07               64.495277   
Bristol_Bay_1007408            1.796575e-08               69.628067   
Bristol_Bay_1008168            4.461478e-09               69.446381   
Bristol_Bay_1008527            2.416759e-08               65.650192   
Bristol_Bay_1008597            1.890819e-09               59.329147   
Bristol_Bay_1013001            1.263810e-08               19.735235   
Bristol_Bay_1013111            8.955972e-07               28.274343   
Bristol_Bay_1013306            1.667843e-08               62.867447   
Bristol_Bay_1013765            9.550183e-07               51.606178   
Bristol_Bay_1014251            7.539602e-09               29.355463   
Bristol_Bay_1014341            1.290133e-06               31.686764   
Bristol_Bay_1014516            1.722045e-08               44.968102   
Bristol_Bay_1014641            5.074586e-07               28.274343   
Bristol_Bay_1014786            3.632756e-09               53.807392   
Bristol_Bay_1014821            1.387648e-06               79.290741   
Bristol_Bay_1015186            4.039695e-09               78.008560   
Bristol_Bay_1015281            6.690834e-07               79.290741   
Bristol_Bay_1015516            4.039695e-09               78.008560   
Bristol_Bay_1015685            9.720249e-09               76.968178   
Bristol_Bay_1015771            4.844761e-11               79.290741   
Bristol_Bay_1015821            5.731864e-12               79.290741   
Bristol_Bay_1016325            7.040934e-07               73.548058   
Bristol_Bay_1016515            8.054575e-07               55.844463   
Bristol_Bay_1016825            4.705060e-09               68.529175   
Bristol_Bay_1021823            2.963972e-09               19.254791   
Bristol_Bay_1021914            2.285829e-06               71.824730   
Bristol_Bay_1021984            3.907888e-08               27.873329   
Bristol_Bay_1022284            3.256182e-09               27.873329   
Bristol_Bay_1023034            1.890819e-09               78.008560   
Bristol_Bay_1024403            5.011703e-06               58.034931   
Bristol_Bay_1025113            3.840461e-06               77.208687   
Bristol_Bay_1025432            6.862969e-09               22.013411   
Bristol_Bay_1025533            3.467819e-06               49.872917   
Bristol_Bay_1025683            4.959595e-06               79.290741   
Bristol_Bay_1025783            1.910930e-09               30.560671   
Bristol_Bay_1026233            2.847159e-09               33.070801   
Bristol_Bay_1026463            1.137902e-09               27.873329   
Bristol_Bay_1026613            3.701191e-06               79.290741   
Bristol_Bay_1026983            1.051740e-09               78.008560   
Bristol_Bay_1027852            1.451100e-06               26.607994   
Bristol_Bay_1028122            1.318890e-09               18.620529   
Bristol_Bay_1028212            5.766290e-06               67.753853   
Bristol_Bay_1028322            3.660007e-06               70.416595   
Bristol_Bay_1029732            4.419242e-06               75.294716   
Bristol_Bay_1029872            2.661464e-06               50.569118   
Bristol_Bay_1030062            1.910930e-09               30.560671   
Bristol_Bay_1030462            2.847159e-09               33.070801   
Bristol_Bay_1030642            5.569201e-09               32.581097   
Bristol_Bay_1031022            1.737729e-06               79.290741   
Bristol_Bay_2019230            6.777595e-06               79.140343   
Bristol_Bay_2019750            6.173441e-06               79.140343   
Bristol_Bay_2020120            5.368977e-06               79.140343   
Bristol_Bay_2040601            3.683331e-06  

In [36]:
# Make watershed north df
wtd_n_df = pd.DataFrame()
wtd_n_field_list = []
for field in arcpy.ListFields(wtd_per_north):
    wtd_n_field_list.append(field.name)
wtd_n_arr = arcpy.da.TableToNumPyArray(wtd_per_north,wtd_n_field_list)
wtd_n_df = pd.DataFrame(wtd_n_arr)
wtd_n_df = wtd_n_df.drop(["OBJECTID","region","cat_ID_txt"],axis=1)
wtd_n_df = wtd_n_df.set_index('cat_ID_con')
dfs.append(wtd_n_df)
wtd_n_df

AwcHuc12_non_north_area  AwcHuc12_north_area  \
cat_ID_con                                                          
Bristol_Bay_1003859             2.885880e+07         1.111710e+07   
Bristol_Bay_1004129             3.155990e+07         1.377600e+07   
Bristol_Bay_1006858             2.414080e+07         7.111100e+06   
Bristol_Bay_1007408             2.801180e+07         1.458500e+07   
Bristol_Bay_1008168             3.169130e+07         1.390660e+07   
Bristol_Bay_1008527             4.813800e+07         2.143150e+07   
Bristol_Bay_1008597             7.985280e+07         3.804210e+07   
Bristol_Bay_1013001             4.084080e+07         7.915100e+06   
Bristol_Bay_1013111             4.781850e+07         8.398100e+06   
Bristol_Bay_1013306             6.729470e+07         3.234710e+07   
Bristol_Bay_1013765             3.896720e+07         1.043070e+07   
Bristol_Bay_1014251             1.247634e+08         1.799040e+07   
Bristol_Bay_1014341             8.690720e+07         3.498420e+07   
Bristol_Bay_1014516             4.651630e+07         1.439670e+07   
Bristol_Bay_1014641             2.202761e+08         3.618100e+07   
Bristol_Bay_1014786             5.652280e+07         2.536700e+07   
Bristol_Bay_1014821             1.232531e+09         4.167690e+08   
Bristol_Bay_1015186             4.835144e+08         8.410600e+07   
Bristol_Bay_1015281             1.427661e+09         4.717852e+08   
Bristol_Bay_1015516             6.000634e+08         1.290788e+08   
Bristol_Bay_1015685             7.777650e+07         2.239020e+07   
Bristol_Bay_1015771             1.959146e+09         5.527348e+08   
Bristol_Bay_1015821             5.850098e+09         1.160288e+09   
Bristol_Bay_1016325             3.021273e+08         4.981370e+07   
Bristol_Bay_1016515             3.758820e+07         2.051820e+07   
Bristol_Bay_1016825             6.590230e+07         4.449300e+06   
Bristol_Bay_1021823             3.770110e+07         5.083600e+06   
Bristol_Bay_1021914             1.202308e+08         1.192620e+07   
Bristol_Bay_1021984             8.225550e+07         1.829780e+07   
Bristol_Bay_1022284             1.810272e+08         3.657470e+07   
Bristol_Bay_1023034             2.803881e+09         4.539658e+08   
Bristol_Bay_1024403             4.463720e+07         1.021580e+07   
Bristol_Bay_1025113             7.912640e+07         4.221790e+07   
Bristol_Bay_1025432             5.281230e+07         1.146330e+07   
Bristol_Bay_1025533             9.528870e+07         3.603010e+07   
Bristol_Bay_1025683             1.348425e+08         5.205820e+07   
Bristol_Bay_1025783             1.011251e+08         1.729800e+07   
Bristol_Bay_1026233             1.869098e+08         1.934070e+07   
Bristol_Bay_1026463             2.283388e+08         4.168910e+07   
Bristol_Bay_1026613             5.373242e+08         2.162474e+08   
Bristol_Bay_1026983             3.380456e+09         5.331248e+08   
Bristol_Bay_1027852             6.442710e+07         5.384680e+07   
Bristol_Bay_1028122             1.451810e+07         2.441500e+06   
Bristol_Bay_1028212             1.270507e+08         1.942700e+07   
Bristol_Bay_1028322             2.162601e+08         3.251890e+07   
Bristol_Bay_1029732             2.411742e+08         9.701140e+07   
Bristol_Bay_1029872             1.505267e+08         6.775670e+07   
Bristol_Bay_1030062             1.532351e+08         2.383090e+07   
Bristol_Bay_1030462             8.696960e+07         1.171850e+07   
Bristol_Bay_1030642             1.700257e+08         2.308440e+07   
Bristol_Bay_1031022             1.090945e+09         3.546554e+08   
Bristol_Bay_2019230             2.390946e+08         6.637020e+07   
Bristol_Bay_2019750             3.055545e+08         9.680830e+07   
Bristol_Bay_2020120             3.888363e+08         1.235349e+08   
Bristol_Bay_2040601             7.778573e+08         2.223275e+08   
Bristol_Bay_2041261             8.856284e+08         2.512513e+08   
Bristol_Bay_2042341

In [37]:
# Make watershed wetland df
wtd_wet_df = pd.DataFrame()
wtd_wet_field_list = []
for field in arcpy.ListFields(wtd_wet):
    wtd_wet_field_list.append(field.name)
wtd_wet_arr = arcpy.da.TableToNumPyArray(wtd_wet,wtd_wet_field_list)
wtd_wet_df = pd.DataFrame(wtd_wet_arr)
wtd_wet_df = wtd_wet_df.drop(["OBJECTID","region","cat_ID_txt"],axis=1)
wtd_wet_df = wtd_wet_df.set_index('cat_ID_con')
dfs.append(wtd_wet_df)
wtd_wet_df

AwcHuc12_non_wetland_area  AwcHuc12_wetland_area  \
cat_ID_con                                                              
Bristol_Bay_1003859               3.988500e+07           9.090000e+04   
Bristol_Bay_1004129               4.533590e+07           0.000000e+00   
Bristol_Bay_1006858               3.124740e+07           4.500000e+03   
Bristol_Bay_1007408               4.244830e+07           1.485000e+05   
Bristol_Bay_1008168               4.558620e+07           1.170000e+04   
Bristol_Bay_1008527               6.925680e+07           3.127000e+05   
Bristol_Bay_1008597               1.135501e+08           4.344800e+06   
Bristol_Bay_1013001               4.774200e+07           1.013900e+06   
Bristol_Bay_1013111               5.192910e+07           4.287500e+06   
Bristol_Bay_1013306               9.782640e+07           1.815400e+06   
Bristol_Bay_1013765               4.833780e+07           1.060100e+06   
Bristol_Bay_1014251               1.359078e+08           6.846000e+06   
Bristol_Bay_1014341               1.211713e+08           7.201000e+05   
Bristol_Bay_1014516               5.734120e+07           3.571800e+06   
Bristol_Bay_1014641               2.410356e+08           1.542150e+07   
Bristol_Bay_1014786               7.494790e+07           6.941900e+06   
Bristol_Bay_1014821               1.631493e+09           1.780730e+07   
Bristol_Bay_1015186               5.634236e+08           4.196800e+06   
Bristol_Bay_1015281               1.878308e+09           2.113760e+07   
Bristol_Bay_1015516               7.161025e+08           1.303970e+07   
Bristol_Bay_1015685               9.996570e+07           2.010000e+05   
Bristol_Bay_1015771               2.456593e+09           5.528730e+07   
Bristol_Bay_1015821               6.794763e+09           2.156231e+08   
Bristol_Bay_1016325               3.503635e+08           1.577500e+06   
Bristol_Bay_1016515               5.795840e+07           1.480000e+05   
Bristol_Bay_1016825               6.319960e+07           7.152000e+06   
Bristol_Bay_1021823               3.503400e+07           7.750700e+06   
Bristol_Bay_1021914               1.320410e+08           1.160000e+05   
Bristol_Bay_1021984               9.300440e+07           7.548900e+06   
Bristol_Bay_1022284               1.893001e+08           2.830180e+07   
Bristol_Bay_1023034               3.200849e+09           5.699790e+07   
Bristol_Bay_1024403               5.326590e+07           1.587100e+06   
Bristol_Bay_1025113               1.212120e+08           1.323000e+05   
Bristol_Bay_1025432               6.221870e+07           2.056900e+06   
Bristol_Bay_1025533               1.307139e+08           6.049000e+05   
Bristol_Bay_1025683               1.851008e+08           1.799900e+06   
Bristol_Bay_1025783               1.138862e+08           4.536900e+06   
Bristol_Bay_1026233               1.925744e+08           1.367610e+07   
Bristol_Bay_1026463               2.363800e+08           3.364790e+07   
Bristol_Bay_1026613               7.467141e+08           6.857500e+06   
Bristol_Bay_1026983               3.782088e+09           1.314928e+08   
Bristol_Bay_1027852               1.156762e+08           2.597700e+06   
Bristol_Bay_1028122               1.641300e+07           5.466000e+05   
Bristol_Bay_1028212               1.464683e+08           9.400000e+03   
Bristol_Bay_1028322               2.468342e+08           1.944800e+06   
Bristol_Bay_1029732               3.356080e+08           2.577600e+06   
Bristol_Bay_1029872               2.170678e+08           1.215600e+06   
Bristol_Bay_1030062               1.682073e+08           8.858700e+06   
Bristol_Bay_1030462               9.763340e+07           1.054700e+06   
Bristol_Bay_1030642               1.834133e+08           9.696800e+06   
Bristol_Bay_1031022               1.432089e+09           1.351110e+07   
Bristol_Bay_2019230               3.054299e+08           3.510000e+04   
Bristol_Bay_2019750               4.021480e+08           2.151000e+05   
Bristo

In [38]:
# Make watershed lakes df
wtd_lp_df = pd.DataFrame()
wtd_lp_field_list = []
for field in arcpy.ListFields(wtd_lp):
    wtd_lp_field_list.append(field.name)
wtd_lp_arr = arcpy.da.TableToNumPyArray(wtd_lp, wtd_lp_field_list)
wtd_lp_df = pd.DataFrame(wtd_lp_arr)
wtd_lp_df = wtd_lp_df.drop(["OBJECTID","region","cat_ID_txt","cat_ID","FType"],axis=1)
wtd_lp_df = wtd_lp_df.set_index('cat_ID_con')
dfs.append(wtd_lp_df)
wtd_lp_df

AwcHuc12_wtd_lake_area_sqm  AwcHuc12_wtd_lake_per
cat_ID_con                                                            
Bristol_Bay_1003859                3.636237e+06               9.096073
Bristol_Bay_1004129                6.742079e+05               1.487139
Bristol_Bay_1006858                3.218224e+03               0.010298
Bristol_Bay_1007408                2.014013e+05               0.472809
Bristol_Bay_1008168                8.169379e+04               0.179161
Bristol_Bay_1008527                7.655855e+04               0.110046
Bristol_Bay_1008597                1.626924e+06               1.379978
Bristol_Bay_1013001                3.227150e+06               6.618994
Bristol_Bay_1013111                6.882349e+06              12.242556
Bristol_Bay_1013306                1.657556e+06               1.663515
Bristol_Bay_1013765                5.855349e+05               1.185344
Bristol_Bay_1014251                1.205690e+07               8.445937
Bristol_Bay_1014341                2.822562e+06               2.315637
Bristol_Bay_1014516                5.427597e+06               8.910408
Bristol_Bay_1014641                2.039901e+07               7.954162
Bristol_Bay_1014786                1.538320e+06               1.878524
Bristol_Bay_1014821                1.248356e+07               0.756901
Bristol_Bay_1015186                3.118644e+06               0.549424
Bristol_Bay_1015281                1.930809e+07               1.016511
Bristol_Bay_1015516                1.198659e+07               1.643930
Bristol_Bay_1015685                1.902378e+05               0.189921
Bristol_Bay_1015771                7.436127e+07               2.960382
Bristol_Bay_1015821                1.427923e+09              20.368678
Bristol_Bay_1016325                8.804497e+05               0.250170
Bristol_Bay_1016515                1.088732e+05               0.187369
Bristol_Bay_1016825                4.643241e+06               6.600050
Bristol_Bay_1021823                3.228017e+06               7.544793
Bristol_Bay_1021914                5.649131e+04               0.042746
Bristol_Bay_1021984                1.563020e+07              15.544198
Bristol_Bay_1022284                3.079249e+07              14.150837
Bristol_Bay_1023034                1.216169e+09              37.330466
Bristol_Bay_1024403                2.523016e+05               0.459960
Bristol_Bay_1025113                4.006124e+05               0.330145
Bristol_Bay_1025432                6.125167e+06               9.529536
Bristol_Bay_1025533                1.953483e+06               1.487589
Bristol_Bay_1025683                1.449625e+05               0.077561
Bristol_Bay_1025783                1.672062e+07              14.119391
Bristol_Bay_1026233                1.724295e+07               8.360196
Bristol_Bay_1026463                3.743653e+07              13.863949
Bristol_Bay_1026613                2.681447e+06               0.355832
Bristol_Bay_1026983                1.287438e+09              32.896668
Bristol_Bay_1027852                1.411933e+06               1.193782
Bristol_Bay_1028122                1.259216e+06               7.424796
Bristol_Bay_1028212                6.466936e+04               0.044150
Bristol_Bay_1028322                3.213242e+06               1.291605
Bristol_Bay_1029732                1.263883e+06               0.373725
Bristol_Bay_1029872                1.981032e+06               0.907551
Bristol_Bay_1030062                2.400797e+07              13.558766
Bristol_Bay_1030462                6.802560e+06               6.892989
Bristol_Bay_1030642                2.040737e+07              10.567741
Bristol_Bay_1031022                9.990478e+06               0.691095
Bristol_Bay_2019230                2.178100e+05               0.071304
Bristol_Bay_2019750                5.577677e+05               0.138623
Bristol_Bay_2020120                6.155337e+05               0.120134
Bristol_Bay_2040601                6.966763e+

In [39]:
# Make watershed glacier df
wtd_glac_df = pd.DataFrame()
wtd_glac_field_list = []
for field in arcpy.ListFields(wtd_glac):
    wtd_glac_field_list.append(field.name)
wtd_glac_arr = arcpy.da.TableToNumPyArray(wtd_glac, wtd_glac_field_list)
wtd_glac_df = pd.DataFrame(wtd_glac_arr)
wtd_glac_df = wtd_glac_df.drop(["OBJECTID","region","cat_ID_txt","cat_ID","O1Region"],axis=1)
wtd_glac_df = wtd_glac_df.set_index('cat_ID_con')
dfs.append(wtd_glac_df)
wtd_glac_df

AwcHuc12_wtd_glacier_area_sqm  AwcHuc12_wtd_glacier_per
cat_ID_con                                                                  
Bristol_Bay_1014821                   3.384660e+07                  2.052180
Bristol_Bay_1015186                   8.152618e+06                  1.436280
Bristol_Bay_1015281                   3.384660e+07                  1.781920
Bristol_Bay_1015516                   8.152618e+06                  1.118111
Bristol_Bay_1015771                   3.384660e+07                  1.347461
Bristol_Bay_1015821                   4.199922e+07                  0.599100
Bristol_Bay_1016325                   8.152618e+06                  2.316473
Bristol_Bay_1021914                   8.152618e+06                  6.168888
Bristol_Bay_1023034                   8.152618e+06                  0.250246
Bristol_Bay_1025113                   1.511614e+06                  1.245723
Bristol_Bay_1025683                   3.134740e+06                  1.677222
Bristol_Bay_1026613                   3.384660e+07                  4.491491
Bristol_Bay_1026983                   8.152618e+06                  0.208316
Bristol_Bay_1029732                   2.920025e+07                  8.634386
Bristol_Bay_1031022                   3.384660e+07                  2.341353
Bristol_Bay_2019230                   1.508901e+08                 49.396870
Bristol_Bay_2019750                   1.732491e+08                 43.057897
Bristol_Bay_2020120                   1.914585e+08                 37.367117
Bristol_Bay_2040601                   3.171267e+08                 31.706794
Bristol_Bay_2041261                   3.267508e+08                 28.741002
Bristol_Bay_2042341                   6.116056e+07                 14.362497
Bristol_Bay_2063257                   2.032208e+06                  3.089758
Bristol_Bay_2066734                   2.534640e+06                  4.693156
Bristol_Bay_2067097                   3.361202e+06                  2.547264
Bristol_Bay_2068147                   7.030043e+05                  0.051752
Bristol_Bay_2068597                   5.745550e+06                  0.982903
Bristol_Bay_2069087                   5.745550e+06                  0.622257
Bristol_Bay_2069144                   1.498523e+06                  1.925644
Bristol_Bay_2069287                   5.745550e+06                  0.562352
Bristol_Bay_2069737                   6.448554e+06                  0.237925
Bristol_Bay_2069987                   6.448554e+06                  0.206091
Bristol_Bay_2070037                   6.448554e+06                  0.194777
Bristol_Bay_2070127                   6.448554e+06                  0.176758
Bristol_Bay_2070227                   5.528062e+08                  2.334040
Bristol_Bay_2070527                   5.528062e+08                  2.272303
Bristol_Bay_2070607                   5.528062e+08                  2.269760
Bristol_Bay_2072204                   7.738259e+05                  0.875434
Bristol_Bay_2073204                   4.157317e+06                  1.624105
Bristol_Bay_2073484                   5.200999e+06                  1.563843
Bristol_Bay_2073634                   6.699522e+06                  1.380446
Bristol_Bay_2075404                   2.245306e+07                  5.862213
Bristol_Bay_2076202                   1.964385e+07                 24.146767
Bristol_Bay_2076454                   5.172052e+08                  5.862785
Bristol_Bay_2076994                   5.172052e+08                  5.795253
Bristol_Bay_2078492                   2.789941e+07                 14.314181
Bristol_Bay_2078822                   3.394023e+07                 20.133775
Bristol_Bay_2079192                   6.245805e+07                 14.888991
Bristol_Bay_2082463                   2.205563e+06                  0.260337
Bristol_Bay_2082862                   1.660854e+07                  2.176088
Bristol_Bay_2083162                   3.020175e+07                  5.771740
Bristol_Bay_20846


## Merge all covariate dataframes together and drop unnecessary columns
## No Longer using dfs to merge and Export - Instead Merge watershed polygons and join fields
 * Recalculate cat_ID as float64 type
 * Reorder columns
 * Export final csv


In [40]:
# Merge all data frames together
import numpy as np
from functools import reduce
df_final = reduce(lambda left,right: pd.merge(left,right,on='cat_ID_con',how="outer"), dfs)

df_final.columns = list(uniquify(df_final))
#List of final columns in the order to output
# final_cols_old = ['cat_ID_txt','cat_ID','region', 'AwcHuc12_cat_slope_COUNT', 'AwcHuc12_cat_slope_AREA', 'AwcHuc12_cat_slope_MIN', 'AwcHuc12_cat_slope_MAX',
#               'AwcHuc12_cat_slope_RANGE','AwcHuc12_cat_slope_MEAN', 'AwcHuc12_cat_slope_STD', 'AwcHuc12_cat_slope_SUM', 'AwcHuc12_cat_slope_MEDIAN', 'AwcHuc12_cat_slope_PCT90',
#               'AwcHuc12_cat_elev_COUNT', 'AwcHuc12_cat_elev_AREA', 'AwcHuc12_cat_elev_MIN', 'AwcHuc12_cat_elev_MAX', 'AwcHuc12_cat_elev_RANGE', 'AwcHuc12_cat_elev_MEAN', 'AwcHuc12_cat_elev_STD',
#               'AwcHuc12_cat_elev_SUM', 'AwcHuc12_cat_elev_VARIETY', 'AwcHuc12_cat_elev_MAJORITY', 'AwcHuc12_cat_elev_MINORITY', 'AwcHuc12_cat_elev_MEDIAN', 'AwcHuc12_cat_elev_PCT90',
#               'AwcHuc12_wtd_elev_COUNT', 'AwcHuc12_wtd_elev_AREA', 'AwcHuc12_wtd_elev_MIN', 'AwcHuc12_wtd_elev_MAX', 'AwcHuc12_wtd_elev_RANGE', 'AwcHuc12_wtd_elev_MEAN',
#               'AwcHuc12_wtd_elev_STD', 'AwcHuc12_wtd_elev_SUM', 'AwcHuc12_wtd_elev_VARIETY', 'AwcHuc12_wtd_elev_MAJORITY', 'AwcHuc12_wtd_elev_MINORITY',
#               'AwcHuc12_wtd_elev_MEDIAN', 'AwcHuc12_wtd_elev_PCT90', 'AwcHuc12_wtd_slope_COUNT', 'AwcHuc12_wtd_slope_AREA', 'AwcHuc12_wtd_slope_MIN', 'AwcHuc12_wtd_slope_MAX',
#               'AwcHuc12_wtd_slope_RANGE', 'AwcHuc12_wtd_slope_MEAN', 'AwcHuc12_wtd_slope_STD', 'AwcHuc12_wtd_slope_SUM', 'AwcHuc12_wtd_slope_MEDIAN', 'AwcHuc12_wtd_slope_PCT90',
#               'AwcHuc12_non_north_area', 'AwcHuc12_north_area', 'AwcHuc12_wtd_north_per', 'non_wetland_area', 'AwcHuc12_wetland_area', 'AwcHuc12_wtd_wet_per',
#               'AwcHuc12_wtd_lake_area_sqm', 'AwcHuc12_wtd_lake_per', 'AwcHuc12_wtd_glacier_area_sqm', 'AwcHuc12_wtd_glacier_per' ]
final_cols = ['AwcHuc12_cat_slope_COUNT', 'AwcHuc12_cat_slope_AREA', 'AwcHuc12_cat_slope_MIN', 'AwcHuc12_cat_slope_MAX',
              'AwcHuc12_cat_slope_RANGE','AwcHuc12_cat_slope_MEAN', 'AwcHuc12_cat_slope_STD', 'AwcHuc12_cat_slope_SUM', 'AwcHuc12_cat_slope_MEDIAN', 'AwcHuc12_cat_slope_PCT90',
              'AwcHuc12_cat_elev_COUNT', 'AwcHuc12_cat_elev_AREA', 'AwcHuc12_cat_elev_MIN', 'AwcHuc12_cat_elev_MAX', 'AwcHuc12_cat_elev_RANGE', 'AwcHuc12_cat_elev_MEAN', 'AwcHuc12_cat_elev_STD',
              'AwcHuc12_cat_elev_SUM', 'AwcHuc12_cat_elev_VARIETY', 'AwcHuc12_cat_elev_MAJORITY', 'AwcHuc12_cat_elev_MINORITY', 'AwcHuc12_cat_elev_MEDIAN', 'AwcHuc12_cat_elev_PCT90',
              'AwcHuc12_wtd_elev_MIN', 'AwcHuc12_wtd_elev_MAX','AwcHuc12_wtd_elev_MEAN','AwcHuc12_wtd_elev_STD','AwcHuc12_wtd_slope_MIN', 'AwcHuc12_wtd_slope_MAX','AwcHuc12_wtd_slope_MEAN',
              'AwcHuc12_wtd_slope_STD','AwcHuc12_non_north_area', 'AwcHuc12_north_area', 'AwcHuc12_wtd_north_per', 'non_wetland_area', 'AwcHuc12_wetland_area', 'AwcHuc12_wtd_wet_per',
              'AwcHuc12_wtd_lake_area_sqm', 'AwcHuc12_wtd_lake_per', 'AwcHuc12_wtd_glacier_area_sqm', 'AwcHuc12_wtd_glacier_per' ]

# #Export merged dataframe to csv
cov_csv_out = os.path.join(outdir,'AKSSF_awcHuc12s_Covariates.csv')
df_final.to_csv(cov_csv_out, encoding = 'utf-8')
print('Export all covariates dataframe to csv complete')

df_final

Export all covariates dataframe to csv complete


AwcHuc12_cat_elev_COUNT  AwcHuc12_cat_elev_AREA  \
cat_ID_con                                                             
Bristol_Bay_1003859                   2442.0                244200.0   
Bristol_Bay_1004129                    380.0                 38000.0   
Bristol_Bay_1006858                   4632.0                463200.0   
Bristol_Bay_1007408                  17509.0               1750900.0   
Bristol_Bay_1008168                  13266.0               1326600.0   
Bristol_Bay_1008527                  19118.0               1911800.0   
Bristol_Bay_1008597                   2299.0                229900.0   
Bristol_Bay_1013001                   8308.0                830800.0   
Bristol_Bay_1013111                   2342.0                234200.0   
Bristol_Bay_1013306                   2292.0                229200.0   
Bristol_Bay_1013765                   3506.0                350600.0   
Bristol_Bay_1014251                    227.0                 22700.0   
Bristol_Bay_1014341                   1854.0                185400.0   
Bristol_Bay_1014516                    929.0                 92900.0   
Bristol_Bay_1014641                   8158.0                815800.0   
Bristol_Bay_1014786                   2842.0                284200.0   
Bristol_Bay_1014821                   1968.0                196800.0   
Bristol_Bay_1015186                   6630.0                663000.0   
Bristol_Bay_1015281                   4465.0                446500.0   
Bristol_Bay_1015516                  14462.0               1446200.0   
Bristol_Bay_1015685                  18349.0               1834900.0   
Bristol_Bay_1015771                   1571.0                157100.0   
Bristol_Bay_1015821                   1141.0                114100.0   
Bristol_Bay_1016325                   3355.0                335500.0   
Bristol_Bay_1016515                   2797.0                279700.0   
Bristol_Bay_1016825                  13973.0               1397300.0   
Bristol_Bay_1021823                   2164.0                216400.0   
Bristol_Bay_1021914                      1.0                   100.0   
Bristol_Bay_1021984                   2996.0                299600.0   
Bristol_Bay_1022284                    780.0                 78000.0   
Bristol_Bay_1023034                   9215.0                921500.0   
Bristol_Bay_1024403                   2007.0                200700.0   
Bristol_Bay_1025113                  11051.0               1105100.0   
Bristol_Bay_1025432                   1193.0                119300.0   
Bristol_Bay_1025533                   5297.0                529700.0   
Bristol_Bay_1025683                  13682.0               1368200.0   
Bristol_Bay_1025783                    863.0                 86300.0   
Bristol_Bay_1026233                   1101.0                110100.0   
Bristol_Bay_1026463                   4154.0                415400.0   
Bristol_Bay_1026613                   1556.0                155600.0   
Bristol_Bay_1026983                   9003.0                900300.0   
Bristol_Bay_1027852                   6344.0                634400.0   
Bristol_Bay_1028122                   1934.0                193400.0   
Bristol_Bay_1028212                    314.0                 31400.0   
Bristol_Bay_1028322                  10280.0               1028000.0   
Bristol_Bay_1029732                   5302.0                530200.0   
Bristol_Bay_1029872                   1692.0                169200.0   
Bristol_Bay_1030062                  11933.0               1193300.0   
Bristol_Bay_1030462                   8143.0                814300.0   
Bristol_Bay_1030642                   1288.0                128800.0   
Bristol_Bay_1031022                   1699.0                169900.0   
Bristol_Bay_2019230                    292.0                 29200.0   
Bristol_Bay_2019750                    183.0                 18300.0   
Bristol_Bay_2020120                     61.0                 


## Merge watersheds and join covariates for data explore in GIS
* Collect all _wtds_merge polygons and merge together
* Join Covariates using cat_ID_con field


In [41]:
arcpy.env.workspace = outgdb
outtables.append(lcld_table)
# Merge watersheds
wtds = [fc for fc in arcpy.ListFeatureClasses('*_wtds_merge','POLYGON')]
akssf_h12wtds = arcpy.Merge_management(wtds,'AKSSF_awcHuc12_Watersheds_Merge')
dropfields = ['OBJECTID','cat_ID_con', 'cat_ID', 'cat_ID_txt', 'region','O1Region','FType','NHDPlusID']
for table in outtables:
    tname = table.getOutput(0).split("\\")[-1]
    fields =[f.name for f in arcpy.ListFields(tname) if f.name not in dropfields]
    print(f'Joining fields : {fields} to all Watersheds\n{("*"*100)}')
    arcpy.JoinField_management(akssf_h12wtds,'cat_ID_con',table, 'cat_ID_con', fields)
akssf_h12wtds_table = arcpy.TableToTable_conversion(akssf_h12wtds,outgdb,'AKSSF_awcHuc12_Covariates')

Joining fields : ['AwcHuc12_non_north_area', 'AwcHuc12_north_area', 'AwcHuc12_wtd_north_per'] to all Watersheds
****************************************************************************************************
Joining fields : ['AwcHuc12_cat_elev_ZONE_CODE', 'AwcHuc12_cat_elev_COUNT', 'AwcHuc12_cat_elev_AREA', 'AwcHuc12_cat_elev_MIN', 'AwcHuc12_cat_elev_MAX', 'AwcHuc12_cat_elev_RANGE', 'AwcHuc12_cat_elev_MEAN', 'AwcHuc12_cat_elev_STD', 'AwcHuc12_cat_elev_SUM', 'AwcHuc12_cat_elev_VARIETY', 'AwcHuc12_cat_elev_MAJORITY', 'AwcHuc12_cat_elev_MINORITY', 'AwcHuc12_cat_elev_MEDIAN', 'AwcHuc12_cat_elev_PCT90'] to all Watersheds
****************************************************************************************************
Joining fields : ['AwcHuc12_wtd_elev_MIN', 'AwcHuc12_wtd_elev_MAX', 'AwcHuc12_wtd_elev_MEAN', 'AwcHuc12_wtd_elev_STD'] to all Watersheds
****************************************************************************************************
Joining fields : ['AwcHuc12_wtd

In [42]:
# Export watershed as table after join fields
akssf_h12_cov_csv = arcpy.conversion.TableToTable(akssf_h12wtds_table, outdir, 'AKSSF_awcHuc12s_Covariates.csv')
print('Export all covariates dataframe to csv complete')


Export all covariates dataframe to csv complete


In [43]:
import pandas as pd
import numpy as np

#convert to df and check
wtds_df = pd.DataFrame()
wtds_fl = []

for field in arcpy.ListFields(akssf_h12wtds_table):
    wtds_fl.append(field.name)
akssf_h12wtds_arr = arcpy.da.TableToNumPyArray(akssf_h12wtds_table, wtds_fl)
akssf_h12wtds_arr
wtds_df = pd.DataFrame(akssf_h12wtds_arr)
wtds_df = wtds_df.set_index('cat_ID_con')
wtds_df


OBJECTID  ORIG_FID  \
cat_ID_con                                
Bristol_Bay_1003859         1         1   
Bristol_Bay_1004129         2         1   
Bristol_Bay_1006858         3         1   
Bristol_Bay_1007408         4         1   
Bristol_Bay_1008168         5         1   
Bristol_Bay_1008527         6         1   
Bristol_Bay_1008597         7         1   
Bristol_Bay_1013001         8         1   
Bristol_Bay_1013111         9         1   
Bristol_Bay_1013306        10         1   
Bristol_Bay_1013765        11         1   
Bristol_Bay_1014251        12         1   
Bristol_Bay_1014341        13         1   
Bristol_Bay_1014516        14         1   
Bristol_Bay_1014641        15         1   
Bristol_Bay_1014786        16         1   
Bristol_Bay_1014821        17         1   
Bristol_Bay_1015186        18         1   
Bristol_Bay_1015281        19         1   
Bristol_Bay_1015516        20         1   
Bristol_Bay_1015685        21         1   
Bristol_Bay_1015771        22         1   
Bristol_Bay_1015821        23         1   
Bristol_Bay_1016325        24         1   
Bristol_Bay_1016515        25         1   
Bristol_Bay_1016825        26         1   
Bristol_Bay_1021823        27         1   
Bristol_Bay_1021914        28         1   
Bristol_Bay_1021984        29         1   
Bristol_Bay_1022284        30         1   
Bristol_Bay_1023034        31         1   
Bristol_Bay_1024403        32         1   
Bristol_Bay_1025113        33         1   
Bristol_Bay_1025432        34         1   
Bristol_Bay_1025533        35         1   
Bristol_Bay_1025683        36         1   
Bristol_Bay_1025783        37         1   
Bristol_Bay_1026233        38         1   
Bristol_Bay_1026463        39         1   
Bristol_Bay_1026613        40         1   
Bristol_Bay_1026983        41         1   
Bristol_Bay_1027852        42         1   
Bristol_Bay_1028122        43         1   
Bristol_Bay_1028212        44         1   
Bristol_Bay_1028322        45         1   
Bristol_Bay_1029732        46         1   
Bristol_Bay_1029872        47         1   
Bristol_Bay_1030062        48         1   
Bristol_Bay_1030462        49         1   
Bristol_Bay_1030642        50         1   
Bristol_Bay_1031022        51         1   
Bristol_Bay_2019230        52         1   
Bristol_Bay_2019750        53         1   
Bristol_Bay_2020120        54         1   
Bristol_Bay_2040601        55         1   
Bristol_Bay_2041261        56         1   
Bristol_Bay_2042341        57         1   
Bristol_Bay_2059915        58         1   
Bristol_Bay_2060975        59         1   
Bristol_Bay_2061205        60         1   
Bristol_Bay_2061325        61         1   
Bristol_Bay_2063167        62         1   
Bristol_Bay_2063257        63         1   
Bristol_Bay_2064245        64         1   
Bristol_Bay_2064385        65         1   
Bristol_Bay_2065025        66         1   
Bristol_Bay_2065485        67         1   
Bristol_Bay_2065885        68         1   
Bristol_Bay_2066555        69         1   
Bristol_Bay_2066734        70         1   
Bristol_Bay_2066827        71         1   
Bristol_Bay_2067075        72         1   
Bristol_Bay_2067097        73         1   
Bristol_Bay_2067114        74         1   
Bristol_Bay_2067195        75         1   
Bristol_Bay_2067465        76         1   
Bristol_Bay_2067604        77         1   
Bristol_Bay_2068147        78         1   
Bristol_Bay_2068305        79         1   
Bristol_Bay_2068474        80         1   
Bristol_Bay_2068514        81         1   
Bristol_Bay_2068597        82         1   
Bristol_Bay_2068715        83         1   
Bristol_Bay_2068895        84         1   
Bristol_Bay_2069087        85         1   
Bristol_Bay_2069134        86         1   
Bristol_Bay_2069144        87         1   
Bristol_Bay_2069287        88         1   
Bristol_Bay_2069334        89         1   
Bristol_Bay_2069365        90         1   
Bristol_Bay_2069504        91         1   
Bristol_Bay_2069737   

In [44]:
bbay_df = wtds_df.filter(like='Bristol_Bay', axis = 0)
bbay_df

OBJECTID  ORIG_FID  \
cat_ID_con                                
Bristol_Bay_1003859         1         1   
Bristol_Bay_1004129         2         1   
Bristol_Bay_1006858         3         1   
Bristol_Bay_1007408         4         1   
Bristol_Bay_1008168         5         1   
Bristol_Bay_1008527         6         1   
Bristol_Bay_1008597         7         1   
Bristol_Bay_1013001         8         1   
Bristol_Bay_1013111         9         1   
Bristol_Bay_1013306        10         1   
Bristol_Bay_1013765        11         1   
Bristol_Bay_1014251        12         1   
Bristol_Bay_1014341        13         1   
Bristol_Bay_1014516        14         1   
Bristol_Bay_1014641        15         1   
Bristol_Bay_1014786        16         1   
Bristol_Bay_1014821        17         1   
Bristol_Bay_1015186        18         1   
Bristol_Bay_1015281        19         1   
Bristol_Bay_1015516        20         1   
Bristol_Bay_1015685        21         1   
Bristol_Bay_1015771        22         1   
Bristol_Bay_1015821        23         1   
Bristol_Bay_1016325        24         1   
Bristol_Bay_1016515        25         1   
Bristol_Bay_1016825        26         1   
Bristol_Bay_1021823        27         1   
Bristol_Bay_1021914        28         1   
Bristol_Bay_1021984        29         1   
Bristol_Bay_1022284        30         1   
Bristol_Bay_1023034        31         1   
Bristol_Bay_1024403        32         1   
Bristol_Bay_1025113        33         1   
Bristol_Bay_1025432        34         1   
Bristol_Bay_1025533        35         1   
Bristol_Bay_1025683        36         1   
Bristol_Bay_1025783        37         1   
Bristol_Bay_1026233        38         1   
Bristol_Bay_1026463        39         1   
Bristol_Bay_1026613        40         1   
Bristol_Bay_1026983        41         1   
Bristol_Bay_1027852        42         1   
Bristol_Bay_1028122        43         1   
Bristol_Bay_1028212        44         1   
Bristol_Bay_1028322        45         1   
Bristol_Bay_1029732        46         1   
Bristol_Bay_1029872        47         1   
Bristol_Bay_1030062        48         1   
Bristol_Bay_1030462        49         1   
Bristol_Bay_1030642        50         1   
Bristol_Bay_1031022        51         1   
Bristol_Bay_2019230        52         1   
Bristol_Bay_2019750        53         1   
Bristol_Bay_2020120        54         1   
Bristol_Bay_2040601        55         1   
Bristol_Bay_2041261        56         1   
Bristol_Bay_2042341        57         1   
Bristol_Bay_2059915        58         1   
Bristol_Bay_2060975        59         1   
Bristol_Bay_2061205        60         1   
Bristol_Bay_2061325        61         1   
Bristol_Bay_2063167        62         1   
Bristol_Bay_2063257        63         1   
Bristol_Bay_2064245        64         1   
Bristol_Bay_2064385        65         1   
Bristol_Bay_2065025        66         1   
Bristol_Bay_2065485        67         1   
Bristol_Bay_2065885        68         1   
Bristol_Bay_2066555        69         1   
Bristol_Bay_2066734        70         1   
Bristol_Bay_2066827        71         1   
Bristol_Bay_2067075        72         1   
Bristol_Bay_2067097        73         1   
Bristol_Bay_2067114        74         1   
Bristol_Bay_2067195        75         1   
Bristol_Bay_2067465        76         1   
Bristol_Bay_2067604        77         1   
Bristol_Bay_2068147        78         1   
Bristol_Bay_2068305        79         1   
Bristol_Bay_2068474        80         1   
Bristol_Bay_2068514        81         1   
Bristol_Bay_2068597        82         1   
Bristol_Bay_2068715        83         1   
Bristol_Bay_2068895        84         1   
Bristol_Bay_2069087        85         1   
Bristol_Bay_2069134        86         1   
Bristol_Bay_2069144        87         1   
Bristol_Bay_2069287        88         1   
Bristol_Bay_2069334        89         1   
Bristol_Bay_2069365        90         1   
Bristol_Bay_2069504        91         1   
Bristol_Bay_2069737   

In [45]:
kod_df = wtds_df.filter(like='Kodiak', axis = 0)
kod_df

OBJECTID  ORIG_FID  \
cat_ID_con                          
Kodiak_13958        614         1   
Kodiak_14049        615         1   
Kodiak_14069        616         1   
Kodiak_14458        617         1   
Kodiak_14658        618         1   
Kodiak_14858        619         1   
Kodiak_14958        620         1   
Kodiak_15261        621         1   
Kodiak_45317        622         1   
Kodiak_45537        623         1   
Kodiak_46167        624         1   
Kodiak_46907        625         1   
Kodiak_47187        626         1   
Kodiak_47207        627         1   
Kodiak_47797        628         1   
Kodiak_48057        629         1   
Kodiak_48067        630         1   
Kodiak_48197        631         1   
Kodiak_48267        632         1   
Kodiak_48707        633         1   
Kodiak_48997        634         1   
Kodiak_49617        635         1   
Kodiak_49707        636         1   
Kodiak_49837        637         1   
Kodiak_50207        638         1   
Kodiak_63603        639         1   
Kodiak_63943        640         1   
Kodiak_63963        641         1   
Kodiak_64263        642         1   
Kodiak_64593        643         1   
Kodiak_64633        644         1   
Kodiak_64673        645         1   
Kodiak_66383        646         1   
Kodiak_66643        647         1   
Kodiak_70982        648         1   
Kodiak_74254        649         1   
Kodiak_74624        650         1   
Kodiak_75194        651         1   
Kodiak_75624        652         1   
Kodiak_76204        653         1   
Kodiak_76354        654         1   
Kodiak_76542        655         1   
Kodiak_76564        656         1   
Kodiak_76942        657         1   
Kodiak_77162        658         1   
Kodiak_77254        659         1   
Kodiak_77294        660         1   
Kodiak_77372        661         1   
Kodiak_77702        662         1   
Kodiak_77794        663         1   
Kodiak_77824        664         1   
Kodiak_77844        665         1   
Kodiak_77864        666         1   
Kodiak_77872        667         1   
Kodiak_77952        668         1   
Kodiak_78072        669         1   
Kodiak_78104        670         1   
Kodiak_78602        671         1   
Kodiak_78804        672         1   
Kodiak_79034        673         1   
Kodiak_79642        674         1   
Kodiak_79842        675         1   
Kodiak_79862        676         1   
Kodiak_80022        677         1   
Kodiak_80054        678         1   
Kodiak_80624        679         1   
Kodiak_80644        680         1   
Kodiak_95226        681         1   
Kodiak_96786        682         1   
Kodiak_97006        683         1   
Kodiak_100826       684         1   
Kodiak_101146       685         1   
Kodiak_101736       686         1   
Kodiak_101826       687         1   
Kodiak_102106       688         1   
Kodiak_102746       689         1   
Kodiak_102936       690         1   
Kodiak_103016       691         1   
Kodiak_103116       692         1   
Kodiak_103196       693         1   
Kodiak_103266       694         1   
Kodiak_103296       695         1   
Kodiak_103556       696         1   
Kodiak_103936       697         1   
Kodiak_104296       698         1   
Kodiak_105086       699         1   
Kodiak_106365       700         1   
Kodiak_106486       701         1   
Kodiak_107216       702         1   
Kodiak_107376       703         1   
Kodiak_107686       704         1   
Kodiak_108206       705         1   
Kodiak_108376       706         1   
Kodiak_108606       707         1   
Kodiak_116535       708         1   
Kodiak_117795       709         1   
Kodiak_120645       710         1   
Kodiak_121025       711         1   
Kodiak_122415       712         1   
Kodiak_122785       713         1   
Kodiak_123415       714         1   
Kodiak_123695       715         1   
Kodiak_124065       716         1   
Kodiak_124185       717         1   
Kodiak_124215       718         1   
Kodiak_124815       719         1   
Kodiak_124945      

In [43]:
pws_df = wtds_df.filter(like='Prince', axis = 0)
pws_df

OBJECTID  ORIG_FID  \
cat_ID_con                                       
Prince_William_Sound_685         859         1   
Prince_William_Sound_3038        860         1   
Prince_William_Sound_13227       861         1   
Prince_William_Sound_16467       862         1   
Prince_William_Sound_17027       863         1   
Prince_William_Sound_17697       864         1   
Prince_William_Sound_18357       865         1   
Prince_William_Sound_18547       866         1   
Prince_William_Sound_18737       867         1   
Prince_William_Sound_18967       868         1   
Prince_William_Sound_19416       869         1   
Prince_William_Sound_24654       870         1   
Prince_William_Sound_25516       871         1   
Prince_William_Sound_26246       872         1   
Prince_William_Sound_26334       873         1   
Prince_William_Sound_27303       874         1   
Prince_William_Sound_28576       875         1   
Prince_William_Sound_28734       876         1   
Prince_William_Sound_29704       877         1   
Prince_William_Sound_29954       878         1   
Prince_William_Sound_30114       879         1   
Prince_William_Sound_30596       880         1   
Prince_William_Sound_30774       881         1   
Prince_William_Sound_30886       882         1   
Prince_William_Sound_30934       883         1   
Prince_William_Sound_31226       884         1   
Prince_William_Sound_32015       885         1   
Prince_William_Sound_32766       886         1   
Prince_William_Sound_33036       887         1   
Prince_William_Sound_33396       888         1   
Prince_William_Sound_34003       889         1   
Prince_William_Sound_34993       890         1   
Prince_William_Sound_35075       891         1   
Prince_William_Sound_35343       892         1   
Prince_William_Sound_36553       893         1   
Prince_William_Sound_37373       894         1   
Prince_William_Sound_37815       895         1   
Prince_William_Sound_37935       896         1   
Prince_William_Sound_38615       897         1   
Prince_William_Sound_39065       898         1   
Prince_William_Sound_39255       899         1   
Prince_William_Sound_39565       900         1   
Prince_William_Sound_40615       901         1   
Prince_William_Sound_40635       902         1   
Prince_William_Sound_40743       903         1   
Prince_William_Sound_41025       904         1   
Prince_William_Sound_41123       905         1   
Prince_William_Sound_41143       906         1   
Prince_William_Sound_41515       907         1   
Prince_William_Sound_41525       908         1   
Prince_William_Sound_41963       909         1   
Prince_William_Sound_41995       910         1   
Prince_William_Sound_42455       911         1   
Prince_William_Sound_43125       912         1   
Prince_William_Sound_43195       913         1   
Prince_William_Sound_43473       914         1   
Prince_William_Sound_43513       915         1   
Prince_William_Sound_43705       916         1   
Prince_William_Sound_43793       917         1   
Prince_William_Sound_43933       918         1   
Prince_William_Sound_44113       919         1   
Prince_William_Sound_44503       920         1   
Prince_William_Sound_44545       921         1   
Prince_William_Sound_44595       922         1   
Prince_William_Sound_44633       923         1   
Prince_William_Sound_44663       924         1   
Prince_William_Sound_45473       925         1   
Prince_William_Sound_45835       926         1   
Prince_William_Sound_45863       927         1   
Prince_William_Sound_45915       928         1   
Prince_William_Sound_46065       929         1   
Prince_William_Sound_46103       930         1   
Prince_William_Sound_46293       931         1   
Prince_William_Sound_46483       932         1   
Prince_William_Sound_60732       933         1   
Prince_William_Sound_61812       934         1   
Prince_William_Sound_62232       935         1   
Prince_William_Sound_64192       936         1   
Prince_William_Sound_66912  

In [44]:
ci_df = wtds_df.filter(like='Cook', axis = 0)
ci_df

OBJECTID  ORIG_FID  \
cat_ID_con                                      
Cook_Inlet_75004200000901         1         1   
Cook_Inlet_75004200001724         2         1   
Cook_Inlet_75004200000437         3         1   
Cook_Inlet_75004200001493         4         1   
Cook_Inlet_75004200009084         5         1   
Cook_Inlet_75004200003619         6         1   
Cook_Inlet_75004200001047         7         1   
Cook_Inlet_75004200016346         8         1   
Cook_Inlet_75004200010717         9         1   
Cook_Inlet_75004200010096        10         1   
Cook_Inlet_75004200003399        11         1   
Cook_Inlet_75004200000722        12         1   
Cook_Inlet_75004200000726        13         1   
Cook_Inlet_75004200012986        14         1   
Cook_Inlet_75004200008847        15         1   
Cook_Inlet_75004200010465        16         1   
Cook_Inlet_75004200014411        17         1   
Cook_Inlet_75004200012680        18         1   
Cook_Inlet_75004200000559        19         1   
Cook_Inlet_75004200007843        20         1   
Cook_Inlet_75004200009093        21         1   
Cook_Inlet_75004200008970        22         1   
Cook_Inlet_75004200005429        23         1   
Cook_Inlet_75004200012771        24         1   
Cook_Inlet_75004200012099        25         1   
Cook_Inlet_75004200001003        26         1   
Cook_Inlet_75004200000848        27         1   
Cook_Inlet_75004200011012        28         1   
Cook_Inlet_75004200006975        29         1   
Cook_Inlet_75004200005415        30         1   
Cook_Inlet_75004200000064        31         1   
Cook_Inlet_75004200001191        32         1   
Cook_Inlet_75004200001574        33         1   
Cook_Inlet_75004200003989        34         1   
Cook_Inlet_75004200002199        35         1   
Cook_Inlet_75004200005203        36         1   
Cook_Inlet_75004200001716        37         1   
Cook_Inlet_75004200008853        38         1   
Cook_Inlet_75004200008845        39         1   
Cook_Inlet_75004200005283        40         1   
Cook_Inlet_75004200005907        41         1   
Cook_Inlet_75004300004332        42         1   
Cook_Inlet_75004300005723        43         1   
Cook_Inlet_75004300006970        44         1   
Cook_Inlet_75004300002057        45         1   
Cook_Inlet_75004300005518        46         1   
Cook_Inlet_75004300004701        47         1   
Cook_Inlet_75004300004365        48         1   
Cook_Inlet_75004300006839        49         1   
Cook_Inlet_75004300007978        50         1   
Cook_Inlet_75004300007859        51         1   
Cook_Inlet_75004300005004        52         1   
Cook_Inlet_75004300005103        53         1   
Cook_Inlet_75004300000311        54         1   
Cook_Inlet_75004300008012        55         1   
Cook_Inlet_75004300001135        56         1   
Cook_Inlet_75004300007259        57         1   
Cook_Inlet_75004300001162        58         1   
Cook_Inlet_75004300002654        59         1   
Cook_Inlet_75004300006302        60         1   
Cook_Inlet_75004300002547        61         1   
Cook_Inlet_75004300006726        62         1   
Cook_Inlet_75004300003713        63         1   
Cook_Inlet_75004300002688        64         1   
Cook_Inlet_75004300000754        65         1   
Cook_Inlet_75004300003311        66         1   
Cook_Inlet_75004300002834        67         1   
Cook_Inlet_75004300001258        68         1   
Cook_Inlet_75004300007331        69         1   
Cook_Inlet_75004300001638        70         1   
Cook_Inlet_75004300002755        71         1   
Cook_Inlet_75004300005625        72         1   
Cook_Inlet_75004300006594        73         1   
Cook_Inlet_75004300006376        74         1   
Cook_Inlet_75004300004090        75         1   
Cook_Inlet_75004300002183        76         1   
Cook_Inlet_75004300006207        77         1   
Cook_Inlet_75004300002023        78         1   
Cook_Inlet_75004300004018        79         1   
Cook_Inlet_75004300000582        80         1   
Cook_Inle

In [45]:
cop_df = wtds_df.filter(like='Copper', axis = 0)
cop_df

OBJECTID  ORIG_FID  \
cat_ID_con                                        
Copper_River_75019800007852       635         1   
Copper_River_75019800005498       636         1   
Copper_River_75019800019853       637         1   
Copper_River_75019800019678       638         1   
Copper_River_75019800011243       639         1   
Copper_River_75019800002398       640         1   
Copper_River_75019800019142       641         1   
Copper_River_75019800006279       642         1   
Copper_River_75019800018811       643         1   
Copper_River_75019800009655       644         1   
Copper_River_75019800010136       645         1   
Copper_River_75019800002519       646         1   
Copper_River_75019800019218       647         1   
Copper_River_75019800010922       648         1   
Copper_River_75019800001400       649         1   
Copper_River_75019800006994       650         1   
Copper_River_75019800009573       651         1   
Copper_River_75019800011692       652         1   
Copper_River_75019800009388       653         1   
Copper_River_75019800010526       654         1   
Copper_River_75019800000955       655         1   
Copper_River_75019800000599       656         1   
Copper_River_75019800015373       657         1   
Copper_River_75019800011462       658         1   
Copper_River_75019800010313       659         1   
Copper_River_75019800000972       660         1   
Copper_River_75019800020292       661         1   
Copper_River_75019800015447       662         1   
Copper_River_75019800009321       663         1   
Copper_River_75019800011612       664         1   
Copper_River_75019800001873       665         1   
Copper_River_75019800020803       666         1   
Copper_River_75019800015952       667         1   
Copper_River_75019800000911       668         1   
Copper_River_75019800020746       669         1   
Copper_River_75019800018104       670         1   
Copper_River_75019800000492       671         1   
Copper_River_75019800017508       672         1   
Copper_River_75019800003840       673         1   
Copper_River_75019800011423       674         1   
Copper_River_75019800016364       675         1   
Copper_River_75019800020900       676         1   
Copper_River_75019800011406       677         1   
Copper_River_75019800012527       678         1   
Copper_River_75019800007832       679         1   
Copper_River_75019800001032       680         1   
Copper_River_75019800011978       681         1   
Copper_River_75019800000182       682         1   
Copper_River_75019600181061       683         1   
Copper_River_75019600185154       684         1   
Copper_River_75019600118290       685         1   
Copper_River_75019600132667       686         1   
Copper_River_75019600164515       687         1   
Copper_River_75019600132017       688         1   
Copper_River_75019600118006       689         1   
Copper_River_75019600120044       690         1   
Copper_River_75019600201125       691         1   
Copper_River_75019600169875       692         1   
Copper_River_75019600118106       693         1   
Copper_River_75019600128838       694         1   
Copper_River_75019600119982       695         1   
Copper_River_75019600143415       696         1   
Copper_River_75019600187749       697         1   
Copper_River_75019600164666       698         1   
Copper_River_75019600151382       699         1   
Copper_River_75019600199134       700         1   
Copper_River_75019600201378       701         1   
Copper_River_75019600187873       702         1   
Copper_River_75019600117650       703         1   
Copper_River_75019600187874       704         1   
Copper_River_75019600165863       705         1   
Copper_River_75019600157893       706         1   
Copper_River_75019600118255       707         1   
Copper_River_75019600179413       708         1   
Copper_River_75019600145695       709         1   
Copper_River_75019600118256       710         1   
Copper_River_75019600148826       711         1   


In [65]:
from collections import Counter
inhucs = os.path.join(outgdb,"AKSSF_awcHuc12s")
inwtds = os.path.join(outgdb,"AKSSF_awcHuc12_Watersheds_Merge")
wtdfields = [f.name  for f in arcpy.ListFields(inwtds)]
if 'HUC12' not in wtdfields:
    print (f'HUC12 field not present in {inwtds}')
    print (f'Joining HUC12 field to watershed merge feature class')
    arcpy.JoinField_management(inwtds,'cat_ID_con', cats_outlets,'cat_ID_con','HUC12')
else:
    print(f'HUC12 field present')
# Identify watershed that was created but did not have HUC12 identifier joined?
awcHucs = [r[0] for r in arcpy.da.SearchCursor(inhucs,'cat_ID_con')]
wtdHucs = [r[0] for r in arcpy.da.SearchCursor(inwtds,'cat_ID_con')]
c1 = Counter(awcHucs)
c2 = Counter(wtdHucs)
diff = Counter(c2)-Counter(c1)
print(len(awcHucs))
print(f'{len(wtdHucs) - len(awcHucs) }')
missingHucs = list(diff.elements())
print(missingHucs)
print(len(missingHucs))

HUC12 field present
1596
-858
[]
0


In [66]:
arcpy.env.workspace = outgdb
outlet_cats = arcpy.ListFeatureClasses("*cats_outlets", "POLYGON")
outlet_cats
outlet_cats_merge = os.path.join(outgdb, 'AKSSF_awcHuc12_outlet_cats_merge')
if not arcpy.Exists(outlet_cats_merge):
    print(f'Merging all Huc12 outlet catchments...')
    arcpy.Merge_management(outlet_cats, outlet_cats_merge, add_source=True)
    print(f'Joining HUC12 identifiers')
    arcpy.JoinField_management(outlet_cats_merge,'cat_ID_con', cats_outlets,'cat_ID_con','HUC12')

else:
    print(f'{outlet_cats_merge} dataset already exists')
print(f'Complete')

Merging all Huc12 outlet catchments...
Joining HUC12 identifiers
Complete


In [67]:
import arcpy
arcpy.env.overwriteOutput = True
#outgdb  = r'D:\\GIS\\AKSSF_awcHuc12_cv_Final\\AKSSF_awcHuc12_cv_Final.gdb'
outlet_cats = os.path.join(outgdb,r'AKSSF_awcHuc12_outlet_cats_merge')
wtds_merge = os.path.join(outgdb,r'AKSSF_awcHuc12_Watersheds_Merge')
catsFields = [f.name for f in arcpy.ListFields(outlet_cats)]
catsKeepFields = ['cat_ID_con','str_slope', 'str_slope_dg','str_ord']
wtdsFields = [f.name for f in arcpy.ListFields(wtds_merge)]
wtdsKeepFields = ['Shape_Area','HUC12']
print(catsFields)
print(f'\n{wtdsFields}')
fieldmappings = arcpy.FieldMappings()
fieldmappings.addTable(outlet_cats)
for field in fieldmappings.fields:
    if field.name not in catsKeepFields:
        fieldmappings.removeFieldMap(fieldmappings.findFieldMapIndex(field.name))
streamwtdtable = arcpy.TableToTable_conversion(outlet_cats,outgdb,'AKSSF_AwcHuc12_StrWtd_cv',None,fieldmappings)
arcpy.JoinField_management(streamwtdtable,'cat_ID_con',wtds_merge,'cat_ID_con',wtdsKeepFields)
arcpy.AddField_management(streamwtdtable,'wtd_AreaSqKm','DOUBLE','','','','Watershed Area Square Kilometers')
arcpy.AddField_management(streamwtdtable,'region','TEXT')
for field in arcpy.ListFields(streamwtdtable):
    print(field.name)
# Use update cursor to calculate region and wtd area
with arcpy.da.UpdateCursor(streamwtdtable,['cat_ID_con','region','Shape_Area','wtd_AreaSqKm']) as cur:
    for row in cur:
        region = row[0].rsplit('_',1)[::-1][1]
        areaSqkm = row[2]*1e-6
        print(f'{row[0]} will have region = {region} and shape area {row[2]} sq meters = {areaSqkm} sqKm')
        row[1] = region
        row[3] = areaSqkm
        cur.updateRow(row)
    del(row)
del(cur)

['OBJECTID', 'Shape', 'gridcode', 'catID', 'DSContArea', 'cat_ID_con', 'str_slope', 'str_ord', 'ds_dist_outlet_km', 'DSContArea_SqKM', 'str_slope_dg', 'MERGE_SRC', 'Shape_Length', 'Shape_Area', 'HUC12']

['OBJECTID', 'Shape', 'ORIG_FID', 'MERGE_SRC', 'cat_ID_con', 'cat_ID', 'cat_ID_txt', 'Shape_Length', 'Shape_Area', 'AwcHuc12_non_north_area', 'AwcHuc12_north_area', 'AwcHuc12_wtd_north_per', 'AwcHuc12_cat_elev_ZONE_CODE', 'AwcHuc12_cat_elev_COUNT', 'AwcHuc12_cat_elev_AREA', 'AwcHuc12_cat_elev_MIN', 'AwcHuc12_cat_elev_MAX', 'AwcHuc12_cat_elev_RANGE', 'AwcHuc12_cat_elev_MEAN', 'AwcHuc12_cat_elev_STD', 'AwcHuc12_cat_elev_SUM', 'AwcHuc12_cat_elev_VARIETY', 'AwcHuc12_cat_elev_MAJORITY', 'AwcHuc12_cat_elev_MINORITY', 'AwcHuc12_cat_elev_MEDIAN', 'AwcHuc12_cat_elev_PCT90', 'AwcHuc12_wtd_elev_MIN', 'AwcHuc12_wtd_elev_MAX', 'AwcHuc12_wtd_elev_MEAN', 'AwcHuc12_wtd_elev_STD', 'AwcHuc12_wtd_slope_MIN', 'AwcHuc12_wtd_slope_MAX', 'AwcHuc12_wtd_slope_MEAN', 'AwcHuc12_wtd_slope_STD', 'AwcHuc12_cat_slop

In [68]:
import pandas as pd
import numpy as np

#convert to df and check
final_df = pd.DataFrame()
final_fl = ['cat_ID_con','region','wtd_AreaSqKm','str_ord','str_slope','str_slope_dg','HUC12']
final_h12wtds_arr = arcpy.da.TableToNumPyArray(streamwtdtable, final_fl)
final_df = pd.DataFrame(final_h12wtds_arr)
final_df = final_df.set_index('cat_ID_con')
final_df


region  wtd_AreaSqKm  str_ord  str_slope  \
cat_ID_con                                                           
Bristol_Bay_1003859  Bristol_Bay     39.975900        4   0.000968   
Bristol_Bay_1004129  Bristol_Bay     45.335900        5   0.000000   
Bristol_Bay_1006858  Bristol_Bay     31.251900        4   0.011165   
Bristol_Bay_1007408  Bristol_Bay     42.596800        4   0.002892   
Bristol_Bay_1008168  Bristol_Bay     45.597900        4   0.001587   
Bristol_Bay_1008527  Bristol_Bay     69.569500        4   0.001807   
Bristol_Bay_1008597  Bristol_Bay    117.894900        5   0.000000   
Bristol_Bay_1013001  Bristol_Bay     48.755900        4   0.001430   
Bristol_Bay_1013111  Bristol_Bay     56.216600        4   0.002880   
Bristol_Bay_1013306  Bristol_Bay     99.641800        5   0.000000   
Bristol_Bay_1013765  Bristol_Bay     49.397900        4   0.001057   
Bristol_Bay_1014251  Bristol_Bay    142.753800        5   0.000000   
Bristol_Bay_1014341  Bristol_Bay    121.891400        4   0.004482   
Bristol_Bay_1014516  Bristol_Bay     60.913000        5   0.002617   
Bristol_Bay_1014641  Bristol_Bay    256.457100        6   0.001292   
Bristol_Bay_1014786  Bristol_Bay     81.889800        5   0.000582   
Bristol_Bay_1014821  Bristol_Bay   1649.300000        6   0.001353   
Bristol_Bay_1015186  Bristol_Bay    567.620400        5   0.000000   
Bristol_Bay_1015281  Bristol_Bay   1899.446000        6   0.001430   
Bristol_Bay_1015516  Bristol_Bay    729.142200        6   0.000331   
Bristol_Bay_1015685  Bristol_Bay    100.166700        5   0.007943   
Bristol_Bay_1015771  Bristol_Bay   2511.880600        7   0.000000   
Bristol_Bay_1015821  Bristol_Bay   7010.386300        8   0.000000   
Bristol_Bay_1016325  Bristol_Bay    351.941000        5   0.001909   
Bristol_Bay_1016515  Bristol_Bay     58.106400        4   0.000967   
Bristol_Bay_1016825  Bristol_Bay     70.351600        4   0.000502   
Bristol_Bay_1021823  Bristol_Bay     42.784700        3   0.000000   
Bristol_Bay_1021914  Bristol_Bay    132.157000        5   0.000000   
Bristol_Bay_1021984  Bristol_Bay    100.553300        5   0.000000   
Bristol_Bay_1022284  Bristol_Bay    217.601900        5   0.000000   
Bristol_Bay_1023034  Bristol_Bay   3257.846600        7   0.000000   
Bristol_Bay_1024403  Bristol_Bay     54.853000        4   0.004704   
Bristol_Bay_1025113  Bristol_Bay    121.344300        5   0.006646   
Bristol_Bay_1025432  Bristol_Bay     64.275600        3   0.001574   
Bristol_Bay_1025533  Bristol_Bay    131.318800        4   0.003893   
Bristol_Bay_1025683  Bristol_Bay    186.900700        5   0.002019   
Bristol_Bay_1025783  Bristol_Bay    118.423100        5   0.000000   
Bristol_Bay_1026233  Bristol_Bay    206.250500        5   0.001919   
Bristol_Bay_1026463  Bristol_Bay    270.027900        5   0.000000   
Bristol_Bay_1026613  Bristol_Bay    753.571600        6   0.003741   
Bristol_Bay_1026983  Bristol_Bay   3913.581300        7   0.000000   
Bristol_Bay_1027852  Bristol_Bay    118.273900        5   0.000747   
Bristol_Bay_1028122  Bristol_Bay     16.959600        3   0.006620   
Bristol_Bay_1028212  Bristol_Bay    146.477700        5   0.000000   
Bristol_Bay_1028322  Bristol_Bay    248.779000        5   0.004494   
Bristol_Bay_1029732  Bristol_Bay    338.185600        5   0.005084   
Bristol_Bay_1029872  Bristol_Bay    218.283400        5   0.002687   
Bristol_Bay_1030062  Bristol_Bay    177.066000        5   0.000000   
Bristol_Bay_1030462  Bristol_Bay     98.688100        4   0.000621   
Bristol_Bay_1030642  Bristol_Bay    193.110100        5   0.001051   
Bristol_Bay_1031022  Bristol_Bay   1445.600300        6   0.001938   
Bristol_Bay_2019230  Bristol_Bay    305.465000        6   0.000000   
Bristol_Bay_2019750  Bristol_Bay    402.363100        6   0.005069   
Bristol_Bay_2020120  Bristol_Bay    512.371500        6   0.000000   
Bristol_Bay_2040601  Bristol_Bay   1000.185400        7   0.003629   
Bristol_Bay_2041261  Bristol_Bay   1

In [69]:
# Export merged dataframe to csv
import os
#outdir = r"C:\Users\dwmerrigan\Documents\GitHub\AKSSF\data_preparation\sensitivity_drivers"
fin_csv_out = os.path.join(outdir,'AKSSF_AwcHuc12s_strwtd_cv.csv')
final_df.to_csv(fin_csv_out, encoding = 'utf-8')
print('Export all watershed and stream covariates dataframe to csv complete')


Export all watershed and stream covariates dataframe to csv complete
